In [ ]:
# Clean Up

In [ ]:
!pip install openai vec2text torch plotly scipy numpy umap-learn evaluate kaggle

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 225.4/225.4 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.7/82.7 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 90.9/90.9 kB 6.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 8.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 9.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 10.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 507.1/507.1 kB 12.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 403.3/403.3 kB 13.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 204.0/204.0 kB 13.5 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Installing backend dependencies ... done
  Preparing me

In [ ]:
import openai
import math
import torch
import enum
import numpy as np
from scipy import pi as PI
from scipy.stats import invgauss, norm, randint, uniform

def get_embeddings_openai(text_list, model="text-embedding-ada-002") -> torch.Tensor:
    client = openai.OpenAI()
    batches = math.ceil(len(text_list) / 128)
    outputs = []
    for batch in range(batches):
        text_list_batch = text_list[batch * 128 : (batch + 1) * 128]
        response = client.embeddings.create(
            input=text_list_batch,
            model=model,
            encoding_format="float",
        )
        outputs.extend([e.embedding for e in response.data])
    return torch.tensor(outputs)

def calculate_centroid(embeddings):
    """
    Calculate the centroid from a set of embeddings.

    Args:
    embeddings: The embeddings as torch.Tensor.

    Returns:
    torch.Tensor: The centroid as torch.Tensor.
    """
    # Calculate the centroid.
    centroid = embeddings.mean(dim=0)

    return centroid

def calculate_cone_height(embeddings_tensor, centroid, percentile=99):
    # Calculate the centered projections of the embedding vectors onto the centroid vector.
    centroid_norm = torch.norm(centroid)
    projections = torch.matmul(embeddings_tensor, centroid) / centroid_norm
    centered_projections = torch.abs(projections - centroid_norm)

    # Set cone height as the centered_projection at a desired percentile.
    cone_height = torch.quantile(centered_projections, percentile / 100.0)

    return cone_height

def calculate_cone_angle(embeddings_tensor, centroid, height, percentile=99):
    # Calculate angles between the embedding vectors and the vertex vector.
    vertex = centroid + height * centroid / torch.norm(centroid)
    embeddings_to_vertex = vertex - embeddings_tensor
    dot_products = torch.matmul(embeddings_to_vertex, vertex)
    norms = torch.norm(embeddings_to_vertex, dim=1) * torch.norm(vertex)
    cos_angles = dot_products / norms
    angles = torch.abs(torch.acos(cos_angles))  # Angles in radians.

    # Set the cone angle as the angle at a desired percentile.
    cone_angle = torch.quantile(torch.stack([angles, PI/2 - angles]), percentile / 100.0)

    return cone_angle


def sample_hypersphere(centroid, radius, m, n, distribution="uniform", use_gpu=False):
    """
    Samples m points within an n-dimensional hypersphere.

    Parameters:
    centroid (torch.Tensor): The centroid of the hypersphere, a vector of size n.
    radius (float): The radius of the hypersphere.
    m (int): The number of points to sample.
    n (int): The dimension of the space.
    distribution (str): The distribution to be sampled - "normal", "uniform", "inverse_normal", "surface"
    use_gpu (bool): Whether to use the GPU in calculating the samples or not.

    Returns:
    torch.Tensor: m points within the n-dimensional hypersphere.
    """
    assert distribution in ["uniform", "normal", "inverse_normal", "surface"]
    device = torch.device("cuda" if use_gpu and torch.cuda.is_available() else "cpu")
    centroid = centroid.to(device)
    # Generate m points from a Gaussian distribution
    points = torch.randn(m, n, device=device)

    if distribution == "normal":
      # Calculate the scaling factor to ensure all points are within the radius
      max_distance = points.norm(dim=1).max()
      scaling_factor = radius / max_distance

      # Scale the points
      points = points * scaling_factor

    elif distribution in ["uniform", "surface", "inverse_normal"]:
      # Normalize each point to lie on the surface of a unit hypersphere
      points = points / points.norm(dim=1, keepdim=True)

      # Scale points within the hypersphere (for UNIFORM mode)
      if distribution == "uniform":
          new_radii = torch.pow(torch.rand(m, 1), 1/n)
          points = points * new_radii

      if distribution == "inverse_normal":
        gaussian_noise = torch.abs(torch.randn(m, 1, device=device))
        decay_factor = torch.exp(-gaussian_noise**2 / 8)
        points = points * decay_factor

      # Scale by the radius
      points = points * radius

    # Center points at centroid
    points = points + centroid

    return points


RANDSIGN = randint(low=0, high=2)
UNIFORM = uniform(loc=0, scale=1)
NORMAL = norm(loc=0, scale=1)

def sample_from_spherical_cone(
    cone_centroid=(0,0,1), cone_angle=PI/3, cone_height=1,
    distribution="uniform",
    size=100000
):
    """
    Sample from a double spherical cone with the axis derived from the centroid norm.
    The cone centroid, angle, height, distribution and sample size are specifiable.
    """
    assert distribution in ["uniform", "normal", "inverse_normal"]
    n_dim = len(cone_centroid)

    direction = (2 * RANDSIGN.rvs(size=size) - 1)
    height = cone_height * UNIFORM.rvs(size=size)**(1/3) * direction
    if distribution == "uniform":
        radius = np.abs(height) * np.tan(cone_angle) * UNIFORM.rvs(size=size)**(1/2)
    elif distribution == "normal":
        rvs = NORMAL.ppf(UNIFORM.rvs(size=size)**(1/2))
        rvs /= rvs.max()
        radius = np.abs(height) * np.tan(cone_angle) * np.abs(rvs)
    elif distribution == "inverse_normal":
        rvs = invgauss.ppf(UNIFORM.rvs(size=size)**(1/2), 0.05)
        rvs /= rvs.max()
        radius = np.abs(height) * np.tan(cone_angle) * np.abs(rvs)

    # Sample points on an (n-1)-dimensional hypersphere
    sphere_points = np.random.normal(size=(size, n_dim-1))
    sphere_points /= np.linalg.norm(sphere_points, axis=1).reshape(-1, 1)

    # Scale points to within the radius
    scaled_points = sphere_points * radius.reshape(-1, 1)

    # Construct points by adding their final coordinates
    final_coord = height - direction * cone_height
    points = np.hstack([scaled_points, final_coord.reshape(-1, 1)])

    # Given unit cone axis
    cone_centroid_norm = cone_centroid / np.linalg.norm(cone_centroid)
    # Original unit cone axis (pointing up in the last dimension)
    original_axis = np.zeros(n_dim)
    original_axis[-1] = 1
    # Apply rotation if the original axis and given axis are not nearly parallel or antiparallel
    if not np.isclose(np.abs(np.dot(original_axis, cone_centroid_norm)), 1):
        print("rotating cone axis")
        u = original_axis.reshape(-1,1)
        v = cone_centroid_norm.reshape(-1,1)
        w = u + v
        w /= np.linalg.norm(w)
        r = np.identity(len(cone_centroid_norm)) + 2 * (v @ u.T - w @ w.T)
        points = points @ r.T

    # Translate all points to align the base of the cone with the centroid
    final_points = points + np.array(cone_centroid).reshape(1, -1)

    return final_points

In [ ]:
import plotly.graph_objects as go

def plot_full_distribution(space_embeddings_reduced, centroid_reduced, sampled_embeddings_reduced, provided_embeddings_reduced, centroid_text=None, sampled_text=None, provided_text=None):
    # Scatter plot for space embeddings
    space_scatter = go.Scatter3d(
        x=space_embeddings_reduced[:, 0],
        y=space_embeddings_reduced[:, 1],
        z=space_embeddings_reduced[:, 2],
        mode='markers',
        marker=dict(size=1, opacity=0.2),
        name='Space'
    )

    # Scatter plot for centroid
    centroid_scatter = go.Scatter3d(
        x=[centroid_reduced[0, 0]],
        y=[centroid_reduced[0, 1]],
        z=[centroid_reduced[0, 2]],
        mode='markers',
        marker=dict(color='red', size=5),
        text=[centroid_text] if centroid_text else None,
        hoverinfo='text' if centroid_text else None,
        name='Centroid'
    )

    # Scatter plot for sampled embeddings
    sampled_scatter = go.Scatter3d(
        x=sampled_embeddings_reduced[:, 0],
        y=sampled_embeddings_reduced[:, 1],
        z=sampled_embeddings_reduced[:, 2],
        mode='markers',
        marker=dict(color='blue', size=3, opacity=0.5),
        text=sampled_text,
        hoverinfo='text' if sampled_text else None,
        name='Sampled'
    )

    # Scatter plot for provided embeddings
    provided_scatter = go.Scatter3d(
        x=provided_embeddings_reduced[:, 0],
        y=provided_embeddings_reduced[:, 1],
        z=provided_embeddings_reduced[:, 2],
        mode='markers',
        marker=dict(color='green', size=3, opacity=0.8),
        text=provided_text,
        hoverinfo='text' if provided_text else None,
        name='Provided'
    )

    # Setting up the layout
    layout = go.Layout(
        scene=dict(
            xaxis_title="DIM1",
            yaxis_title="DIM2",
            zaxis_title="DIM3"
        ),
        margin=dict(r=0, b=0, l=0, t=0),  # Tight layout
        showlegend=True
    )

    # Creating the figure and adding the scatter plots
    fig = go.Figure(data=[space_scatter, centroid_scatter, sampled_scatter, provided_scatter], layout=layout)

    # Showing the figure
    fig.show()

In [ ]:
space = sample_from_spherical_cone(cone_angle=math.radians(20))

In [ ]:
plot_full_distribution(space, np.array([(0, 0, 1)]), np.array([(0, 1, 0)]), np.array([(1, 0, 0)]))

In [ ]:
# RUN IT

In [ ]:
import vec2text

inputs = [
  "First thing I'd suggest is getting the sleep you need or it will impact how you think and feel. I'd look at finding what is going well in your life and what you can be grateful for. I believe everyone has talents and wants to find their purpose in life. I think you can figure it out with some help.",
  "Therapy is essential for those that are feeling depressed and worthless. When I work with those that are experiencing concerns related to feeling of depression and issues with self esteem. I generally work with my client to help build coping skills to reduce level of depression and to assist with strengthening  self esteem, by guiding my client with CBT practices. CBT helps with gaining a better awareness of how your thought process influences your belief system, and how your beliefs impact your actions and the outcome of your behaviors.  This process isn’t easy but it helps teach an individual that we don’t always have control over what happens in our lives but we can control how we interpret, feel, and behave. CBT is good for individuals dealing with depression, anxiety, toxic relationships, stress, self esteem, codependency, etc.",
  "I first want to let you know that you are not alone in your feelings and there is always someone there to help. You can always change your feelings and change your way of thinking by being open to trying to change. You can always make yourself available to learning new things or volunteering so that you can make a purpose for yourself.",
  "Heck, sure thing, hun!Feelings of 'depression' have a deeply-rooted base in physical structures that may not be functioning very well at present; and, we can certainly turn them on again using means that you are able to find around the house and with relative ease :)After that, emotional and spiritual support will be liberally applied.",
  "You are exhibiting some specific traits of a particular temperament type. Seek out a counselor who provides NCCA temperament therapy and discover the joy of being you -- God loves you as you are!",
  "It sounds like you may be putting yourself last. You wrote that you want to fix your issues but never get around to it. I wonder how you are spending your mental and physical energy. Are you spending time taking care of and doing for others? I also wonder where the thoughts and feelings of being worthless are coming from - are you around people who treat you poorly or are hurtful? Or do you feel it is more of a worry you have but aren't really sure how others feel? It may be helpful to talk to someone about your feelings - a counselor perhaps - to clarify your feelings and move forward from se that are hurting you.",
  "It must be really difficult to experience what your going through right now.  It takes a lot of courage to reach out. It sounds like you want to get better, but perhaps need some help to get over the hump.  Many of the symptoms you have described are consistent with a person who is dealing with depression.   Depression is a treatable condition.  Typically, if these symptoms have persisted for more than two weeks, then it is a good idea to seek professional help.   Someone who is trained in dealing with depression.  Initially, a comprehensive assessment would be completed to rule out any other causes for your symptoms and to determine the exact nature of your presenting concern.  Then, in collaboration with one another, a tailored treatment plan would be developed, focusing on how to best help you reach your goals.  The good news is that their is hope for getting better! You don;t have to do it alone.  Allow me to be your ally in healing.",
  "People who feel worthless were, in one way or another, were told that they are worthless. This is the lie that they are living with. The work of therapy is to help people see their true good selves. This gives them self esteem.",
  "I'm sorry to hear you're feeling this intense emotion of worthlessness.  I'm glad to hear this has not reached the point of suicidal ideation; however, it does sounds like you could use some additional support right now.  I would recommend seeking out counseling to help you challenge the negative beliefs you have about yourself.  Although many types of therapy would be helpful, cognitive-behavioral therapy has been shown to be a good approach for this type of struggle.  A CBT therapist can help you identify your negative thoughts and beliefs, figure out the ways your thoughts are being distorted (for example, all-or-nothing thinking, or discounting the positives about yourself), and reframe your thoughts to be more positive.  You might also consider EMDR therapy, which helps the brain reprocess traumatic or distressing memories and helps you move forward with more positive beliefs about yourself.  Best wishes!",
  "It sounds like you may be struggling with depression. Depression can make you feel overwhelmed and paralyzed to change. I would suggest that you connect with a provider who can help you get to the root of where the worthlessness is coming from and help you develop a plan for recovery. In the meantime, small steps can go a long way. Self-care interventions such as journaling your feelings, mindfulness meditation, and regular exercise are all helpful to reconnecting with the present moment and gaining internal motivation. Focusing on one day at a time and bringing your thoughts back to the present can also be beneficial. There is hope!",
  "I'm glad you are interested in changing your feelings of worthlessness. Visiting your doctor is a great first step to address your lack of sleep. First, you want to make sure that you are physically healthy and that there isn't a physical condition causing your problem with sleep. Changing your feelings is something that is difficult to do, especially on your own. Make sure that you have someone you can trust and you can talk to about how you feel. This can be a friend or a family member. If you find that there isn't anyone you would feel comfortable talking to about this issue, find a therapist close to you who can help. One activity that people have found helpful in feeling better about themselves is keeping a gratitude journal. You can do this by journaling daily about the things that you are grateful for. There is no right or wrong way of doing this, as long as you focus your journal entries on the things you are grateful for in life."
]
embeddings = get_embeddings_openai(inputs)

In [ ]:
corrector = vec2text.load_corrector("text-embedding-ada-002")

config.json:   0%|          | 0.00/4.20k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.42G [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

...

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/t5/tokenization_t5_fast.py:160: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


config.json:   0%|          | 0.00/4.47k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.15G [00:00<?, ?B/s]

In [ ]:
centroid = calculate_centroid(embeddings)
shape = "cone"
assert shape in ["cone", "sphere"]

if shape == "sphere":
  print("Using hypersphere sampling")
  sampled_embeddings = sample_hypersphere(centroid, 0.2, 10, centroid.shape[1], 'uniform', use_gpu=False)
  space_embeddings = sample_hypersphere(centroid, 0.2, 10000, centroid.shape[1], 'uniform', use_gpu=False)
  inverted_embeddings = vec2text.invert_embeddings(
      embeddings=sampled_embeddings.cuda(),
      corrector=corrector,
      num_steps=3
  )
elif shape == "cone":
  print("Using double-cone sampling")
  cone_height = calculate_cone_height(embeddings.cuda(), centroid.cuda()).cpu().item()
  cone_angle = calculate_cone_angle(embeddings.cuda(), centroid.cuda(), torch.tensor([cone_height]).cuda(), 50).cpu().item()
  print(f"Cone angle: {cone_angle} radians ({math.degrees(cone_angle)} degrees)")
  print(f"Cone height: {cone_height}")
  sampled_embeddings = sample_from_spherical_cone(centroid.cpu().numpy(), cone_angle, cone_height, distribution='uniform', size= 10)
  space_embeddings = sample_from_spherical_cone(centroid.cpu().numpy(), cone_angle, cone_height, distribution='uniform', size= 10000)
  inverted_embeddings = vec2text.invert_embeddings(
     embeddings=torch.from_numpy(sampled_embeddings).float().cuda(),
     corrector=corrector,
     num_steps=3
  )

Using double-cone sampling
Cone angle: 0.7853981852531433 radians (45.00000125223908 degrees)
Cone height: 0.03207094967365265
rotating cone axis
rotating cone axis


In [ ]:
inverted_embeddings

['I think you are dealing with feelings of worthlessness. There are many types of therapists that can help you to change your mind and get better. The first thing you need to do is to explore what is affecting you. This can be done by talking with someone who is supportive of you and focusing on your self-worth. Good news is that depression is a natural trait for many people. They are willing to help you find a way to make positive changes in their lives, like regaining your confidence, regaining your health, and regaining your sleep.',
 "You are feeling a bit of a clumsy. I believe that there are ways to help you with your feelings of depression. The first thing to do is to seek out a therapist who can help you explore the negative aspects of your life. This can help you to change your thoughts about yourself and others. This can help you to rewrite your life into a more meaningful and meaningful one. I've found that even if you are not feeling well, you can still make a positive impa

In [ ]:
centroid_text = vec2text.invert_embeddings(embeddings=centroid.unsqueeze(0).cuda(),
                                           corrector=corrector,
                                           num_steps=30)

In [ ]:
centroid_text

["I believe you are feeling worthless. There are ways to help with these feelings. The first thing to do is to seek out a good therapist who can help you explore your own feelings of self-worth and make positive changes in your life. This kind of therapy can help you discover the nature of your feelings and what is affecting you emotionally, spiritually, and in some cases, even in your life. I'm glad you are now aware of the importance of kindness and love, and that you are a person who can do anything to get the kind of support you need."]

In [ ]:
import umap
# Combine all embeddings
all_embeddings = np.vstack([centroid, sampled_embeddings, embeddings.cpu().numpy(), space_embeddings])

# Perform umap to reduce dimensions to 3
reducer = umap.UMAP(n_neighbors=30, n_components=3, metric='euclidean')
all_embeddings_reduced = reducer.fit_transform(all_embeddings)

# Extract the reduced embeddings
centroid_reduced = all_embeddings_reduced[0:1, :]
sampled_embeddings_reduced = all_embeddings_reduced[1:1+len(sampled_embeddings), :]
provided_embeddings_reduced = all_embeddings_reduced[1+len(sampled_embeddings):1+len(sampled_embeddings)+len(embeddings.cpu().numpy()), :]
space_embeddings_reduced = all_embeddings_reduced[1+len(sampled_embeddings)+len(embeddings.cpu().numpy()):, :]

In [ ]:
# n_neighbors = 30
plot_full_distribution(space_embeddings_reduced, centroid_reduced, sampled_embeddings_reduced, provided_embeddings_reduced, centroid_text=centroid_text, sampled_text=inverted_embeddings, provided_text=inputs)

In [ ]:
# Play with params
cone_angle = math.radians(60)
cone_height = 0.08
sampled_embeddings = sample_from_spherical_cone(centroid.cpu().numpy(), cone_angle, cone_height, distribution='uniform', size= 10)
space_embeddings = sample_from_spherical_cone(centroid.cpu().numpy(), cone_angle, cone_height, distribution='uniform', size= 10000)
inverted_embeddings = vec2text.invert_embeddings(
     embeddings=torch.from_numpy(sampled_embeddings).float().cuda(),
     corrector=corrector,
     num_steps=3
  )

rotating cone axis
rotating cone axis


In [ ]:
inverted_embeddings

['You are probably feeling depressed. I would suggest that you seek help with feelings of worthlessness. There is a type of therapy that can help you make positive changes in your life. It is a habit that can help you to explore your inner self and work toward a better understanding of yourself and others. At the same time, you need to be able to focus on what you are doing and how you are doing it. As I have said, some individuals find that the first thing they do is to shut out their negative thoughts and feelings. Good luck!',
 "Most feelings are accompanied by feelings of worthlessness and depression. You might want to seek help by working with a therapist or counselor who can help you discover ways to change your self - that is, to focus on what you are doing right now, and to focus on what you aren't doing on a daily basis. I believe this is a good thing for you.",
 'You have to be able to refocus your thoughts on what is causing you to feel worthless. I would suggest seeking hel

In [ ]:
# Combine all embeddings
all_embeddings = np.vstack([centroid, sampled_embeddings, embeddings.cpu().numpy(), space_embeddings])

# Perform t-sne to reduce dimensions to 3
reducer = umap.UMAP(n_neighbors=30, n_components=3, metric='euclidean')
all_embeddings_reduced = reducer.fit_transform(all_embeddings)

# Extract the reduced embeddings
centroid_reduced = all_embeddings_reduced[0:1, :]
sampled_embeddings_reduced = all_embeddings_reduced[1:1+len(sampled_embeddings), :]
provided_embeddings_reduced = all_embeddings_reduced[1+len(sampled_embeddings):1+len(sampled_embeddings)+len(embeddings.cpu().numpy()), :]
space_embeddings_reduced = all_embeddings_reduced[1+len(sampled_embeddings)+len(embeddings.cpu().numpy()):, :]

In [ ]:
# n_neighbors = 30
plot_full_distribution(space_embeddings_reduced, centroid_reduced, sampled_embeddings_reduced, provided_embeddings_reduced, centroid_text=centroid_text, sampled_text=inverted_embeddings, provided_text=inputs)

In [ ]:
# ANALYSIS

In [ ]:
import locale
locale.getpreferredencoding = lambda *args: "UTF-8"

In [ ]:
# Download dataset from kaggle
from google.colab import files

# This will prompt you to upload the kaggle.json file
uploaded = files.upload()

# Ensure the kaggle.json file is in the current directory
!ls -lha kaggle.json

Saving kaggle.json to kaggle.json
-rw-r--r-- 1 root root 64 Dec 29 17:34 kaggle.json


In [ ]:
# Make a kaggle directory and move the json file there
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/

# Change the permission
!chmod 600 ~/.kaggle/kaggle.json

In [ ]:
!kaggle datasets download -d jpmiller/layoutlm

100% 8.16G/8.16G [06:55<00:00, 22.1MB/s]
100% 8.16G/8.16G [06:55<00:00, 21.1MB/s]


In [ ]:
!unzip \*.zip

Streaming output truncated to the last 5000 lines.
  inflating: medquad_xml/2_GARD_QA/0001106.xml  
  inflating: medquad_xml/2_GARD_QA/0001108.xml  
  inflating: medquad_xml/2_GARD_QA/0001109.xml  
  inflating: medquad_xml/2_GARD_QA/0001110.xml  
  inflating: medquad_xml/2_GARD_QA/0001111.xml  
  inflating: medquad_xml/2_GARD_QA/0001112.xml  
  inflating: medquad_xml/2_GARD_QA/0001116.xml  
  inflating: medquad_xml/2_GARD_QA/0001119.xml  
  inflating: medquad_xml/2_GARD_QA/0001126.xml  
  inflating: medquad_xml/2_GARD_QA/0001127.xml  
  inflating: medquad_xml/2_GARD_QA/0001130.xml  
  inflating: medquad_xml/2_GARD_QA/0001132.xml  
  inflating: medquad_xml/2_GARD_QA/0001133.xml  
  inflating: medquad_xml/2_GARD_QA/0001134.xml  
  inflating: medquad_xml/2_GARD_QA/0001135.xml  
  inflating: medquad_xml/2_GARD_QA/0001136.xml  
  inflating: medquad_xml/2_GARD_QA/0001137.xml  
  inflating: medquad_xml/2_GARD_QA/0001138.xml  
  inflating: medquad_xml/2_GARD_QA/0001142.xml  
  inflating: medqu

In [ ]:
def sample_synthetic_data_cone(references, corrector, num_samples, percentile=99, cone_height=None, cone_angle_degrees=None, distribution='uniform', num_steps=3, sequence_beam_width=2, angle_factor=1.0, height_factor=1.0, min_angle_degrees=None, min_height=None):
  assert distribution in ['uniform', 'normal', 'inverse_normal']

  embeddings = get_embeddings_openai(references)
  centroid = calculate_centroid(embeddings)

  if not cone_height:
    cone_height = calculate_cone_height(embeddings.cuda(), centroid.cuda(), percentile).cpu().item() * height_factor
  if not cone_angle_degrees or cone_angle_degrees > 90:
    cone_angle = calculate_cone_angle(embeddings.cuda(), centroid.cuda(), torch.tensor([cone_height]).cuda(), percentile).cpu().item()
    print(f'Original Cone Angle: {math.degrees(cone_angle)} degrees')
    cone_angle = cone_angle * angle_factor if cone_angle * angle_factor < math.radians(90) else math.radians(90)
    print(f'Transformed Cone Angle: {math.degrees(cone_angle)} degrees')
  if min_angle_degrees:
    cone_angle = max(cone_angle, math.radians(min_angle_degrees))
  if min_height:
    cone_height = max(cone_height, min_height)

  print(f"Cone angle: {cone_angle} radians ({math.degrees(cone_angle)} degrees)")
  print(f"Cone height: {cone_height}")
  sampled_embeddings = sample_from_spherical_cone(centroid.cpu().numpy(), cone_angle, cone_height, distribution=distribution, size=num_samples)
  inverted_embeddings = vec2text.invert_embeddings(
     embeddings=torch.from_numpy(sampled_embeddings).float().cuda(),
     corrector=corrector,
     num_steps=num_steps,
     sequence_beam_width=sequence_beam_width
  )
  return inverted_embeddings

In [ ]:
def calculate_metrics(generated_data, reference_data, bert_score, bleu):

    # Calculate Pairwise BERTScores
    max_bert_scores = []
    for gen_sentence in generated_data:
        sentence_scores = []
        for ref_sentence in reference_data:
            # Calculate BERTScore for each pair
            score = bert_score.compute(predictions=[gen_sentence], references=[ref_sentence], model_type='microsoft/deberta-xlarge-mnli')
            sentence_scores.append(max(score['f1']))  # F1 is typically a good overall performance measure

        # Find the max score for this generated sentence
        max_bert_scores.append(max(sentence_scores))

    # Calculate Self-BLEU
    self_bleu_scores = []
    for i, sentence in enumerate(generated_data):
        other_sentences = generated_data[:i] + generated_data[i+1:]
        score = bleu.compute(predictions=[sentence], references=[other_sentences])
        self_bleu_scores.append(score['bleu'])

    return {
        'max_bert_scores': max_bert_scores,  # List of max BERTScores for each generated sentence
        'self_bleu': self_bleu_scores  # Self-BLEU scores
    }

In [ ]:
# Load dataset as dataframe
import pandas as pd

df = pd.read_csv('medquad.csv')

In [ ]:
import pandas as pd
import torch
import numpy as np
import evaluate
import vec2text

# 1. Count the occurrences of each 'focus_area'
focus_area_counts = df['focus_area'].value_counts()

# 2. Filter the 'focus_area's to only those that occur more than once
focus_areas_with_multiple_rows = focus_area_counts[focus_area_counts > 1].index

# 3. Randomly sample 5 'focus_area's from those with more than one occurrence (or all if there are fewer than 5)
num_samples = min(len(focus_areas_with_multiple_rows), 5)
sampled_focus_areas = np.random.choice(focus_areas_with_multiple_rows, num_samples, replace=False)

# 4. Create a new DataFrame with the rows that match those sampled 'focus_area's
filtered_df = df[df['focus_area'].isin(sampled_focus_areas)]

# Initialize corrector
corrector = vec2text.load_corrector("text-embedding-ada-002")

# Load BERTScore metric
bert_score = evaluate.load('bertscore')

# Load BLEU metric
bleu = evaluate.load('bleu')

config.json:   0%|          | 0.00/4.20k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.42G [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

...

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/t5/tokenization_t5_fast.py:160: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-base automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  warnings.warn(


config.json:   0%|          | 0.00/4.47k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.15G [00:00<?, ?B/s]

In [ ]:
filtered_df

question  \
6285                    What is (are) GRACILE syndrome ?   
6286         What are the symptoms of GRACILE syndrome ?   
7614   What is (are) Craniometaphyseal dysplasia, aut...   
7615   What are the symptoms of Craniometaphyseal dys...   
7616   What causes Craniometaphyseal dysplasia, autos...   
7617   What are the treatments for Craniometaphyseal ...   
9106             What is (are) Fibromuscular Dysplasia ?   
9107   What are the treatments for Fibromuscular Dysp...   
9108   What is the outlook for Fibromuscular Dysplasia ?   
9109   what research (or clinical trials) is being do...   
9835   What is (are) infantile-onset spinocerebellar ...   
9836   How many people are affected by infantile-onse...   
9837   What are the genetic changes related to infant...   
9838   Is infantile-onset spinocerebellar ataxia inhe...   
9839   What are the treatments for infantile-onset sp...   
10580                   What is (are) GRACILE syndrome ?   
10581  How many people are affected by GRACILE syndro...   
10582  What are the genetic changes related to GRACIL...   
10583                    Is GRACILE syndrome inherited ?   
10584     What are the treatments for GRACILE syndrome ?   
14595   What is (are) LAMA2-related muscular dystrophy ?   
14596  How many people are affected by LAMA2-related ...   
14597  What are the genetic changes related to LAMA2-...   
14598    Is LAMA2-related muscular dystrophy inherited ?   
14599  What are the treatments for LAMA2-related musc...   

                                                  answer source  \
6285   GRACILE syndrome is an inherited metabolic dis...   GARD   
6286   What are the signs and symptoms of GRACILE syn...   GARD   
7614   Autosomal recessive craniometaphyseal dysplasi...   GARD   
7615   What are the signs and symptoms of Craniometap...   GARD   
7616   What causes autosomal recessive craniometaphys...   GARD   
7617   How might craniometaphyseal dysplasia be treat...   GARD   
9106   Fibromuscular dysplasia (FMD) is the abnormal ...  NINDS   
9107   There is no standard protocol to treat FMD. An...  NINDS   
9108   Currently there is no cure for FMD. Medicines ...  NINDS   
9109   The National Institute of Neurological Disorde...  NINDS   
9835   Infantile-onset spinocerebellar ataxia (IOSCA)...    GHR   
9836   More than 20 individuals with IOSCA have been ...    GHR   
9837   Mutations in the C10orf2 gene cause IOSCA. The...    GHR   
9838   This condition is inherited in an autosomal re...    GHR   
9839   These resources address the diagnosis or manag...    GHR   
10580  GRACILE syndrome is a severe disorder that beg...    GHR   
10581  GRACILE syndrome is found almost exclusively i...    GHR   
10582  GRACILE syndrome is caused by a mutation in th...    GHR   
10583  This condition is inherited in an autosomal re...    GHR   
10584  These resources address the diagnosis or manag...    GHR   
14595  LAMA2-related muscular dystrophy is a disorder...    GHR   
14596  The prevalence of early-onset LAMA2-related mu...    GHR   
14597  As its name suggests, LAMA2-related muscular d...    GHR   
14598  This condition is inherited in an autosomal re...    GHR   
14599  These resources address the diagnosis or manag...    GHR   

                                              focus_area  
6285                                    GRACILE syndrome  
6286                                    GRACILE syndrome  
7614   Craniometaphyseal dysplasia, autosomal recessi...  
7615   Craniometaphyseal dysplasia, autosomal recessi...  
7616   Craniometaphyseal dysplasia, autosomal recessi...  
7617   Craniometaphyseal dysplasia, autosomal recessi...  
9106                             Fibromuscular Dysplasia  
9107                             Fibromuscular Dysplasia  
9108                             Fibromuscular Dysplasia  
9109                             Fibromuscular Dysplasia  
9835              infantile-onset spinocerebellar ataxia  
9836              infantile-onset sp

In [ ]:
# Initialize storage for results
results = []

for focus_area in sampled_focus_areas:
    sub_df = filtered_df[filtered_df['focus_area'] == focus_area]

    # Generate 10 synthetic examples for 'question' and 'answer'
    for column in ['question', 'answer']:
        print(f"Generating synthetic data ({focus_area} + {column})")
        real_data = sub_df[column].tolist()
        synthetic_data = sample_synthetic_data_cone(real_data, corrector, 10, num_steps=30, sequence_beam_width=3, height_factor=1.5, angle_factor=1.2, distribution='inverse_normal')

        # Score synthetic examples using BERTScore and Self-BLEU
        print(f"Calculating metrics ({focus_area} + {column})")
        metrics = calculate_metrics(synthetic_data, real_data, bert_score, bleu)

        # Store results
        results.append({
            'focus_area': focus_area,
            'column': column,
            'metrics': metrics,
            'real_data': real_data,
            'synthetic_data': synthetic_data
        })

Generating synthetic data (Fibromuscular Dysplasia + question)
Original Cone Angle: 89.5975950793377 degrees
Transformed Cone Angle: 89.5975950793377 degrees
Cone angle: 1.5637730360031128 radians (89.5975950793377 degrees)
Cone height: 0.003638664144091308
rotating cone axis
Calculating metrics (Fibromuscular Dysplasia + question)


tokenizer_config.json:   0%|          | 0.00/52.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/792 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/3.04G [00:00<?, ?B/s]

Generating synthetic data (Fibromuscular Dysplasia + answer)
Original Cone Angle: 80.05197541232717 degrees
Transformed Cone Angle: 80.05197541232717 degrees
Cone angle: 1.3971705436706543 radians (80.05197541232717 degrees)
Cone height: 0.0686772633343935
rotating cone axis
Calculating metrics (Fibromuscular Dysplasia + answer)
Generating synthetic data (Craniometaphyseal dysplasia, autosomal recessive type + question)
Original Cone Angle: 88.99224224338863 degrees
Transformed Cone Angle: 88.99224224338863 degrees
Cone angle: 1.5532076358795166 radians (88.99224224338863 degrees)
Cone height: 0.006050216965377331
rotating cone axis
Calculating metrics (Craniometaphyseal dysplasia, autosomal recessive type + question)
Generating synthetic data (Craniometaphyseal dysplasia, autosomal recessive type + answer)
Original Cone Angle: 87.70594003775682 degrees
Transformed Cone Angle: 87.70594003775682 degrees
Cone angle: 1.5307574272155762 radians (87.70594003775682 degrees)
Cone height: 0.02

In [ ]:
results

[{'focus_area': 'Fibromuscular Dysplasia',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.7257352471351624,
    0.8888832330703735,
    0.46173712611198425,
    0.8221412897109985,
    0.747003436088562,
    0.9000228643417358,
    0.8734928369522095,
    0.6434082388877869,
    0.9175307154655457,
    0.8438653349876404],
   'self_bleu': [0.6340466277046861,
    0.9457416090031758,
    0.06884322566267259,
    0.5410822690539396,
    0.0,
    0.691441569283882,
    0.7016879391277371,
    0.0,
    0.8408964152537145,
    0.0]},
  'real_data': ['What is (are) Fibromuscular Dysplasia ?',
   'What are the treatments for Fibromuscular Dysplasia ?',
   'What is the outlook for Fibromuscular Dysplasia ?',
   'what research (or clinical trials) is being done for Fibromuscular Dysplasia ?'],
  'synthetic_data': ['What is the research on Fibromuscular Dysplasia ( fibromuscular dysplasia )?',
   'What is the research on Fibromuscular Dysplasia?',
   "What is a grant ( ) for Fibromu

In [ ]:
# In case the env dies halfway

results = [{'focus_area': 'Pseudopelade of Brocq',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8517076969146729,
    0.8646624088287354,
    0.5227058529853821,
    0.8417725563049316,
    0.877738893032074,
    0.5812272429466248,
    0.553707480430603,
    0.7167820930480957,
    0.8080316781997681,
    0.4613971710205078],
   'self_bleu': [0.6434588841607617,
    0.8408964152537146,
    0.0,
    0.5946035575013605,
    0.7952707287670506,
    0.0,
    0.0,
    0.5348259312838877,
    0.5019724248795793,
    0.6434588841607617]},
  'real_data': ['What is (are) Pseudopelade of Brocq ?',
   'What are the symptoms of Pseudopelade of Brocq ?',
   'What are the treatments for Pseudopelade of Brocq ?'],
  'synthetic_data': ['What are the symptoms of Pseudo-Brodacque?',
   'What are the symptoms of Pseudo-Brodaek?',
   'What is a P  Broderick? (P  Broderick )??????????????????????????????????????????????? Symptoms of p  Broderick ',
   'What are the treatments of Pseudo-Brodaque?',
   'What are the symptoms of Pseudo-Brodaque?',
   "What are pseudopseudopseudopseudopse? Broda's pseudopseudopse?",
   'What are the pseudopseudopseudopseudopse (Pseudo-Broda) of Broda?',
   'What are the symptoms of Pseudo-Brodaek ( of Brodaek )?',
   'What are the treatments for Pseudo-Brodaque of Peloponnese?',
   'What are the treatments for pseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudop?']},
 {'focus_area': 'Pseudopelade of Brocq',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5197083353996277,
    0.6337071657180786,
    0.623412549495697,
    0.6448864340782166,
    0.5930875539779663,
    0.5347109436988831,
    0.6435707807540894,
    0.5578061938285828,
    0.6463408470153809,
    0.6638810634613037],
   'self_bleu': [0.14332814788092085,
    0.2439647475805835,
    0.34490693895761865,
    0.5141093682873723,
    0.3692682194012276,
    0.0,
    0.4363235858329489,
    0.24389967604506255,
    0.35870150972657755,
    0.5003895657661542]},
  'real_data': ['Pseudopelade of Brocq (PBB) is a slowly progressive, chronic condition characterized by scarring hair loss (cicatricial alopecia). There exists some controversy as to whether PBB is a distinct condition or the common final stage or variant of several different forms of scarring alopecias such as discoid lupus erythematosus (DLE) or lichen planopilaris (LPP). Some have suggested abandoning the use of the term pseudopelade of Brocq while others think that the term should be strictly used to describe patients that follow the pattern of hair loss described by Brocq et al.(i.e., multiple, small, discrete, asymmetrical, smooth, soft, flesh-colored or white patches of hair loss with little, if any, inflammation). Although the exact cause of PBB has not been identified, it is believed to be an autoimmune disease. Some individuals with PBB have been found to have Borrelia burgdorferi, the bacterium that causes Lyme disease.  Neither an effective treatment nor cure is currently available.',
   'What are the signs and symptoms of Pseudopelade of Brocq? The Human Phenotype Ontology provides the following list of signs and symptoms for Pseudopelade of Brocq. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Alopecia 90% Hypertrichosis 90% Lichenification 90% Skin ulcer 50% Abnormality of the nail 7.5% Aplasia/Hypoplasia of the eyebrow 7.5% Cheilitis 7.5% The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.',
   "Is there treatment or a cure for pseudopelade of Brocq? Neither an effective treatment nor cure has been identified for pseudopelade of Brocq.  Unfortunately, even when treatment relieves the symptoms and signs, the progression of hair loss may continue. The choice of treatment prescribed varies from person to person and depends mainly on the activity, extent of the disease and patient's tolerance to the treatment. Various forms of corticosteroids have been tried, including injections or skin lotions or creams. Surgery such as hair transplant or scalp reduction might be considered in patients whose condition has remained stable for two or more years."],
  'synthetic_data': ['Pseudopseudopseudopse of Broddecourt is often diagnosed on the basis of a combination of signs and symptoms. There is no cure for Pseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudops.',
   "Brodd's of Pepine is a progressive disease with a number of signs and symptoms. No cure, diagnosis or treatment has been found for Brodd's of Pepine. The frequency, severity and duration of the first sign or symptom of Brodd's of Pepine vary from person to person. When the symptom or symptom is not met, the patient may have a slough, a hair loss or a hair loss recurrence. As with all life forms, the term'short-acting' is used",
   'No cure has been found for Pseudoplasia Brod cle. The diagnosis of Pseudoplasia Brod cle is based on the frequency of hair loss, a symptom, or a combination of these. The frequency of hair loss varies widely between people with Pseudoplasia Brod cle and their proximate causes. The frequency of these symptoms is usually less than 1% of the population. The best treatment for these symptoms is a long-term, conservative approach.',
   'Pseudoplasia of Brod le-Pric is a symptomatic disease. Neither a cure nor treatment has been found for the condition. The frequency of the signs and symptoms of Pseudoplasia of Brod le-Pric is often determined by the frequency of hair loss, as well as the severity of the disease. When hair loss is first seen, the patient may have a small number of hair follicles on the scalp. Occasionally, the hair removal and/or balding',
   "Treatment of Pseudo-Broca's is a matter of identifying the cause of the condition. The symptom or signs of Pseudo-Broca's include hair loss, baldness, and alopecia. The frequency of hair loss in Pseudo-Broca's is unknown, but the frequency of hair loss in patients with the disease is estimated to be between 0 and 50%. The symptom or signs of Pseudo-Broca's are derived from the patient population. The most recent statistics",
   'Not a cure for P.C. Brodel which is a symptom of P.C. Brodel (as a symptom of underlying malignant hyperplasia of the facial hair) on the femtosecond scale. P.C. Brodel is a symptom of P.C. Brodel (as a symptom of underlying malignant hyperplasia of the facial hair) on the femtosecond scale. The femtosecond scale is usually triggered by the loss of hair growth and',
   'Pseudoplasia of Broca-Peyron is classified as either a symptom or a sign. No definitive treatment for Pseudoplasia of Broca-Peyron is available. The frequency of hair loss in people with Pseudoplasia of Broca-Peyron is unknown. The frequency of hair loss in patients with the disease is based on the frequency of hair loss over a period of time. Several different drugs, including oral steroids, are used to treat the condition.',
   'Pseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopseudopse. 1 Currently, there is no definitive way to diagnose the symptom of Brodd-Croche-Pelau disease. When the symptoms are a combination of hair loss and scalp inflammation, the treatment is often effective, but the frequency of the symptoms is often',
   'Pseudoplasia of Brode-Ple has been listed as a symptomatic condition, but there is no cure for this disease. The frequency of the signs and symptoms of Pseudoplasia of Brode-Ple is often variable, depending on the severity of the disease. The first few years of life have been spent on topical, topical, or oral treatments. The patient profile for the presence of hair loss on the scalp is based on the number of patients with this condition and the frequency.',
   'Pseudoplasia of Broddell is a symptomatic alopecia. Neither a cure nor treatment has been found for Pseudoplasia of Broddell. The frequency of hair loss or baldness in people with Pseudoplasia of Broddell depends on the severity of the disease. The following list of signs and symptoms is based on the most recent available data. Patients with Pseudoplasia of Broddell disease are often treated with oral steroids, or']},
 {'focus_area': 'beta-ureidopropionase deficiency',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8377676606178284,
    0.7594513893127441,
    0.7601557374000549,
    0.7665237188339233,
    0.7990161776542664,
    0.7659611105918884,
    0.8332484364509583,
    0.806885302066803,
    0.7876442074775696,
    0.7787838578224182],
   'self_bleu': [0.5133450480401704,
    0.0,
    0.0,
    0.0,
    0.0,
    0.0,
    0.5946035575013605,
    0.0,
    0.0,
    0.0]},
  'real_data': ['What is (are) beta-ureidopropionase deficiency ?',
   'How many people are affected by beta-ureidopropionase deficiency ?',
   'What are the genetic changes related to beta-ureidopropionase deficiency ?',
   'Is beta-ureidopropionase deficiency inherited ?',
   'What are the treatments for beta-ureidopropionase deficiency ?'],
  'synthetic_data': ['What are the symptoms of a beta-uropoidae deficiency?',
   'Are beta-acid-reductase deficiency?',
   'What are beta-uropropyl urea deficiency?',
   'What are beta-adjusted uropeptidase deficiency?',
   'What causes beta-uropeptide deficiency??',
   'What are the beta-urease propionyltransferase mutations in beta-urease deficiency?',
   'What are the symptoms of beta-uropoietin deficiency?',
   'What is beta-urea deficiency??',
   'What are beta-uroprene deficiency?',
   'What are beta-ergosterol deficiency?']},
 {'focus_area': 'beta-ureidopropionase deficiency',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6737594604492188,
    0.6016917824745178,
    0.6288230419158936,
    0.6380169987678528,
    0.6325699090957642,
    0.6259456872940063,
    0.6265247464179993,
    0.4611862003803253,
    0.56666499376297,
    0.6257383823394775],
   'self_bleu': [0.27859695725825123,
    0.0,
    0.1258090924974416,
    0.0,
    0.21778375552789994,
    0.21769897651788855,
    0.32763737671113496,
    0.0,
    0.0,
    0.0]},
  'real_data': ['Beta-ureidopropionase deficiency is a disorder that causes excessive amounts of molecules called N-carbamyl-beta-aminoisobutyric acid and N-carbamyl-beta-alanine to be released in the urine. Neurological problems ranging from mild to severe also occur in some affected individuals.  People with beta-ureidopropionase deficiency can have low muscle tone (hypotonia), seizures, speech difficulties, developmental delay, intellectual disability, and autistic behaviors that affect communication and social interaction. Some people with this condition have an abnormally small head size (microcephaly); they may also have brain abnormalities that can be seen with medical imaging. Deterioration of the optic nerve, which carries visual information from the eyes to the brain, can lead to vision loss in this condition.  In some people with beta-ureidopropionase deficiency, the disease causes no neurological problems and can only be diagnosed by laboratory testing.',
   'The prevalence of beta-ureidopropionase deficiency is unknown. A small number of affected individuals from populations around the world have been described in the medical literature. In Japan, the prevalence of beta-ureidopropionase deficiency has been estimated as 1 in 6,000 people. Researchers suggest that in many affected individuals with absent or mild neurological problems, the condition may never be diagnosed.',
   'Beta-ureidopropionase deficiency is caused by mutations in the UPB1 gene, which provides instructions for making an enzyme called beta-ureidopropionase. This enzyme is involved in the breakdown of molecules called pyrimidines, which are building blocks of DNA and its chemical cousin RNA.  The beta-ureidopropionase enzyme is involved in the last step of the process that breaks down pyrimidines. This step converts N-carbamyl-beta-aminoisobutyric acid to beta-aminoisobutyric acid and also breaks down N-carbamyl-beta-alanine to beta-alanine, ammonia, and carbon dioxide. Both beta-aminoisobutyric acid and beta-alanine are thought to play roles in the nervous system. Beta-aminoisobutyric acid increases the production of a protein called leptin, which has been found to help protect brain cells from damage caused by toxins, inflammation, and other factors. Research suggests that beta-alanine is involved in sending signals between nerve cells (synaptic transmission) and in controlling the level of a chemical messenger (neurotransmitter) called dopamine.  UPB1 gene mutations can reduce or eliminate beta-ureidopropionase enzyme activity. Loss of this enzyme function reduces the production of beta-aminoisobutyric acid and beta-alanine, and leads to an excess of their precursor molecules, N-carbamyl-beta-aminoisobutyric acid and N-carbamyl-beta-alanine, which are released in the urine. Reduced production of beta-aminoisobutyric acid and beta-alanine may impair the function of these molecules in the nervous system, leading to neurological problems in some people with beta-ureidopropionase deficiency. The extent of the reduction in enzyme activity caused by a particular UPB1 gene mutation, along with other genetic and environmental factors, may determine whether people with beta-ureidopropionase deficiency develop neurological problems and the severity of these problems.',
   'This condition is inherited in an autosomal recessive pattern, which means both copies of the gene in each cell have mutations. The parents of an individual with an autosomal recessive condition each carry one copy of the mutated gene, but they typically do not show signs and symptoms of the condition.',
   'These resources address the diagnosis or management of beta-ureidopropionase deficiency:  - Genetic Testing Registry: Deficiency of beta-ureidopropionase   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care'],
  'synthetic_data': ['People with beta-ureopropionidase deficiency are affected by genetic mutations in the beta-ureopropionidase gene. Although the amount of beta-ureopropionidase in each cell is unknown, it is estimated that up to 1 in 200 births leads to a deficiency in this enzyme.  The disorder causes a decreased neuronal development.  The following resources provide information on symptoms, diagnosis, and treatment for people with beta-ureopropionidase deficiency.',
   ' Beta-ureopyridinosidase deficiency is present in a number of people with this condition.  A gene that encodes for the enzyme beta-ureopyridinosidase decreases in the brain and spinal cord.  Typically, one copy of each chromosome is inherited from each parent.  Deficiencies in beta-ureopyridinosidase are not considered diagnostic or treatment for this condition.  Medications are used to treat symptoms and disorders of the',
   '- A deficiency in the beta-ureopyridine prodrug is present in 1 in every 2 individuals who are carriers of this genetic condition. The deficiency results in decreased production of beta-ureopyridine prodrug and a decrease in the amount of beta-ureopyridine in the brain. There are also symptoms that can be transmitted from parents to children. These symptoms are often accompanied by neurological and behavioral problems. The beta-ureopyridine prodrug mutation is the only known genetic mutation that can be detected by laboratory tests.',
   '- There is a beta guanine ureadylation deficiency in both parents, although the exact cause of this condition is unknown. People with beta guanine ureadylation deficiency, a condition that affects 1 in every 3 to 5 people, develop a number of neurological disorders, including impaired brain function, speech, and other physical problems. - Click here to view a full profile of the disease.',
   'The beta-adenosine urease deficiency is diagnosed through a gene mutation in the beta-adenosine urease-reducting protein. This resource provides detailed information about the genetic and clinical conditions that are often associated with beta-adenosine urease deficiency.  Up to 1 million people in the U.S. have a defective copy of this gene.  Inbred parents rarely develop symptoms of this condition.  Inbred children may develop neurological symptoms, such as seizures, in their brains.',
   'Researchers have shown that 1 in every 2 individuals with this condition is deficient in beta-uroproteoside reductase, a gene that is responsible for the formation of amides. The following resources are available to help diagnose the genetic disorder beta-uroproteoside deficiency: 1 Autosomal recessive mutations in the beta-uroproteoside reductase gene may cause symptoms of the condition. 2 Abnormalities in the brain, nerves, or ovaries may also be a problem.',
   'The protamine-releasing enzymes in beta-uridine deficiency are inherited.  Each person with this condition has a mutation in the beta-uridine-1,5-diphosphate-reductase gene.  Although the condition is rare, it is estimated that up to 200,000 people in the U.S. have a deficiency of this enzyme.  Genetics and prognosis of beta-uridine deficiency are still unknown.  Treatment of the condition depends on the presence of symptoms and the presence of symptoms',
   'Disease Causes -  A family with a                                                          ',
   'It is possible to develop beta-urease deficiency if the beta-urease gene is deficient, since this gene causes the formation of beta-ureases, which affect the brain and nervous system.  2,000 pages on this wiki.                                  .',
   'This resource describes beta-uropropionate deficiency.  Mutations in the enzyme, beta-uropropionate reductase, cause the condition.  In the brain, the amount of beta-uropropionate produced by the enzyme is decreased.  About 1 in every 10,000 individuals with beta-uropropionate deficiency have a genetically determined defect in their genes.  Genetic testing of affected individuals may be helpful in diagnosing the condition.  Health care professionals may use genetic testing to diagnose the condition.']},
 {'focus_area': 'Dominant dystrophic epidermolysis bullosa',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.9059355854988098,
    0.9078015089035034,
    0.9638068675994873,
    0.8732091784477234,
    0.9897457361221313,
    0.8475498557090759,
    0.7748718857765198,
    0.9500013589859009,
    0.8282085657119751,
    0.9001288414001465],
   'self_bleu': [0.6434588841607617,
    0.6389431042462724,
    0.7952707287670506,
    0.9306048591020996,
    0.9621954581957615,
    0.5081327481546147,
    0.0,
    0.6756000774035172,
    0.0,
    0.6147881529512643]},
  'real_data': ['What is (are) Dominant dystrophic epidermolysis bullosa ?',
   'What are the symptoms of Dominant dystrophic epidermolysis bullosa ?',
   'What causes Dominant dystrophic epidermolysis bullosa ?',
   'Is Dominant dystrophic epidermolysis bullosa inherited ?',
   'What are the treatments for Dominant dystrophic epidermolysis bullosa ?'],
  'synthetic_data': ['What is dominant dystrophic epidermolysis bullosa?',
   'What are the symptoms of Dominant bullous dystrophy epidermolysis?',
   'What causes dominant dystrophic epidermolysis bullosa?',
   'What are dominant dystrophic epidermolysis bullosa?',
   'What are the symptoms of Dominant dystrophic epidermolysis bullosa?',
   'What are dominant dystrophic bullosa epidermolysis?',
   'What are dominant eczema symptoms of bullous dystrophy?',
   'What are the causes of Dominant dystrophic epidermolysis bullosa?',
   'What causes dominant bullous dystrophy?',
   'Treatments for dominant dystrophic epidermolysis bullosa?']},
 {'focus_area': 'Dominant dystrophic epidermolysis bullosa',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6426330804824829,
    0.6805079579353333,
    0.47571122646331787,
    0.6060139536857605,
    0.6100024580955505,
    0.6055914759635925,
    0.6182761788368225,
    0.6018184423446655,
    0.6358416080474854,
    0.6428076028823853],
   'self_bleu': [0.26577845104093245,
    0.39987640358857557,
    0.0,
    0.18170989986450084,
    0.19489500109513028,
    0.1842473899748513,
    0.3354535383097168,
    0.19776346906604822,
    0.3348093152851821,
    0.40731987351259136]},
  'real_data': ['Dominant dystrophic epidermolysis bullosa (DDEB) is a type of epidermolysis bullosa (EB), which is a group of rare inherited conditions in which the skin blisters extremely easily. DDEB is one of the milder forms of EB, although the severity is variable. Blisters may be present at birth, but typically appear during early childhood; occasionally they do not develop until later in life. Blisters often become more numerous and tend to occur over vulnerable sites such as knees, ankles, elbows and knuckles. In adulthood, they usually become less frequent and scars fade. Other signs and symptoms of DDEB may include dystrophic or absent nails, constipation, dental caries and swallowing problems. It is caused by mutations in the COL7A1 gene and is inherited in an autosomal dominant manner. Treatment typically includes treating blisters and avoiding infection.',
   'What are the signs and symptoms of Dominant dystrophic epidermolysis bullosa? Dominant dystrophic epidermolysis bullosa (DDEB) is consivered to be a more mild form of dystrophic epidermolysis bullosa (DEB). Blistering is often limited to the hands, feet, knees, and elbows. Blistering may be relatively benign, but still heals with scarring and milia. Dystrophic nails, especially toenails, are common and loss of nails may occur. In the mildest forms, dystrophic nails may be the only characteristic noted. Blistering in DDEB often improves somewhat with age. The Human Phenotype Ontology provides the following list of signs and symptoms for Dominant dystrophic epidermolysis bullosa. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Abnormal blistering of the skin 90% Abnormality of the fingernails 90% Abnormality of the toenails 90% Cheilitis 90% Carious teeth 50% Hypopigmented skin patches 50% Abnormal renal physiology 7.5% Abnormality of the urethra 7.5% Anemia 7.5% Corneal erosion 7.5% Feeding difficulties in infancy 7.5% Tracheoesophageal fistula 7.5% Atrophic scars - Autosomal dominant inheritance - Congenital onset - Milia - Nail dysplasia - Nail dystrophy - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.',
   'What causes dominant dystrophic epidermolysis bullosa? Dominant dystrophic epidermolysis bullosa (DDEB) is caused by mutations in the COL7A1 gene. The COL7A1 gene provides instructions for making a protein that is used to assemble type VII collagen. Collagen gives structure and strength to connective tissues, such as skin, tendons, and ligaments, throughout the body. Type VII collagen plays an important role in strengthening and stabilizing the skin. It is the main component of structures called anchoring fibrils, which anchor the top layer of skin, called the epidermis, to an underlying layer called the dermis. COL7A1 mutations alter the structure or disrupt the production of type VII collagen, which impairs its ability to help connect the epidermis to the dermis. When type VII collagen is abnormal or missing, friction or other minor trauma can cause the two skin layers to separate. This separation leads to the formation of blisters, which can cause extensive scarring as they heal. A diagram of the skin structure including the area of skin implicated in DDEB is provided by the National Institute of Arthritis and Musculoskeletal and Skin Diseases. Click on the link for more.',
   'How is dominant dystrophic epidermolysis bullosa inherited? Dominant dystrophic epidermolysis bullosa (DDEB) has an autosomal dominant pattern of inheritance. Autosomal dominant inheritance means that one copy of the gene with the mutation in each cell is sufficient to cause the disorder. About 70 percent of individuals with DDEB have inherited a COL7A1 mutation from an affected parent. The remaining 30 percent have the condition as a result of a new (de novo) mutation in the COL7A1 gene. These cases occur in people with no history of the disorder in their family. Regardless of whether an individual with an autosomal dominant condition has inherited the mutation or has a new mutation, each child of the affected individual has a 50% (1 in 2) chance of also having the condition, and a 50% chance of not having the condition.',
   'How might dominant dystrophic epidermolysis bullosa be treated? There is currently no cure for all types of dystrophic epidermolysis bullosa (DEB). Treatment generally focuses on managing signs and symptoms. For some individuals, such as those that have a mild form of dominant dystrophic epidermolysis bullosa (DDEB), dystrophic nails may be the only manifestation. However, other individuals may have much more severe problems that need to be managed. Management typically focuses on treating blisters and avoiding or treating infections. Wound care usually included treatment of new blisters by lancing and draining. Additionally in most cases, wounds are then dressed with a non-adherent material, covered with padding for stability and protection, and secured with an elastic wrap for integrity. Due to the increased risk of bacterial resistance, topical antibiotic ointments and antimicrobial dressings should be reserved for those wounds that are colonized with bacteria and fail to heal, referred to as critical colonization." Individuals with epidermolysis bullosa (EB) have increased caloric and protein needs due to the increased energy utilized in wound healing. Involvement of the digestive system in some forms of EB may limit nutritional intake. Infants and children with more severe forms of EB and failure to thrive usually require attention to fluid and electrolyte balance and may require nutritional support, including a gastrotomy feeding tube. Anemia is typically treated with iron supplements and transfusions as needed. Other nutritional supplements may include calcium, vitamin D, selenium, carnitine, and zinc. Surveillance is important for individuals with DEB. Biopsies of abnormal-appearing wounds that do not heal may be recommended in some types of DEB due to predisposition to squamous cell carcinoma, beginning in the second decade of life. Screening for deficiencies of iron, zinc, vitamin D, selenium, and carnitine is typically recommended after the first year of life. Routine echocardiograms are recommended to identify dilated cardiomyopathy, and bone mineral density studies are recommended to identify osteoporosis. Activities and bandages that may traumatize the skin (including all adhesives) should typically be avoided. Recent treatment advancements and therapies under investigation include but are not limited to:  Use of biological dressings to treat chronic or recurrent skin ulcers Bone marrow transplantation Intra-dermal (in the skin) injection of fibroblasts Protein replacement therapy (intra-dermal injection of type VII collagen)  Gene therapy Revertant mosaicism Gene correction technologies (ex. CRISPR) DEBRA International has developed clinical practice guidelines for different aspects of treating EB including wound care and pain management. Click on the link to see their completed guidelines.'],
  'synthetic_data': ['Dominant degenerative epidermolysis bullosa (DDEB) is a form of epidermal degeneration. In infants with DDEB, the epidermal degeneration is dominant and only a few blisters or scars occur. Treatment of DDEB is usually based on the type of epidermal degeneration that is present. The genes on the first line of inheritance (chromosome 7) are not used to cause DDEB. 2 People with DDEB may have a more severe form of the disease. 3 Symptoms are usually mild',
   'Dominant degenerative epidermolysis bullosa is a type of degenerative epidermolysis bullosa (DDEB). The dominant inheritance of the dominant gene is usually found in 7 to 10 percent of individuals with the condition. The dominant inheritance is also responsible for the presence of scars on the skin, nails, and other areas of the body. The symptoms of DDEB are usually mild and normal, but can be more severe and more severe. Treatments include antibiotics, a sclerotherapy, and a combination of both.',
   'A common cause of deuteranoblastoma is a â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. â. A different form of the condition, known as severe cutaneous',
   'Epidermolysis bullosa is also the type of epidermolysis bullosa that is caused by the presence of the Ddb7 gene, which is responsible for the protective coating of the skin and nails. The Ddb7 gene does not normally provide all the necessary antibodies to fight infection. How is this condition inherited? In rare cases, individuals with dominant inheritance of the disease may have symptoms and signs of the disease, including: Frequent and severe blistering of the joints, tendons, and skin, and a slow, progressive onset of the disease.',
   'How is dermatomyositis bullosa treated? Dominant epidermal dystrophy means that an individual inherits a mutation in the DBE gene (type 7). A mutation in the DBE gene causes skin blisters and may cause scarring. A form of DBE is rare in infants, but is more common in adults. A form of DBE is more common in children. A form of DBE is less common in people with a family history of the condition. The following list of conditions and symptoms may be relevant to diagnosis and treatment of DBE, including',
   'Degenerative blisters of the ebb (DBD) are typically mediated by the formation of a particular type of cytokine, ephemerin VII, or other cytokine. When DBD is a dominant disease, it is not the same as other forms of eczema. Other causes of DBD include infection, trauma, and autoimmune diseases. What are the typical clinical signs and symptoms of DBD? The formation of blisters on the skin and other areas of the body is characterized by a rash, a swolle',
   'Dominant epidermal dystrophy is a type of degenerative epidermal dystrophy that is caused by a recessive inheritance of the DEB7 gene. Treatments for DEB7 may include a protective barrier to prevent the formation of blisters and scars, and a protective barrier to prevent the formation of scars and scars. How does this condition affect individuals with the dominant gene? In infants and young adults, the usual signs and symptoms of degenerative epidermal dystrophy (DED) are mild and do not usually occur. The condition is rarely',
   'How is deuteranoblastoma dominant to deuteranoblastoma epidermis (DBE) caused by mutations in the DL7A1 gene? Type of blistering: Normal blisters are usually asymptomatic. It is not common for children to have blisters in the eyes, limbs, or other areas of the body. Treatments for the condition include: In general, the following signs and symptoms may be present in a parent with deuteranoblastoma epidermis dominant to deuteranoblastoma.',
   'How is dermatomyositis bullosa dominant (DEB) inherited? Dermatomyositis bullosa dominant is a type of epidermal cell disease that causes blistering and scarring of the epidermis. The condition is usually inherited on chromosome seven. The symptoms of DEB are mild and not severe. Treatment of DEB is based on the type of epidermal cell disease. 1 Acute cases of DEB are rare in adults, but more than half of healthy people will develop the condition. 2 More information',
   'How is dermatomyositis bullosa dominant (DEB)? Dermatomyositis bullosa is a type of degenerative epidermal disease with characteristic blistering and peeling of the skin. The condition is caused by a mutation in the DEB7 gene. The DEB7 gene is found only in about 1 in 100 individuals. The condition is more common in infants and young children. Treatments may include lifestyle changes, antibiotics, and a protective coating. Severe forms of DEB do not cause symptoms. The protective coating']},
 {'focus_area': 'Spondyloepiphyseal dysplasia Maroteaux type',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.5150538682937622,
    0.8683017492294312,
    0.6113351583480835,
    0.9257032871246338,
    0.8140791058540344,
    0.8328750133514404,
    0.7366099953651428,
    0.8461275696754456,
    0.8776949048042297,
    0.8334336280822754],
   'self_bleu': [0.4417918226831577,
    0.7016879391277371,
    0.0,
    0.7348889200874658,
    0.6580370064762462,
    0.7016879391277371,
    0.22374677077485577,
    0.42969435238201475,
    0.5462757644646491,
    0.7016879391277371]},
  'real_data': ['What is (are) Spondyloepiphyseal dysplasia Maroteaux type ?',
   'What are the symptoms of Spondyloepiphyseal dysplasia Maroteaux type ?'],
  'synthetic_data': ['What are the symptoms of MartelâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâSpahrâ type type 1?',
   'What are the symptoms of spondylophyseal dysplasia ( type )?',
   'What are symptoms of Spondylophyte-Martel type ( )? Spondylophyte-Martel type ( )? Ligament dysplasias, ectopic growths, spondylophyte-martel type?',
   'What are the symptoms of Spondylo-Epiphyseal dysplasia (Marquette type )?',
   'What are the symptoms of Martel-Spondylodactyly ( type )?',
   'What are the symptoms of Martel-Sponge dysplasia ( type )?',
   "What are the symptoms of Martel's Syndrome (Spondyloarthropathy ),Type C,Disordered,Insufficiency,Possible )?",
   'What are the symptoms of Martel-Spondylophyseal Dysplasia (Type )?',
   'What is Spondyloepiphyseal dysplasia ( Marquette type )?',
   'What are the symptoms of Martel-Sporaeus dysplasia (type )?']},
 {'focus_area': 'Spondyloepiphyseal dysplasia Maroteaux type',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5790408849716187,
    0.6154370307922363,
    0.6148262023925781,
    0.6157312989234924,
    0.614241361618042,
    0.5693058967590332,
    0.5204030871391296,
    0.623347282409668,
    0.6049796938896179,
    0.6165685653686523],
   'self_bleu': [0.3793697085737269,
    0.2146751207726034,
    0.18915672932690555,
    0.3017733322939706,
    0.17362672888887787,
    0.1950383497418115,
    0.0,
    0.31620074377638474,
    0.4385593408440598,
    0.4554242161408062]},
  'real_data': ['Spondyloepiphyseal dysplasia (SED) Maroteaux type is a rare skeletal dysplasia that is characterized by short stature beginning in infancy, short, stubby hands and feet, and genu valgum (knock knees). In addition to these physical characteristics, individuals with SED Maroteaux type have some common radiographic findings, including platyspondyly (flattened vertebral bodies in the spine), abnormalities of the pelvis and severe brachydactyly (short fingers and toes). Intelligence is generally normal and there is no clouding of the cornea, which distinguishes SED Maroteaux type from other forms of spondyloepiphyseal dysplasia. SED Maroteaux type is caused by mutations in the TRPV4 gene and is inherited any an autosomal dominant fashion.',
   'What are the signs and symptoms of Spondyloepiphyseal dysplasia Maroteaux type? The Human Phenotype Ontology provides the following list of signs and symptoms for Spondyloepiphyseal dysplasia Maroteaux type. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Abnormality of the eye - Autosomal dominant inheritance - Genu valgum - Platyspondyly - Spondyloepiphyseal dysplasia - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.'],
  'synthetic_data': ['Spondylodendrosis type is a rare phenotype of Martel-Hauves syndrome. The following table lists the signs and symptoms of Spondylodendrosis type based on the frequency of mutations in the MARTEX gene. The frequency of mutations in the MARTEX gene is listed as the number of times the mutation occurs in humans. The normal phenotype for Spondylodendrosis type is normal, but the symptoms may include short stature, slenderness, and unsteadiness',
   'The following signs and symptoms of Spondylodysplasia type are common in individuals with the MDPES gene: The appearance of a squamous or spherical distal phalanx of the hand. The number of signs and symptoms of Spondylodysplasia type is a statistic calculated from the data of the Human Genome Project (HGP). This statistic is based on the average frequency of these symptoms in the past 30 years. It is not a measure of how often the disease is diagnosed or treated.',
   'Symptoms of Spondylode type MARE are characterized by a distal phalanx, a normal or very normal bone density, and a tendency to have a spondylode (femoral) dislocation. This is a very rare form of spondylode dysplasia. The following table lists the symptoms, signs, and causes of Spondylode type MARE. The information provided below is based on the answers to the common questions asked by people with Spondylode.',
   'What does spondylodactyly type mean in the MEDOSPHERE gene? The frequency of the signs and symptoms of spondylodactyly type, based on the frequency of the spondylodactyly type mutation, is given in the table below. It is a rare inherited condition and is usually found in the elderly. Other symptoms and signs may include a spondylodactyly type skeletal abnormalities, such as a shortening of the tendons, or a.',
   'The following symptoms and signs are common to Spondylodendrosis type (MARPTYLE): Displacement of bones of the forearm or scapula; Short stature; Normal or baldness of the hands and feet; This is a phenotype of a rare genetic disorder. The frequency of these symptoms and signs in patients with Spondylodendrosis type (MARPTYLE) is 0.4 [source: etiology.org] How many people have this phenotype and how many have it?',
   'Spondylodea type is a phenotype when signs and symptoms of MARTEX syndrome (short stature, scoliosis of the skeletal muscles, or spondylodea type) occur. The symptom frequency for MARTEX syndrome (short stature, spondylodea type) is listed in the table below. The occurrence of MARTEX syndrome (short stature, spondylodea type) is very rare in humans. Only about 1 in 100 individuals develop',
   'Orthopedic Spondylodactyly. PARTICULAR: Autosomal recessive. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. PARTICULAR: Other. The following are some of the symptoms and signs that appear on the first light microscope, which is seen',
   'Signs and symptoms of Spondyloepiphyseal dysplasia type are described in the following table. The MEDATEO phenotype of Spondyloepiphyseal dysplasia type is a rare, inherited trait. It is characterized by a disturbance of the proximal limbs, which may be normal or abnormal. The frequency of these symptoms is listed as a number from 1 to 255 in people with this type of phenotype. The frequency of these symptoms is listed as.',
   'Spondyloepiphyseal dysplasia type is a phenotype with the following signs and symptoms. The table below shows the frequency of the signs and symptoms of MARDOTE type. The number of occurrences of the signs and symptoms is based on the number of chromosomes (k) that are inherited from the parent. When a person has a rare inherited trait, it is usually referred to as a rare spondyloepiphyseal dysplasia type. These are not',
   'Spondyloepiphyseal dysplasia type is a phenotype of the following signs and symptoms. The table below lists the signs and symptoms of Spondyloepiphyseal dysplasia type based on the frequency of the mutation in the MARDOTE gene. When a person has the MARDOTE gene, the frequency is normal or very rare. When a person has the MARDOTE gene, the frequency is normal or very rare. This information is not available for all patients with this condition. For more']},
 {'focus_area': 'prekallikrein deficiency',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.3886294960975647,
    0.8043399453163147,
    0.7064435482025146,
    0.7139703035354614,
    0.4632355868816376,
    0.731267511844635,
    0.751414954662323,
    0.8951848149299622,
    0.8873321413993835,
    0.8951848149299622],
   'self_bleu': [0.0,
    0.0,
    0.0,
    0.0,
    0.0,
    0.0,
    0.5081327481546147,
    1.0,
    0.0,
    1.0]},
  'real_data': ['What is (are) prekallikrein deficiency ?',
   'How many people are affected by prekallikrein deficiency ?',
   'What are the genetic changes related to prekallikrein deficiency ?',
   'Is prekallikrein deficiency inherited ?',
   'What are the treatments for prekallikrein deficiency ?'],
  'synthetic_data': ['About                                                          What is preklinrere',
   'What are prekreidal kallikreinase deficiency?',
   'How many prekilik mutations are there in prekilik deficiency?',
   'About prekrein-kallikrein deficiency?',
   'What are the causes of pre-Kreidle deficiency? ( Is this related to a alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine alanine )',
   '1 What are prekreid deficiency ( kallikreid deficiency )?',
   '0 Reactions are prekallikrein deficiency?',
   'What are prekallikrein deficiency?',
   'How many prekallikrein deficiency are affected?',
   'What are prekallikrein deficiency?']},
 {'focus_area': 'prekallikrein deficiency',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6247490644454956,
    0.6549994349479675,
    0.6246501207351685,
    0.67923504114151,
    0.6613290905952454,
    0.6334922909736633,
    0.5981073975563049,
    0.6555027365684509,
    0.661774218082428,
    0.589979350566864],
   'self_bleu': [0.20473883844957852,
    0.0,
    0.18106657444569724,
    0.2777391141508571,
    0.3115922981034718,
    0.3042728322258449,
    0.14880454673886712,
    0.44260018058576023,
    0.44245933876542154,
    0.0]},
  'real_data': ['Prekallikrein deficiency is a blood condition that usually causes no health problems. In people with this condition, blood tests show a prolonged activated partial thromboplastin time (PTT), a result that is typically associated with bleeding problems; however, bleeding problems generally do not occur in prekallikrein deficiency. The condition is usually discovered when blood tests are done for other reasons.  A few people with prekallikrein deficiency have experienced health problems related to blood clotting such as heart attack, stroke, a clot in the deep veins of the arms or legs (deep vein thrombosis), nosebleeds, or excessive bleeding after surgery. However, these are common problems in the general population, and most affected individuals have other risk factors for developing them, so it is unclear whether their occurrence is related to prekallikrein deficiency.',
   'The prevalence of prekallikrein deficiency is unknown. Approximately 80 affected individuals in about 30 families have been described in the medical literature. Because prekallikrein deficiency usually does not cause any symptoms, researchers suspect that most people with the condition are never diagnosed.',
   'Prekallikrein deficiency is caused by mutations in the KLKB1 gene, which provides instructions for making a protein called prekallikrein. This protein, when converted to an active form called plasma kallikrein in the blood, is involved in the early stages of blood clotting. Plasma kallikrein plays a role in a process called the intrinsic coagulation pathway (also called the contact activation pathway). This pathway turns on (activates) proteins that are needed later in the clotting process. Blood clots protect the body after an injury by sealing off damaged blood vessels and preventing further blood loss.  The KLKB1 gene mutations that cause prekallikrein deficiency reduce or eliminate functional plasma kallikrein, which likely impairs the intrinsic coagulation pathway. Researchers suggest that this lack (deficiency) of functional plasma kallikrein protein does not generally cause any symptoms because another process called the extrinsic coagulation pathway (also known as the tissue factor pathway) can compensate for the impaired intrinsic coagulation pathway.',
   'This condition is inherited in an autosomal recessive pattern, which means both copies of the gene in each cell have mutations. The parents of an individual with an autosomal recessive condition each carry one copy of the mutated gene, but they typically do not show signs and symptoms of the condition.',
   'These resources address the diagnosis or management of prekallikrein deficiency:  - Genetic Testing Registry: Prekallikrein deficiency  - Massachusetts General Hospital Laboratory Handbook: Prekallikrein   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care'],
  'synthetic_data': ['Preklinckiasis is inherited in an autosomal recessive way. This means that most people with preklinckiasis have no symptoms and do not develop the condition. However, the amount of preklinckiasis-related protein deficiency varies among individuals.  A National Library of Medicine resource that summarizes blood tests and related conditions for Preklinckiasis. These tests may be useful in determining the cause of preklinckiasis, as well as the treatment options.',
   'About preklinin deficiency. Preklinin deficiency is diagnosed in each family. The condition is characterized by a recessive form of preklinin deficiency.  Most people with preklinin deficiency do not have any symptoms, and the condition is usually inherited.  Blood tests, such as a complete blood count (CBC), show that the defective gene causes a number of health problems.  Preklinin deficiency may increase the risk of death or other medical problems.',
   ' Prekernal cell death syndrome is a rare condition.  Prekernal cell death syndrome is inherited in about 200,000 people.  Prekernal cell death syndrome is usually a result of a deficiency of a protein that plays an important role in coagulation.  Prekernal cell death syndrome is characterized by an impaired function of this enzyme.  Prekernal cell death syndrome causes no symptoms.  The following resources provide a general overview of prekernal cell death syndrome:  Blood tests and laboratory tests',
   'Prekaryotin deficiency is a condition referred to in the National Institutes of Health.  About 1 in 20 people with prekaryotin deficiency inherit an autosomal recessive gene mutation.  Both parents usually have this condition, but the affected family members do not develop any symptoms.  Blood tests can diagnose prekaryotin deficiency and guide treatment.  Because the causes of prekaryotin deficiency are unknown, they are often not considered a cause of symptoms.',
   'About 1 in 20 people with this condition develop a preklinckjakrein deficiency. Because the preklinckjakrein gene is usually inherited in an autosomal recessive form, it does not cause symptoms and there are no known treatments for the deficiency. Pathology tests that can be performed on blood samples from affected patients include: Precursors to the abnormal activity of the enzyme that plays a role in the breakdown of proteins.',
   '1 People with a deficiency in this gene are carriers of the preklintal gene, which plays a role in the formation and activity of the preklintal protein. Despite the presence of preklintal deficiency, the condition usually does not cause symptoms and is inherited in an autosomal recessive manner. About 30 health and medical literature online are available for patients with preklintal deficiency...',
   'A preregulatory karyotype deficiency is present in all families with the condition and is estimated to cause symptoms in approximately 1 to 20 percent of individuals with the condition. These defects usually do not cause symptoms and may lead to a lifetime of severe aplastic anemia. Blood tests and body mass index (BMI) tests can be used to help diagnose preregulatory karyotype deficiency. Blood tests and body mass index (BMI) tests can be used to help diagnose preregulatory karyotype deficiency.',
   'Prekrebsial kinase deficiency is inherited in an autosomal recessive pattern. This means that about 1 in 20 people with prekrebsial kinase deficiency develop the condition. Although these genes cause prekrebsial kinase deficiency, they usually do not cause symptoms. The following resources provide a detailed overview of prekrebsial kinase deficiency and its diagnosis.  Blood tests are available for diagnosis and treatment.',
   'This condition is inherited in an autosomal recessive pattern. About 1 in 20 people with preklintal kaempferol deficiency have a deficiency of the gene that controls the activity of the preklintal kaempferol reductase enzyme. Because the deficiency usually causes no symptoms, these individuals usually do not develop any symptoms. Blood tests and other health resources are available to help doctors diagnose and treat the various causes of preklintal kaempferol deficiency.',
   'This condition is diagnosed in all patients with a pre-Prekaknijl deficiency. : Pre-Prekaknijl deficiency is thought to be due to a change in the nature of the repressors. It can also be a feature of normal aging. The most-discussed form of pre-Prekaknijl deficiency occurs in individuals of a nationality.']},
 {'focus_area': 'autoimmune Addison disease',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.7115777730941772,
    0.8335317373275757,
    0.8456239700317383,
    0.7390498518943787,
    0.8762408494949341,
    0.8456239700317383,
    0.8456239700317383,
    0.8456239700317383,
    0.9553018808364868,
    0.7711388468742371],
   'self_bleu': [0.0,
    0.34329452398451965,
    1.0,
    0.4347208719449915,
    0.8694417438899827,
    1.0,
    1.0,
    1.0,
    0.0,
    0.37817904276524744]},
  'real_data': ['What is (are) autoimmune Addison disease ?',
   'How many people are affected by autoimmune Addison disease ?',
   'What are the genetic changes related to autoimmune Addison disease ?',
   'Is autoimmune Addison disease inherited ?',
   'What are the treatments for autoimmune Addison disease ?'],
  'synthetic_data': ['How many Addisons are autoimmune?',
   'What are the autoimmune diseases related to Addison-Crisp disease?',
   'What are autoimmune changes in Addison disease?',
   'Many autoimmune alterations in Addison disease?',
   'What are the autoimmune changes in Addison disease?',
   'What are autoimmune changes in Addison disease?',
   'What are autoimmune changes in Addison disease?',
   'What are autoimmune changes in Addison disease?',
   'How many are affected by autoimmune Addison disease?',
   'What are the auto immune autoimmune diseases in Addison disease?']},
 {'focus_area': 'autoimmune Addison disease',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5891343951225281,
    0.5776731967926025,
    0.6178075671195984,
    0.6363760232925415,
    0.6007586121559143,
    0.6461317539215088,
    0.6370275616645813,
    0.5703664422035217,
    0.5611467957496643,
    0.6418173313140869],
   'self_bleu': [0.14269729300142844,
    0.25425902529127237,
    0.4046665087820204,
    0.33671602286184316,
    0.38447799946354017,
    0.41054988075974524,
    0.2686927622272801,
    0.2161330931339373,
    0.13712814863233272,
    0.24216197442996695]},
  'real_data': ['Autoimmune Addison disease affects the function of the adrenal glands, which are small hormone-producing glands located on top of each kidney. It is classified as an autoimmune disorder because it results from a malfunctioning immune system that attacks the adrenal glands. As a result, the production of several hormones is disrupted, which affects many body systems.  The signs and symptoms of autoimmune Addison disease can begin at any time, although they most commonly begin between ages 30 and 50. Common features of this condition include extreme tiredness (fatigue), nausea, decreased appetite, and weight loss. In addition, many affected individuals have low blood pressure (hypotension), which can lead to dizziness when standing up quickly; muscle cramps; and a craving for salty foods. A characteristic feature of autoimmune Addison disease is abnormally dark areas of skin (hyperpigmentation), especially in regions that experience a lot of friction, such as the armpits, elbows, knuckles, and palm creases. The lips and the inside lining of the mouth can also be unusually dark. Because of an imbalance of hormones involved in development of sexual characteristics, women with this condition may lose their underarm and pubic hair.  Other signs and symptoms of autoimmune Addison disease include low levels of sugar (hypoglycemia) and sodium (hyponatremia) and high levels of potassium (hyperkalemia) in the blood. Affected individuals may also have a shortage of red blood cells (anemia) and an increase in the number of white blood cells (lymphocytosis), particularly those known as eosinophils (eosinophilia).  Autoimmune Addison disease can lead to a life-threatening adrenal crisis, characterized by vomiting, abdominal pain, back or leg cramps, and severe hypotension leading to shock. The adrenal crisis is often triggered by a stressor, such as surgery, trauma, or infection.  Individuals with autoimmune Addison disease or their family members often have another autoimmune disorder, most commonly autoimmune thyroid disease or type 1 diabetes.',
   'Addison disease affects approximately 11 to 14 in 100,000 people of European descent. The autoimmune form of the disorder is the most common form in developed countries, accounting for up to 90 percent of cases.',
   "The cause of autoimmune Addison disease is complex and not completely understood. A combination of environmental and genetic factors plays a role in the disorder, and changes in multiple genes are thought to affect the risk of developing the condition.  The genes that have been associated with autoimmune Addison disease participate in the body's immune response. The most commonly associated genes belong to a family of genes called the human leukocyte antigen (HLA) complex. The HLA complex helps the immune system distinguish the body's own proteins from proteins made by foreign invaders (such as viruses and bacteria). Each HLA gene has many different normal variations, allowing each person's immune system to react to a wide range of foreign proteins. The most well-known risk factor for autoimmune Addison disease is a variant of the HLA-DRB1 gene called HLA-DRB1*04:04. This and other disease-associated HLA gene variants likely contribute to an inappropriate immune response that leads to autoimmune Addison disease, although the mechanism is unknown.  Normally, the immune system responds only to proteins made by foreign invaders, not to the body's own proteins. In autoimmune Addison disease, however, an immune response is triggered by a normal adrenal gland protein, typically a protein called 21-hydroxylase. This protein plays a key role in producing certain hormones in the adrenal glands. The prolonged immune attack triggered by 21-hydroxylase damages the adrenal glands (specifically the outer layers of the glands known, collectively, as the adrenal cortex), preventing hormone production. A shortage of adrenal hormones (adrenal insufficiency) disrupts several normal functions in the body, leading to hypoglycemia, hyponatremia, hypotension, muscle cramps, skin hyperpigmentation and other features of autoimmune Addison disease.  Rarely, Addison disease is not caused by an autoimmune reaction. Other causes include infections that damage the adrenal glands, such as tuberculosis, or tumors in the adrenal glands. Addison disease can also be one of several features of other genetic conditions, including X-linked adrenoleukodystrophy and autoimmune polyglandular syndrome, type 1, which are caused by mutations in other genes.",
   'A predisposition to develop autoimmune Addison disease is passed through generations in families, but the inheritance pattern is unknown.',
   "These resources address the diagnosis or management of autoimmune Addison disease:  - Genetic Testing Registry: Addison's disease  - MedlinePlus Encyclopedia: Addison's Disease   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care"],
  'synthetic_data': ['The Addison autoimmune disorder affects about 20% of patients with Addison disease, but the exact cause is unknown. Autoimmune disorders include adrenal inflammation, which is characterized by a lack of immune response to injury or disease. Autoimmune disorders develop when the adrenal glands are damaged. The Addison -H gene is a circulating gene. The Addison -H gene is a circulating gene. The Addison -H gene is not recognized in the United States. To learn more about the development of Addison disease, see the Complete Guide',
   " Addison's disease is a autoimmune disorder. However, the exact role of autoimmune factors in the development of the disease is unknown.  Most people with Addison's disease do not suffer from a predisposition to autoimmune disease.  Risk factors include a mutation in one or more genes or a mutation in a gene.  Risk factors include a mutation in a gene or a mutation in a gene.  Addison's disease is diagnosed on a monthly basis.  Addison's disease.",
   'Autoimmune Addison disease is diagnosed by a medical professional, but the risk of developing the disorder is unknown. Addison disease affects an estimated 1 in 20,000 people. The genes that cause Addison disease are thought to play a role in the development of the adrenal gland and the progression of the disease. For more information, see the Addison disease resources page.  Genetic and ethnic variations in disease.  Diseases that affect the immune system.  Diseases that affect the nervous system.',
   "Autoimmune Addison disease is diagnosed on a national basis. The risk of developing Addison disease is unknown. Experts are not familiar with the relationship between genes and the development of Addison disease. The genes control the production of adrenocorticotropic hormones, which affect the body's endocrine and reproductive systems. The pages below provide general information about Addison disease. Symptoms of Addison disease vary from person to person.  Pregnancy.",
   'Autoimmune Addison disease is diagnosed by testing for autoimmune disorders. The cause of Addison disease is unknown, but the disease is thought to be a genetic disorder. The genes that regulate the immune system, including the hippocampus, play a role in autoimmune development. Addison disease affects about 1 in every 100,000 people. The prevalence of Addison disease varies from region to region.  References.  References.  References.  References.  References.  References.',
   'Autoimmune Addison disease is diagnosed by autoimmune testing. The exact genes that play a role in the development of Addison disease are unknown. The disease affects about 10 million people, but the incidence is increasing. The risk of developing Addison disease varies from ethnicity to ethnicity. The disease is passed down from one generation to the next. The signs and symptoms of Addison disease are related to an abnormality in the adrenal glands, a disorder of the endocrine system, or a combination of these. For more information, see: 1 Treatment. 2',
   "Autoimmune Addison disease develops as a response to a deficiency in the genes that regulate the immune system, but the causes of this disorder are unknown. The disease affects approximately 1 in 100,000 people. Additional information on the genetics, pathophysiology, and clinical features of Addison's disease is available from the: Prednisone gland.",
   "Autoimmune Addison disease is a widespread condition, but the genes that cause Addison's disease are unknown. The genes affect both the immune system and the endocrine system. Addison's disease occurs in about 1 in 10 people. The following online resources provide a diagnosis of Addison's disease: 1 Risk factors for developing Addison's disease. 2 Risk factors for developing Addison's disease. 3 Risk factors for developing Addison's disease. 4 Risk factors for developing Addison's disease. 5 Risk factors for developing.",
   "The development of Addison's disease is asymptomatic, but it is common to develop autoimmune disorders. Autoimmune disease is affected by mutations in the gene that controls the production and function of the immune response. The following information is taken from the National Institute of Health and the European Medicine Network:  1 - 2 of 21 people with Addison's disease (source: CDC)  3 - 4 of 21 people with Addison's disease (source: CDC)  5 - 6 of 21 people with Addison's disease.",
   'Autoimmune Addison disease is diagnosed by a family history of the disorder, but most of the risk factors are unknown. The disease affects people of all races, ethnicities, and geographic regions. Genes related to Addison disease, such as the genes for adrenal hyperplasia, are also found in the immune system. The development of an autoimmune response to medications is a process called autoimmune reversal.  The American Society of Clinical Endocrinologists offers information on the following:  The severity of symptoms varies from acute to chronic.']},
 {'focus_area': 'carnitine palmitoyltransferase II deficiency',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8651245832443237,
    0.8162598013877869,
    0.6950583457946777,
    0.8756577968597412,
    0.9047747850418091,
    0.8491886258125305,
    0.8957639932632446,
    0.7221348285675049,
    0.5821713209152222,
    0.8651245832443237],
   'self_bleu': [1.0,
    0.0,
    0.0,
    0.5946035575013605,
    0.5169731539571706,
    0.34172334076593075,
    0.691441569283882,
    0.0,
    0.0,
    1.0]},
  'real_data': ['What is (are) carnitine palmitoyltransferase II deficiency ?',
   'How many people are affected by carnitine palmitoyltransferase II deficiency ?',
   'What are the genetic changes related to carnitine palmitoyltransferase II deficiency ?',
   'Is carnitine palmitoyltransferase II deficiency inherited ?',
   'What are the treatments for carnitine palmitoyltransferase II deficiency ?'],
  'synthetic_data': ['How many carnitine palmitate transferase II deficiency are affected?',
   'How many carnitine-related palmitoyltransferase II deficiency are there?',
   'Carnitine â 2 -phosphate transferase deficiency is a by-product of the pallidinosine steroid syndrome?',
   'How many carnitine-palmitoyltransferase II deficiency are affected?',
   'What are the carnitine palmitoyltransferase II deficiency?',
   'How many carnitine related changes are affected by palmitoyltransferase II deficiency?',
   'What are carnitine palmitate transferase II deficiency?',
   'What are the Carnitine II - ATP-Carnitine II transferase deficiency confirmed in a pleural cavity?',
   'What is the CTP2                                                            ',
   'How many carnitine palmitate transferase II deficiency are affected?']},
 {'focus_area': 'carnitine palmitoyltransferase II deficiency',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5729372501373291,
    0.5840012431144714,
    0.569414496421814,
    0.5886614322662354,
    0.6133323907852173,
    0.5622601509094238,
    0.5486153364181519,
    0.5979792475700378,
    0.5862781405448914,
    0.5643521547317505],
   'self_bleu': [0.13203718386446836,
    0.1767252317626732,
    0.1915219637398896,
    0.20709291816781072,
    0.23908538492142883,
    0.18368947409629702,
    0.03205600567763682,
    0.30582843768738904,
    0.351382211800011,
    0.0]},
  'real_data': ['Carnitine palmitoyltransferase II (CPT II) deficiency is a condition that prevents the body from using certain fats for energy, particularly during periods without food (fasting). There are three main types of CPT II deficiency: a lethal neonatal form, a severe infantile hepatocardiomuscular form, and a myopathic form.  The lethal neonatal form of CPT II deficiency becomes apparent soon after birth. Infants with this form of the disorder develop respiratory failure, seizures, liver failure, a weakened heart muscle (cardiomyopathy), and an irregular heart beat (arrhythmia). Affected individuals also have low blood sugar (hypoglycemia) and a low level of ketones, which are produced during the breakdown of fats and used for energy. Together these signs are called hypoketotic hypoglycemia. In many cases, the brain and kidneys are also structurally abnormal. Infants with the lethal neonatal form of CPT II deficiency usually live for a few days to a few months.  The severe infantile hepatocardiomuscular form of CPT II deficiency affects the liver, heart, and muscles. Signs and symptoms usually appear within the first year of life. This form involves recurring episodes of hypoketotic hypoglycemia, seizures, an enlarged liver (hepatomegaly), cardiomyopathy, and arrhythmia. Problems related to this form of CPT II deficiency can be triggered by periods of fasting or by illnesses such as viral infections. Individuals with the severe infantile hepatocardiomuscular form of CPT II deficiency are at risk for liver failure, nervous system damage, coma, and sudden death.  The myopathic form is the least severe type of CPT II deficiency. This form is characterized by recurrent episodes of muscle pain (myalgia) and weakness and is associated with the breakdown of muscle tissue (rhabdomyolysis). The destruction of muscle tissue releases a protein called myoglobin, which is processed by the kidneys and released in the urine (myoglobinuria). Myoglobin causes the urine to be red or brown. This protein can also damage the kidneys, in some cases leading to life-threatening kidney failure. Episodes of myalgia and rhabdomyolysis may be triggered by exercise, stress, exposure to extreme temperatures, infections, or fasting. The first episode usually occurs during childhood or adolescence. Most people with the myopathic form of CPT II deficiency have no signs or symptoms of the disorder between episodes.',
   'CPT II deficiency is a rare disorder. The lethal neonatal form has been described in at least 18 families, while the severe infantile hepatocardiomuscular form has been identified in approximately 30 families. The myopathic form occurs most frequently, with more than 300 reported cases.',
   'Mutations in the CPT2 gene cause CPT II deficiency. This gene provides instructions for making an enzyme called carnitine palmitoyltransferase 2. This enzyme is essential for fatty acid oxidation, which is the multistep process that breaks down (metabolizes) fats and converts them into energy. Fatty acid oxidation takes place within mitochondria, which are the energy-producing centers in cells. A group of fats called long-chain fatty acids must be attached to a substance known as carnitine to enter mitochondria. Once these fatty acids are inside mitochondria, carnitine palmitoyltransferase 2 removes the carnitine and prepares them for fatty acid oxidation. Fatty acids are a major source of energy for the heart and muscles. During periods of fasting, fatty acids are also an important energy source for the liver and other tissues.  Mutations in the CPT2 gene reduce the activity of carnitine palmitoyltransferase 2. Without enough of this enzyme, carnitine is not removed from long-chain fatty acids. As a result, these fatty acids cannot be metabolized to produce energy. Reduced energy production can lead to some of the features of CPT II deficiency, such as hypoketotic hypoglycemia, myalgia, and weakness. Fatty acids and long-chain acylcarnitines (fatty acids still attached to carnitine) may also build up in cells and damage the liver, heart, and muscles. This abnormal buildup causes the other signs and symptoms of the disorder.',
   'This condition is inherited in an autosomal recessive pattern, which means both copies of the gene in each cell have mutations. The parents of an individual with an autosomal recessive condition each carry one copy of the mutated gene, but they typically do not show signs and symptoms of the condition.',
   "These resources address the diagnosis or management of CPT II deficiency:  - Baby's First Test  - FOD (Fatty Oxidation Disorders) Family Support Group: Diagnostic Approach to Disorders of Fat Oxidation - Information for Clinicians  - Gene Review: Gene Review: Carnitine Palmitoyltransferase II Deficiency  - Genetic Testing Registry: CARNITINE PALMITOYLTRANSFERASE II DEFICIENCY, LATE-ONSET  - Genetic Testing Registry: CARNITINE PALMITOYLTRANSFERASE II DEFICIENCY, LETHAL NEONATAL  - Genetic Testing Registry: Carnitine palmitoyltransferase II deficiency  - Genetic Testing Registry: Carnitine palmitoyltransferase II deficiency, infantile   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care"],
  'synthetic_data': ['CPT-2A, the gene for this condition, lacks a protein that carries the amino acid tyrosine. The deficiency causes the metabolic disorders fatty acid oxidation and phosphorylation. CPT-2A deficiency can be diagnosed in either mild or severe form. The most common form of CPT-2A deficiency is fatal. The following table summarizes the symptoms of this condition in more than 50 years. Parents, siblings, and children with CPT-2A deficiency can be treated with medications. The following table summarizes the causes',
   'The CPT II gene deficiency forms a fatty acid renin deficiency. This condition is rare in infants. It is usually diagnosed in neonates. A family with CPT II deficiency has two or more inherited mutations. Each mutation in the gene results in a different form of cardiomyopathy. For example, a person with CPT II deficiency will have a severe metabolic disorder. This article discusses the causes of cardiomyopathy. This page discusses the symptoms, signs, and treatment of cardiomyopathy.',
   "Since CPT II deficiency is a rare genetic disorder, it affects both parents. The following mutations cause the deficiency: ''Hydroxynadrenoproteinase II deficiency'' is a fatal form of the condition, which is characterized by the inability to use the liver for energy, and the inability to carry out the normal functions of the liver. This form of the disease is less common than other forms of the condition. Test the mutations on the same gene and see how many people with this condition have symptoms",
   'This guide is about the CPT2 family: Individuals with this condition typically have two copies of the defective gene. The severe form is cardiolipin deficiency. The less severe form is neoplastic cardiolipin deficiency. All the signs and symptoms of this disorder are not known. Mutations in the fatty acid oxidase enzyme prevent the body from absorbing and metabolizing fatty acids. These mutations can cause other metabolic disorders. Infants with cardiolipin deficiency often die each day.',
   'The following resources describe CPT II deficiency: Each mutation in the CPT2 gene is a form of an autosomal recessive disorder. This condition is transmitted by blood tests. The mutations in this gene cause a variety of symptoms, including fatty liver and oleic pyruvate oxidation. Infants with this condition usually have a healthy, healthy diet and few calories. The infant with this condition is usually in the early stages of life, and the mother is usually unaware that she has the condition. The condition rarely causes serious or life-threatening complications',
   "Inherited: The condition is inherited in families. Individuals with this condition do not have any family history of the condition. The condition is caused by a deficiency of the CPT gene, which is involved in the breakdown of fatty acids. Several tests are available to diagnose this condition....more about 'Cardiomyositis I'. Rare cases of severe deficiency of the MCOP gene are called 'Cardiomyositis I' or 'Cardiomyositis II'",
   'CPT-2 is a form of adenocarboxylase deficiency (which can be inherited into parents) and adenocarboxylase deficiency (which can be inherited into siblings). NIH-MY-N-I-I-I: NIH-MY-N-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I-I.',
   'CPT II deficiency is a form of a condition in which the fatty acids in the fatty acids are destroyed by the liver and the muscarinic steroid. Mutations in the CPT II gene can cause a deficiency in each copy of this gene. This is a recessive disorder, and all children with CPT II have at least one copy of this gene. Mutations in the CPT II gene can lead to a number of symptoms, including: 1 Mild: Usually not life-threatening. 2 Severe: Death',
   'CPT II is a condition in which the fatty acid oxidase enzyme is deficient. Mutations in the CPT II gene cause the condition. This form of CPT II deficiency is rarely seen in neonates, but it can be transmitted from one generation to the next. 1 The most common form of CPT II deficiency is a monosomy. 2 A family member with CPT II deficiency develops a history of liver disease, kidney disease, and obesity. 3 CPT II deficiency causes serious and sometimes fatal complications.',
   'The lack of a complete CPT2® hydroxylipoacyltransferase gene causes several different forms of the disorder. This guide will help you diagnose the various forms of CPT2® deficiency. The disorder is usually inherited by the affected family. Early infants are at risk for CPT2® deficiency because they are prone to developing a heart attack or stroke.iew full size image. A comprehensive guide to CPT2® hydroxylipoacyltransferase gene mutations.']},
 {'focus_area': 'Myxopapillary ependymoma',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.885486900806427,
    0.8153336644172668,
    0.9080007672309875,
    0.7228605151176453,
    0.7064706087112427,
    0.8563571572303772,
    0.8018951416015625,
    0.724697470664978,
    0.7877708077430725,
    0.823585569858551],
   'self_bleu': [0.5946035575013605,
    0.537284965911771,
    0.3976353643835253,
    0.0,
    0.7652058832556895,
    0.8891397050194614,
    0.6389431042462724,
    0.7652058832556895,
    0.7952707287670506,
    0.4347208719449915]},
  'real_data': ['What is (are) Myxopapillary ependymoma ?',
   'What are the treatments for Myxopapillary ependymoma ?'],
  'synthetic_data': ['What are the treatments for Myxomatoid ependyma?',
   'What are treatments for Myxo-ependyma?',
   'What are the treatments of Myxoma ependymopapillary?',
   'What is Myxoependyma ependyma?',
   'What is Myxoma ependymoplasia ( ependymoplasia )?',
   'What are the treatments for Myxoependyma ( ependymopapillary )?',
   'What are the treatments for Myxoependyma ependyma ( )?',
   'What are Myxoma ependymoplasia ( ependymoplasia )?',
   'What is Myxoependyma ( ependymopapillary )?',
   'What are treatments for My-epiphyseal ependymoma?']},
 {'focus_area': 'Myxopapillary ependymoma',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6121882200241089,
    0.6481812000274658,
    0.6574357748031616,
    0.6381385326385498,
    0.6832011342048645,
    0.6303473711013794,
    0.6580284833908081,
    0.5752953886985779,
    0.6491876244544983,
    0.664260983467102],
   'self_bleu': [0.07513361961518142,
    0.3485248384311511,
    0.1973571515056516,
    0.35329874994789034,
    0.2630144452785673,
    0.11904377071582736,
    0.3318075449703847,
    0.09773971449442184,
    0.4010785649479388,
    0.2460748104266283]},
  'real_data': ['Myxopapillary ependymoma (MEPN) is a slow-growing ependymoma (a type of glioma, which is a tumor that arises from the supportive tissue of the brain). They tend to occur in the lower part of the spinal column and are usually considered to be benign, low-grade or grade I tumors. The age of diagnosis ranges from 6 to 82 years. Symptoms of an ependymoma are related to the location and size of the tumor and may include nausea, vomiting, headache, pain, numbness, bowel or bladder symptoms, and various other signs and symptoms. The cause of ependymomas is unknown. They are known to recur locally (more commonly in individuals diagnosed in childhood). Treatment may vary depending on the location, grade, and whether the tumor has spread to the spine, but typically includes aggressive surgery. Management may also include chemotherapy and radiation therapy.',
   'How might myxopapillary ependymoma be treated? Standard treatment of myxopapillary ependymoma is surgery with the aim of removing as much of the tumor as possible. This tumor type may be cured if all of the tumor is removed during surgery, which is referred to as total resection, and there is usually a favorable outlook in these cases. However, surgery is typically less curative in tumors that are large, multifocal or extend outside the spinal cord. These tumors have the potential to regrow after the initial diagnosis and surgery (recur), particularly in individuals diagnosed as children. Following surgery, radiation therapy may be considered to destroy any cancer cells that could remain in the body.  The use of chemotherapy as another treatment of myxopapillary ependymoma remains controversial; chemotherapy has been widely used in pediatric individuals due to more aggressive disease. The usefulness of additional therapies following surgery is unclear for the subset of individuals with recurrence or in individuals in whom total resection cannot be achieved.'],
  'synthetic_data': ['Treatment is best for recurrent, recurrent, or recurrent myxomas. Myxomas are tumors that are surrounded by a membrane (ependyma) and can be in any of the choroid plexuses, including the spinal cord. Myxomas can occur in both pediatric and adult persons..........................',
   "Myxedema epiduralplasia (MEP) are generally slow-growing, low-grade tumors of the brain and spinal column. Treatment of this type of tumor is unknown because the individual's diagnosis and treatment may depend on the type of tumor. Surgery may be used to remove all remaining tumors (as well as any tumors that have spread to the spinal cord) when the tumor is large enough to be referred to a complete resection. When the tumor is large enough, symptoms may begin to recur, which can lead to relapse and/or ",
   'Epidural myxoma is considered a type of myxoma, which is a tumor of the ependymoma. When all remaining cells are removed, the tumor may grow as a whole. Treatment of epidural myxoma is conservative and may include surgery (e.g., a long-term resection) to remove the tumor. These tumors are generally low-grade and asymptomatic. They are most likely to recur in individuals younger than age 20. Large tumors can cause progressive neurological symptoms.',
   'Myxedema epiphysial (EP-E) tumors are considered a type of benign tumor, which tends to grow slowly and recur as individuals age. Treatment of this type of tumor depends on the extent of the tumor and the location of the tumor. When diagnosed, surgery may be performed to remove all of the remaining cells. However, if the tumor is large enough, a more complete surgical procedure may be needed. The treatment of this type of tumor may include: Symptoms of a recurrent (recurrent) ependymoencepha',
   'What is treatment for ependymal myxoma (EP)? Ependymal myxomas are considered a type of tumor that grows in the spinal cord. They are generally low-grade, meaning they are recurrent. As a tumor grows larger, it may recur. Treatment of ependymal myxoma may include chemotherapy or radiation therapy. All ependymal myxomas are diagnosed by a complete biopsy of the tumor. The size of the individual tumor may vary depending on the tumorâs location.',
   'Ependymoma is a type of myeloma that grows as a tumor of the lower spine. It may begin in the ependyma, if it is present, or it may be a total or all-or-nothing tumor. Treatment of recurrent myeloma is unknown. The best treatment for recurrent myeloma is surgery. The surgical procedures used to treat it are based on the age of the child and the severity of symptoms. 1 The tumors are very wide and wide.',
   'As a type of myelomeningoma, epiphrenymoma (also known as ependymoma) is of low-grade (total) and slow-growing. Treatment varies from individual to individual. If the tumor is diagnosed in the first year of life, surgery may be considered to remove all or part of the tumor. This may be followed by chemotherapy and/or a resection of the tumor. Relapses may be associated with symptoms of a recurrent (recurrence) of the brain and spinal',
   'Treatment of a Spinal-Epipamyoma. About 15 percent of all adults with a total number of epipamyomas have a relatively low risk of recurrence [4]. However, some epipamyomas can grow from any type of epipamyoma and may be asymptomatic [4]. Typically, a single drug is used to remove the tumor from the epipamyoma. However, the drugs are not effective in removing',
   "Myelophagia ependymoma is of a type of low-grade, slow-growing tumor that can be considered recurrent and recur as a result of the spread of the tumor. Treatment depends on the individual's age and overall health. Surgery may be used to remove all or part of the tumor if the tumor is large enough to be removed. As a result, the tumors in the ventral pons and/or medulla (the ependyma) are usually removed completely when children are 3 years",
   'What is treatment of epidural myxoma (also known as a ependymoma)? Epidural myxomas are slow-growing tumors that arise in the spinal cord. As they grow, they may recur. The type of surgery used to remove all tumors depends on the size, location, and grade of the tumor. Because epidural myxomas are rare, they are considered to be of low-grade. Individuals with a large tumor may have more severe symptoms. The most common recurrence occurs in children']},
 {'focus_area': 'Glutaric acidemia type II',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.4467059373855591,
    0.9125691056251526,
    0.9387298226356506,
    0.9459218978881836,
    0.8006951808929443,
    0.9321226477622986,
    0.9387298226356506,
    0.939088761806488,
    0.8247336745262146,
    0.9387298226356506],
   'self_bleu': [0.0,
    0.6580370064762462,
    1.0,
    0.6580370064762462,
    0.4001601601922499,
    0.5253819788848316,
    1.0,
    0.5253819788848316,
    0.4305051632268923,
    1.0]},
  'real_data': ['What is (are) Glutaric acidemia type II ?',
   'What are the symptoms of Glutaric acidemia type II ?',
   'What are the treatments for Glutaric acidemia type II ?'],
  'synthetic_data': ['What is the glucosamine alanine treponema type II? â Glucosamine alanine treponemas â Glucosamine alanine treponemas â Glucosamine alanine treponemas â Glucosamine alanine treponemas â Glucosamine alanine treponemas â Glucosamine alanine â  ',
   'What are the symptoms of gluconeotidase acidemia type II?',
   'What are the symptoms of glucuronic acidemia type II?',
   'What are the symptoms of glutaric acidemia type II?',
   'What are the trats of glucuronic acidemia (glucosuria type II )?',
   'What are the symptoms of Glutamine acidosis type II?',
   'What are the symptoms of glucuronic acidemia type II?',
   'What are the symptoms of Glutamic aciduria type II?',
   'What are glucuronic acidemia ( type II )?',
   'What are the symptoms of glucuronic acidemia type II?']},
 {'focus_area': 'Glutaric acidemia type II',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6231710314750671,
    0.48816558718681335,
    0.6225045323371887,
    0.6421639323234558,
    0.6170786619186401,
    0.5769007802009583,
    0.6111249327659607,
    0.6515036225318909,
    0.5971722602844238,
    0.6266141533851624],
   'self_bleu': [0.30774532736738985,
    0.0,
    0.3694408966227662,
    0.44845852108397405,
    0.27795123355485657,
    0.36658988020287947,
    0.13960714616947512,
    0.3665972585174065,
    0.15527211518619027,
    0.40834883825494184]},
  'real_data': ["Glutaric acidemia type II (GA2) is a disorder that interferes with the body's ability to break down proteins and fats to produce energy. The severity of GA2 varies widely among affected individuals. Some have a very severe form which appears in the neonatal period and may be fatal; individuals with this form may be born with physical abnormalities including brain malformations, an enlarged liver, kidney malformations, unusual facial features, and genital abnormalities. They may also emit an odor resembling sweaty feet. Others have a less severe form which may appear in infancy, childhood, or even adulthood. Most often, GA2 first appears in infancy or early childhood as a sudden episode of a metabolic crisis that can cause weakness, behavior changes (such as poor feeding and decreased activity) and vomiting. GA2 is inherited in an autosomal recessive manner and is caused by mutations in the ETFA, ETFB, or ETFDH genes. Treatment varies depending on the severity and symptoms but often includes a low fat, low protein, and high carbohydrate diet.",
   'What are the signs and symptoms of Glutaric acidemia type II? Signs and symptoms of glutaric acidemia type II (GA2) can vary widely depending on the age of onset and severity of the condition in each affected individual. In most cases, the condition appears in infancy or early childhood as a sudden episode called a metabolic crisis which causes weakness; behavior changes such as poor feeding and decreased activity; and vomiting. These crises can be life-threatening and may be triggered by common childhood illnesses or other stresses on the body. The most severe cases may appear in the neonatal period (within the first 4 weeks of life) and may also be characterized by the presence of physical abnormalities at birth. These abnormalities may include brain malformations; an enlarged liver (hepatomegaly); a weakened and enlarged heart (dilated cardiomyopathy); fluid-filled cysts and other malformations of the kidneys; unusual facial features; and genital abnormalities. Some affected individuals have a characteristic odor resembling sweaty feet. Other cases are less severe and may appear later in childhood, in adolescence, or in adulthood. In the most mild cases, muscle weakness may be the first sign of the disorder. The Human Phenotype Ontology provides the following list of signs and symptoms for Glutaric acidemia type II. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Abnormal facial shape - Abnormality of the genital system - Abnormality of the pinna - Autosomal recessive inheritance - Congenital cataract - Defective dehydrogenation of isovaleryl CoA and butyryl CoA - Depressed nasal bridge - Electron transfer flavoprotein-ubiquinone oxidoreductase defect - Ethylmalonic aciduria - Generalized aminoaciduria - Gliosis - Glutaric acidemia - Glutaric aciduria - Glycosuria - Hepatic periportal necrosis - Hepatic steatosis - Hepatomegaly - High forehead - Hypoglycemia - Hypoglycemic coma - Jaundice - Macrocephaly - Muscle weakness - Muscular hypotonia - Nausea - Neonatal death - Pachygyria - Polycystic kidney dysplasia - Proximal tubulopathy - Pulmonary hypoplasia - Renal cortical cysts - Respiratory distress - Telecanthus - Vomiting - Wide anterior fontanel - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.',
   "How might glutaric acidemia type II be treated? The goal of treatment is to prevent long-term problems. However, children who have repeated metabolic crises may develop life-long learning problems. Individuals with glutaric acidemia type II should consult with a metabolic doctor and a dietician who can help to develop an appropriate dietary plan. Some treatments may be recommended for some children but not for others. When necessary, treatment should be continued throughout the lifetime. The following treatments are often recommended:     -Avoidance of fasting. Infants and young children with glutaric acidemia type II should eat frequent meals in order to prevent hypoglycemia and metabolic crises.     -A low-fat, low-protein, high-carbohydrate diet may be advised.     -Riboflavin, L-carnitine and glycine supplements may be needed. These supplements help the body create energy.     -Alert the child's doctor if they should become ill, as illness can trigger a metabolic crisis."],
  'synthetic_data': ['Glutamic acidemia type II is a metabolic disorder of the fetal liver. Signs and symptoms of type II can vary from person to person and may appear suddenly or gradually. The symptoms of type II may include: - fatigue and weakness. - recurrent problems with gait and behavior. - a reduced or absent appetite. - a reduced or absent sex drive. - a reduced or absent sex drive. How are people with type II II treated? The following steps can be taken to help prevent or reduce the risk of developing the condition: 1 ',
   'Type II glucosuria is usually diagnosed when the following occur: (See also: glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria, glucosuria,... ).. ',
   'Glutamic acidosis type II is a metabolic disorder that can occur in infants or children. The symptoms of the disease are not unique to each person. For example, a person with type II may have too few EGFR and have a low EGFR. The severity of symptoms and the frequency of flare-ups are different. Treatment is recommended based on the severity of the problem. Dietary recommendations include avoiding foods that cause edema and causing a rapid rise in blood glucose. In addition, short-term dietary changes and lifestyle changes are recommended.',
   'Glutamic acidemia type II is a metabolic disorder. The symptoms of glutamic acidemia type II vary from person to person. The disease may appear in infants or young children. The first signs of the disease are often a lack of protein or fat in the diet. The symptoms of glutamic acidemia type II are often life-threatening. Treatment is based on the type of glucuronidemia and the frequency of flare-ups. 1 Symptoms may be avoided with diet and exercise. 2 Symptoms may be treated with medications. 3 Symptoms may include seizures',
   'Glutamic acidosis type II is a metabolic disorder. The frequency of symptoms varies with the severity of the disease.  First signs of glycogenuria (fatigue) may appear in people who have not yet reached puberty or who are unable to eat enough.  Often, the condition is diagnosed and treated as a lifelong condition.  Often, the treatment of glycogenuria type II is based on a balanced diet, exercise, and medications.  Often, the diet is avoided because of the potential for liver failure and other',
   'Glutamic acidosis type II appears as a metabolic disorder in infants with a low EF2 (Fresnel-Gadren-Eutrile-Hydroxylase) and a low EF2 (Fresnel-Gadren-Eutrile-Hydroxylase) diet. Symptoms can vary from person to person and can be life-threatening. Treatment for type II usually involves: 1 Helping to prevent or treat the symptoms of the disease. 2 Helping to prevent or treat',
   'Glutamic acidosis type II symptoms are a problem that may occur in infants. For example, in humans, the body is unable to eliminate all fats from the diet. Treatment is usually aimed at reducing or eliminating the fats and reducing the risk of future metabolic problems. For more information, see the following: -Diagnosis and treatment of Glutamic acidosis type II should be evaluated by a health care professional or registered nurse. -Fetal and perinatal ectopic ectopic ectopic ec',
   'What are the symptoms of glutamic acidemia type II? Glutamic acidemia type II is a metabolic disorder that may appear in infancy or childhood. It is diagnosed by a dietary change or a dietary deficiency. People with type II often have a low EGFR (fat-free) and are not able to function normally. Treatment for type II is based on the cause of the symptoms. Symptoms may be different from those of other metabolic disorders. Symptoms may include a rapid heartbeat, fatigue, and a decreased appetite.',
   'The symptoms of glutamic aciduria type II are often not understood and may be life-threatening. The disease appears in all people and can be a form of a metabolic syndrome. The following are the suggested treatment for GLUT2 type II. â Infants and young children with GLUT2 type II are âfailureâ to respond to a dietary restriction. â The failure may be a result of a genetic defect or a genetic predisposition. â The failure may be',
   'Glutamic acidemia type II is a metabolic disorder that can appear in infants and children. The signs and symptoms of type II may vary from person to person and may be triggered by the presence or absence of certain foods or proteins. The symptoms of type II may be recurrent or intermittent. Treatments for type II are based on the severity of the condition and the type of glucuronide deficiency. -Diabetes may be triggered by the lack of fasting. -Hemorrhage, weakness, and other problems may be prevented or reduced with treatment']},
 {'focus_area': 'complement factor I deficiency',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.9142134785652161,
    0.7520357966423035,
    0.799576461315155,
    0.8301578164100647,
    0.7184706330299377,
    0.6417325139045715,
    0.7964127659797668,
    0.6330541372299194,
    0.8084014654159546,
    0.8098891973495483],
   'self_bleu': [0.5410822690539396,
    0.45499414040480374,
    0.0,
    0.0,
    0.691441569283882,
    0.0,
    0.7071067811865476,
    0.0,
    0.3549481056010052,
    0.7071067811865476]},
  'real_data': ['What is (are) complement factor I deficiency ?',
   'How many people are affected by complement factor I deficiency ?',
   'What are the genetic changes related to complement factor I deficiency ?',
   'Is complement factor I deficiency inherited ?',
   'What are the treatments for complement factor I deficiency ?'],
  'synthetic_data': ['What are the effects of complement factor I deficiency?',
   'Are complement factor I deficiency affected?',
   'Are Complement Factor I deficiency inherited?',
   'What is a genetic deficiency in complement factor I?',
   'What are the complement factor I deficiency?',
   '(The majority of people with severe complement deficiency are recombinant factor I-deficient.) Is it possible? Is inherited spleen taken in a month?',
   'What are complement factor I deficiency?',
   'Factor I -complementary mutation and complement deficiency are?',
   'How many complement factor I deficiency are treated?',
   'What is complement factor I deficiency?']},
 {'focus_area': 'complement factor I deficiency',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5940189361572266,
    0.665018618106842,
    0.6353330016136169,
    0.6353964805603027,
    0.6466343402862549,
    0.6538772583007812,
    0.5869817137718201,
    0.6301140189170837,
    0.6084471940994263,
    0.5957232117652893],
   'self_bleu': [0.21442880819980303,
    0.37192637189144917,
    0.27616767086701205,
    0.474298992611101,
    0.5245856512492795,
    0.3482281011677046,
    0.15966285587088264,
    0.3220149645454971,
    0.16111526907645912,
    0.2172481957927964]},
  'real_data': ["Complement factor I deficiency is a disorder that affects the immune system. People with this condition are prone to recurrent infections, including infections of the upper respiratory tract, ears, skin, and urinary tract. They may also contract more serious infections such as pneumonia, meningitis, and sepsis, which may be life-threatening.  Some people with complement factor I deficiency have a kidney disorder called glomerulonephritis with isolated C3 deposits. Complement factor I deficiency can also be associated with autoimmune disorders such as rheumatoid arthritis or systemic lupus erythematosus (SLE). Autoimmune disorders occur when the immune system malfunctions and attacks the body's tissues and organs.",
   'Complement factor I deficiency is a rare disorder; its exact prevalence is unknown. At least 38 cases have been reported in the medical literature.',
   "Complement factor I deficiency is caused by mutations in the CFI gene. This gene provides instructions for making a protein called complement factor I. This protein helps regulate a part of the body's immune response known as the complement system. The complement system is a group of proteins that work together to destroy foreign invaders (such as bacteria and viruses), trigger inflammation, and remove debris from cells and tissues. This system must be carefully regulated so it targets only unwanted materials and does not attack the body's healthy cells. Complement factor I and several related proteins protect healthy cells by preventing activation of the complement system when it is not needed.  Mutations in the CFI gene that cause complement factor I deficiency result in abnormal, nonfunctional, or absent complement factor I. The lack (deficiency) of functional complement factor I protein allows uncontrolled activation of the complement system. The unregulated activity of the complement system decreases blood levels of another complement protein called C3, reducing the immune system's ability to fight infections. In addition, the immune system may malfunction and attack its own tissues, resulting in autoimmune disorders.",
   'This condition is inherited in an autosomal recessive pattern, which means both copies of the gene in each cell have mutations. The parents of an individual with an autosomal recessive condition each carry one copy of the mutated gene, but they typically do not show signs and symptoms of the condition.',
   'These resources address the diagnosis or management of complement factor I deficiency:  - MedlinePlus Encyclopedia: Complement   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care'],
  'synthetic_data': ['Complement factor I deficiency is described by the condition in its rare, autosomal recessive form.  Each of the 38 known gene mutations in this gene brings about an immune system disorder.  People with one or more copies of this gene may develop or inherit the disorder.  These resources include:  Medicine, dietary, and other health information;  Diagnosis and treatment;  Treatment; and more.',
   'Complement factor I deficiency is an uncommon condition, and the disorder is inherited in an autosomal recessive pattern. The genes that control the immune system also can lead to the symptoms of this disorder. The following 33 health and medical literature pages provide information about each one.',
   'Complement factor I deficiency is inherited in an unusual way.  The condition includes the following disorders:  The condition only affects one copy of the complement factor I gene.  The condition causes the body to mismanage the immune system.  The condition may lead to recurrent or recurrent infections.  The condition is diagnosed during a routine PCR test.  Patients with this disorder are at increased risk for developing a cirrhosis.  Treatment options are available through the WebMD Health Care website.',
   'Complement factor I deficiency is an inherited disorder. At least 38 copies of the gene are present in each cell. Mutations in this gene cause the condition, but the condition is rare.  Complement factor I deficiency is a disorder that affects the immune system.  The condition is a combination of an autosomal recessive and a syndromic pattern.  People with this condition have a decreased ability to manage their health problems. The following resources provide information about the symptoms, diagnosis, and treatment of complement factor I defici',
   ' Complement factor I deficiency is a rare condition.  The condition is inherited in an autosomal recessive pattern.  Each of the three copies of the gene that causes complement factor I deficiency is mutated in at least one of the 20 genes.  These mutations can affect the immune system, resulting in a variety of disorders, including infections, neurological disorders, and sclerosis.  The following resources provide information about the symptoms, diagnosis, and treatment of people with this disorder.',
   'Complement factor I deficiency is an inherited condition, with the first 32 cases being autosomal recessive. The genes that regulate this gene also play a role in the immune system -- some people with this disorder may develop chronic or recurrent infections and other symptoms. The resources below provide detailed information about the disorder.',
   'When complement factor I deficiency is present, either the COR gene is missing or the COR gene is not functioning properly. Individuals with complement factor I deficiency develop a rare, potentially fatal disorder of the immune system. Medications, tests, and other tools help treat complement factor I deficiency. Topics covered in this guide include: 1 Immunology. 2 Neurology. 3 Neurology. 4 Neurology. 5 Neurology. 6 Neurology. 7 Neurology. 8 Neurology.',
   "Complement factor I deficiency is a rare condition. Both parents inherit mutations in the complement factor I gene, which plays a role in the body's defense against infection and inflammation. The following 38 books provide information on the disorder, its symptoms, and management. Each of these books includes a summary of the available resources.  Complement factor I deficiency disorders are not yet diagnosed.  Patients with the disorder may need to be referred to a health care provider.",
   'In addition, individuals with complement factor I deficiency have a rare condition in which the gene responsible for regulating the activity of complement factor I is lost in the vascular system. Deficiency of these antibodies is a health condition and is not a life-threatening condition.  Drugs & Supplements (25 pages) â These medicines are intended to be used as a dietary supplement and may be prescribed by your doctor.',
   ' Deficiency of complement factor I leads to illness and the symptoms are unknown.  The way the condition is diagnosed is regulated by the complement factor I gene (C26.8 and C25.8).  Patients with this gene may need to check for a number of complementary and recombinant proteins, including a key enzyme needed to form antibodies, a blood clotting factor, and a bone marrow resorption factor. ']},
 {'focus_area': 'Niemann-Pick disease type A',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.9184035658836365,
    0.8605928421020508,
    0.8775603771209717,
    0.9268245100975037,
    0.9495969414710999,
    0.8975157737731934,
    0.927264392375946,
    0.9019902944564819,
    0.8650375008583069,
    0.8514043688774109],
   'self_bleu': [0.9146912192286945,
    0.587728372510532,
    0.6493358309501979,
    0.6580370064762462,
    0.8891397050194614,
    0.7348889200874658,
    0.6580370064762462,
    0.4234197579236933,
    0.668740304976422,
    0.7348889200874658]},
  'real_data': ['What is (are) Niemann-Pick disease type A ?',
   'What are the symptoms of Niemann-Pick disease type A ?',
   'What are the treatments for Niemann-Pick disease type A ?'],
  'synthetic_data': ['What are the symptoms of Niels-Pick disease ( type A )?',
   'What are the symptoms of Neisseria pyogenes type A disease?',
   'What are the symptoms and treatments of Nissler-Parkinson disease type A?',
   'What are the symptoms of Niirmann-Pick disease type A?',
   'What are the symptoms of Niels-Pick disease type A?',
   'What are the symptoms of Niermann-Pickman disease ( type A )?',
   'What are the symptoms of Niermann-Pick type A disease?',
   'What are the treatments for Niiman-Pick disease type A?',
   'What are the symptoms and treatments for Niels-Parkinson-White disease type A?',
   'What are the symptoms of Parkinson-Nielsen disease ( type A )?']},
 {'focus_area': 'Niemann-Pick disease type A',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6541517376899719,
    0.6037687659263611,
    0.5791140794754028,
    0.6503658890724182,
    0.5761322975158691,
    0.5865345597267151,
    0.6387924551963806,
    0.601351797580719,
    0.6093366146087646,
    0.6292544007301331],
   'self_bleu': [0.30656839850350265,
    0.2689207995450403,
    0.2537090724161572,
    0.5063314608316138,
    0.11052685079323592,
    0.2226464119961278,
    0.3953687611798111,
    0.29861114438040354,
    0.5138394445092392,
    0.37329639360216776]},
  'real_data': ['Niemann-Pick disease is an inherited condition involving lipid metabolism, which is the breakdown, transport, and use of fats and cholesterol in the body. In people with this condition, abnormal lipid metabolism causes harmful amounts of lipids to accumulate in the spleen, liver, lungs, bone marrow, and brain. Niemann-Pick disease type A appears during infancy and is characterized by an enlarged liver and spleen (hepatosplenomegaly), failure to gain weight and grow at the expected rate (failure to thrive), and progressive deterioration of the nervous system. Due to the involvement of the nervous system, Niemann-Pick disease type A is also known as the neurological type. There is currently no effective treatment for this condition and those who are affected generally do not survive past early childhood. Niemann-Pick disease type A is caused by mutations in the SMPD1 gene. It is inherited in an autosomal recessive pattern.',
   'What are the signs and symptoms of Niemann-Pick disease type A? The Human Phenotype Ontology provides the following list of signs and symptoms for Niemann-Pick disease type A. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Cherry red spot of the macula 50% Athetosis - Autosomal recessive inheritance - Bone-marrow foam cells - Constipation - Diffuse reticular or finely nodular infiltrations - Failure to thrive - Feeding difficulties in infancy - Foam cells with lamellar inclusion bodies - Hepatomegaly - Hyporeflexia - Infantile onset - Intellectual disability - Lymphadenopathy - Microcytic anemia - Muscle weakness - Muscular hypotonia - Osteoporosis - Protuberant abdomen - Recurrent respiratory infections - Rigidity - Sea-blue histiocytosis - Short stature - Spasticity - Splenomegaly - Vomiting - Xanthomatosis - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.',
   'How might Niemann-Pick disease type A be treated? There is no specific treatment for this disease. Supportive care from the following specialists may be helpful for managing the symptoms:  A pulmonologist for respiratory problems A cardiologist for heart problems Liver and spleen specialists Nutritionists Physical therapists A gastroenterologist Learning specialists You can learn more about ongoing research efforts to better understand the natural history of this condition and identify treatment options in the Research section of our web page.'],
  'synthetic_data': ['What is Nemours-Pick disease type A? Nemours-Pick disease type A is diagnosed by liver biopsy or hepatocellular splenomegaly. There is no known treatment for this condition. Symptoms in Nemours-Pick disease type A are different for each person affected. Symptoms include a fatty liver, a sluggish heart, and a progressive brain disorder. Contact a pediatrician or neurologist for help with symptoms. This information is compiled from the latest medical literature available on this site',
   'Physical symptoms of Nihmann-Pickler disease type A are listed in the following section: No cure for this disease is known. The disease is inherited and can be treated by a variety of therapies. Symptoms include frequent recurrence of the disease, a progressive decline in the normal function of the liver, spleen, and kidneys. Supportive care specialists are available to diagnose and treat the condition. For example, pediatricians can diagnose the condition in infants and children. For adults, the pediatrician can diagnose and treat the condition in adults.',
   'What are the symptoms of Nihon-Pickman disease type A? â This is a inherited disorder of the liver and spleen. â The number of spleen cells affected varies. â The number of spleen cells affected varies. â Prevention of sclerosis may be more effective when the disease is treated by a health care professional (e.g., a pediatrician, family doctor, or a family physician). â Chronic recurrent sclerosis may be treated with a drug.',
   'Neiman-Pick disease type A is diagnosed based on the frequency of symptoms and the severity of the disease. For more information, see the topic Neiman-Pick disease type A. Support from a pediatrician, family physician, or other health care professional. There is no known treatment for this condition. People with this condition may have abnormalities in the spleen, liver, and kidneys. These abnormalities include a recessive form of a fatty acid called hematopoietic acid (H-Muhlmann-Pick).',
   'How is Neanderthal type A neoplasm treated? The following list of diseases are in some way related to Neanderthal type A neoplasm. These diseases may include liver dysfunction, lipid depletion, asthma, pulmonary disease, sarcopenia, and aplastic anemia. Each child is unique and has a different diagnosis and treatment plan. The best way to diagnose Neanderthal type A neoplasm is by a family doctor or a family doctor. The frequency of symptoms for Neanderthal type A neoplasm is.',
   'About Niels-Pickman disease type A The frequency and severity of symptoms are determined by the presence of a phenotypic abnormality in the lipids of the lipids (sugars) in the lipids. This abnormality may be seen on a chest MRI or in a chest MRI. No treatment for this inherited disease is currently known. Supportive care is needed for people with this condition, including a pediatrician, a family physician, a pediatrician, a family doctor, and a pediatrician.',
   'How is Nihmann-Pick disease type A diagnosed? Symptoms of this disease can include abnormalities of the liver and spleen, a chronic disease of the lungs known as a nephrotic syndrome, and a progressive disease of the kidneys known as a metabolic syndrome. Support from a pediatrician, family physician, or physical therapist is needed for the onset and progression of symptoms. There is no cure for this condition. The information in this section is based on the information available in the Resources section.',
   'What is the NPI for Pickens-Mollenheimer type A disease? The diagnosis of this disease is based on the symptoms experienced by the affected person. Symptoms may include frequent urination, dysphagia, and a fatty or spongy discharge from the nose. The liver and kidneys may be affected. There is no cure for this condition. Support from a physician is needed to treat the symptoms of this disorder. The disease is a recessive disorder, meaning that the disease is not inherited. Support from a physician is needed',
   'What are the symptoms of Niels-Pickman disease type A? The severity of this disease is determined by the frequency of a disease. For example, a person with this condition may have a neoplastic hematopoietic reticulopathy (a deficiency of a neoplastic reticulocyte) in the liver, kidneys, and lungs. No treatment is known for this condition. Supportive care is available from a pediatrician, family physician, or other health care professional. The specialists in this section are not affiliated.',
   'What is Niemann-Pick disease type A? The severity of Niemann-Pick disease type A is known from the splenic plexus (splenic hematopoietic epithelium) and pulmonary vascular disease. The following list of symptoms may be helpful in treating this condition. Medicines used to treat Niemann-Pick disease type A are listed in the Diseases section of this website. A family doctor or health care professional can help diagnose and treat this condition. There is no cure for this condition. The risk of developing a serious lung, heart,']},
 {'focus_area': 'Granuloma annulare',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.9313396215438843,
    0.9738609790802002,
    0.8858492374420166,
    0.9438955783843994,
    0.9043881297111511,
    0.8719117641448975,
    0.8858492374420166,
    0.9709466099739075,
    0.9323251843452454,
    0.9043881297111511],
   'self_bleu': [0.0,
    0.0,
    1.0,
    0.7071067811865475,
    1.0,
    0.0,
    1.0,
    0.9457416090031758,
    0.0,
    1.0]},
  'real_data': ['What is (are) Granuloma annulare ?',
   'What are the symptoms of Granuloma annulare ?',
   'What causes Granuloma annulare ?',
   'What are the treatments for Granuloma annulare ?'],
  'synthetic_data': ['What are the usual treatments for Granuloma annulare?',
   'What causes granuloma annulare?',
   'What is Granuloma annulare?',
   'What are the symptoms of Granuloma Annuum?',
   'What is the cause of Granuloma annulare?',
   'What is granuloma annulare?',
   'What is Granuloma annulare?',
   'What are the symptoms of Granuloma annulare?',
   'What is a symptom of granuloma annulare?',
   'What is the cause of Granuloma annulare?']},
 {'focus_area': 'Granuloma annulare',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.7082443833351135,
    0.6850062012672424,
    0.6747562885284424,
    0.7251340746879578,
    0.6763373017311096,
    0.6205825209617615,
    0.7023264169692993,
    0.6515328288078308,
    0.6727521419525146,
    0.6647825241088867],
   'self_bleu': [0.23439983610100093,
    0.4556907616852654,
    0.2903171605613247,
    0.3740816897781823,
    0.3176648521928878,
    0.21807844490296355,
    0.4953233188545663,
    0.3262132584626047,
    0.39810295232240556,
    0.20805523284472577]},
  'real_data': ['Granuloma annulare is a long-term (chronic) skin disease consisting of a rash with reddish bumps arranged in a circle or ring. The most commonly affected areas are the forearms, hands and feet. The lesions associated with granuloma annulare usually resolve without treatment. Strong steroids (applied as a cream or injection) are sometimes used to clear the rash more quickly. Most symptoms will disappear within 2 years (even without treatment), but recurrence is common. The underlying cause of granuloma annulare is unknown.',
   'What symptoms are associated with granuloma annulare? People with this condition usually notice a ring of small, firm bumps (papules) over the backs of the forearms, hands or feet. Occasionally, multiple rings may be found. Rarely, granuloma annulare may appear as a firm nodule under the skin of the arms or legs.',
   'What causes granuloma annulare? The cause of granuloma annulare is unknown, although there is much evidence that it is linked to the immune system. It has been reported to follow insect bites; sun exposure; tuberculin skin tests, ingestion of allopurinol; trauma; and viral infections, including Epstein-Barr, HIV, hepatitis C, and herpes zoster. Occasionally, granuloma annulare may be associated with diabetes or thyroid disease.',
   "How might granuloma annulare be treated? Granuloma annulare is difficult to treat and there are a limited number of clinical trials to reliably inform patients and physicians of the treatment options. Fortunately, most lesions of granuloma annulare disappear with no treatment within two years. Sometimes, however, the rings can remain for many years. Very strong topical steroid creams or ointments may be used to speed the disappearance of the lesions. Injections of steroids directly into the rings may also be effective. Some physicians may choose to freeze the lesions with liquid nitrogen. In severe cases, ultraviolet light therapy (PUVA) or oral medications may be needed. Other treatments that have been tried include :   Dapsone (a type of antibiotic) for widespread granuloma annulare  Isotretinoin  Etretinate (not available in the US)  Hydroxychloroquine  Chloroquine  Cyclosporine  Niacinamide  Oral psoralen  Vitamin E combined with a 5-lipoxygenase inhibitor  Fumaric acid esters  Topical tacrolimus  Pimecrolimus  Infliximab (in a patient with disseminated granuloma annulare that did not respond to other treatments) A review article titled, 'Diagnosis and Management of Granuloma Annulare' provides additional information on treatment options for granuloma annulare: http://www.aafp.org/afp/20061115/1729.html  Also, an article from Medscape Reference provides information on treatment for granuloma annulare at the following link. You may need to register to view the article, but registration is free. http://emedicine.medscape.com/article/1123031-overview"],
  'synthetic_data': ['Granuloma annulare is uncommon. It comes with a rash that may be seen on the feet or hands. The rash may be a sign of a systemic disease (see Glomerulonephritis). The cause of granuloma annulare is unknown. Treatments for granuloma annulare include a combination of medications, including a topical steroid cream. 1 Symptoms usually resolve after several days. 2 Granuloma annulare is usually caused by a combination of fungi, viruses, and',
   'What causes granuloma annulare? Granuloma annulare is associated with a wide range of symptoms. The lesions may be red or appear as a ring. The lesions may be a few centimeters across. Treatment for granuloma annulare includes topical corticosteroids, a steroid regimen, and a neomycin-based regimen. Rarely, granuloma annulare may be seen on the hands or feet. People with psoriasis often have the disease',
   'What is granuloma annulare? Granuloma annulare is a chronic, unresolved disease. Treatment is limited to the treatment of the lesion. People with granuloma annulare often have a ring of scabs around the skin, which can be seen on the fronts of the feet, hands, and face. Other symptoms include: rash; itchiness; scabs; dandruff; fungus; fungus granuloma annulare. DHZ has been tested',
   '1 Granuloma annulare is often associated with a red, firm ring of skin that may be seen over the groin, wrists, and feet. The cause of this disease is unknown. Treatment for granuloma annulare is anti-inflammatory medications such as steroid shots or an antifungal/anti-fungal regimen. The granulomas typically disappear after a few years, but some people develop recurrent episodes.',
   'The following are associated with granuloma annulare: Granuloma annulare is often a red ring that gradually fades over years. The skin may also be irritated by a strong immune system reaction to a drug (e.g., sulfa drugs or hyaluronic acid). Treatment for granuloma annulare is generally broad-spectrum. Rarely, the lesions may form on the hands or feet, especially when there is a skin test for psoriasis.',
   'What treatment is used for granuloma annulare? Granuloma annulare often appears as a ring-like lesions but the symptoms are often brief and resolvable if the disease is treated quickly. A number of factors contribute to the disease, including systemic infections (e.g., atopic dermatitis) or a skin problem (e.g., atopic dermatitis of the hands or feet); blood vessel problems (e.g., atopic dermatitis of the feet); or a skin problem',
   'What causes granuloma annulare? Granuloma annulare is a ring-like skin lesion with a granuloma-like pattern. The lesions may persist for years. Treatment for granuloma annulare is often a combination of topical steroids, anti-inflammatory drugs, or a neomycin-based treatment. The granuloma may be triggered by a herpes simplex virus. It is most common on the hands and feet. People with granuloma annulare',
   'What treatment does granuloma annulare? Granuloma annulare is often associated with a persistent, vague rash. The rash can be red, with small, firm bumps that appear over the skin. The granuloma annulare may also be caused by an infection with the fungus papillomavirus. This disease usually disappears without treatment, but some people develop a combination of these conditions: atopic dermatitis (skin disease) of the hands and feet, and atopic dermatitis (skin',
   'What is granuloma annulare? Granuloma annulare is a skin lesion often associated with a hereditary syndrome. The symptoms may last for years. Treatment for granuloma annulare depends on the cause. â Acute granuloma annulare occurs in the hands and feet. â Infections such as scabies or ringworm can make granuloma annulare worse. â Several drugs such as corticosteroids (e.g., ibupro',
   'Granuloma annulare is associated with a few ring-like lesions that often remit over time. The cause is unclear. Treatment is simple: rubbing the granuloma annulare with a topical steroid or a topical corticosteroid. Granuloma annulare is difficult to diagnose because it is a permanent skin disease. It is seen on the fingers and hands of people with psoriasis, atopic dermatitis, and ringworm. See also: granuloma']},
 {'focus_area': 'cherubism',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.7211095690727234,
    0.6668918132781982,
    0.7772921323776245,
    0.7227397561073303,
    0.7849095463752747,
    0.6288231611251831,
    0.7738454341888428,
    0.729021430015564,
    0.815190851688385,
    0.895835280418396],
   'self_bleu': [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]},
  'real_data': ['What is (are) cherubism ?',
   'How many people are affected by cherubism ?',
   'What are the genetic changes related to cherubism ?',
   'Is cherubism inherited ?',
   'What are the treatments for cherubism ?'],
  'synthetic_data': ['2 treatments for cherubic acromegaly?',
   'About 2 million cherubic acromegaly are treated?',
   'What are cherub entropion?',
   'Are 2 cherubic parents?',
   'What are cherubic limbs?',
   '1 So called cherubics are chancres?',
   'What is cherub pediosis?',
   'What is the effect of cherubic, chameleons?',
   'What is cherubim syndrome?',
   'How many people are affected by cherubima?']},
 {'focus_area': 'cherubism',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6588007211685181,
    0.5876560211181641,
    0.6426647901535034,
    0.5358110070228577,
    0.566836953163147,
    0.5494534373283386,
    0.7025907635688782,
    0.4970059394836426,
    0.6449722051620483,
    0.6345329880714417],
   'self_bleu': [0.3928561680654853,
    0.0,
    0.2636575429178864,
    0.13245920481401605,
    0.27894122179975256,
    0.08955622932515915,
    0.2496553412637276,
    0.14651600437172246,
    0.2699532090040704,
    0.2188951136355714]},
  'real_data': ['Cherubism is a disorder characterized by abnormal bone tissue in the lower part of the face. Beginning in early childhood, both the lower jaw (the mandible) and the upper jaw (the maxilla) become enlarged as bone is replaced with painless, cyst-like growths. These growths give the cheeks a swollen, rounded appearance and often interfere with normal tooth development. In some people the condition is so mild that it may not be noticeable, while other cases are severe enough to cause problems with vision, breathing, speech, and swallowing. Enlargement of the jaw usually continues throughout childhood and stabilizes during puberty. The abnormal growths are gradually replaced with normal bone in early adulthood. As a result, many affected adults have a normal facial appearance.  Most people with cherubism have few, if any, signs and symptoms affecting other parts of the body. Rarely, however, this condition occurs as part of another genetic disorder. For example, cherubism can occur with Ramon syndrome, which also involves short stature, intellectual disability, and overgrowth of the gums (gingival fibrosis). Additionally, cherubism has been reported in rare cases of Noonan syndrome (a developmental disorder characterized by unusual facial characteristics, short stature, and heart defects) and fragile X syndrome (a condition primarily affecting males that causes learning disabilities and cognitive impairment).',
   'The incidence of cherubism is unknown. At least 250 cases have been reported worldwide.',
   'Mutations in the SH3BP2 gene have been identified in about 80 percent of people with cherubism. In most of the remaining cases, the genetic cause of the condition is unknown.  The SH3BP2 gene provides instructions for making a protein whose exact function is unclear. The protein plays a role in transmitting chemical signals within cells, particularly cells involved in the replacement of old bone tissue with new bone (bone remodeling) and certain immune system cells.  Mutations in the SH3BP2 gene lead to the production of an overly active version of this protein. The effects of SH3BP2 mutations are still under study, but researchers believe that the abnormal protein disrupts critical signaling pathways in cells associated with the maintenance of bone tissue and in some immune system cells. The overactive protein likely causes inflammation in the jaw bones and triggers the production of osteoclasts, which are cells that break down bone tissue during bone remodeling. An excess of these bone-eating cells contributes to the destruction of bone in the upper and lower jaws. A combination of bone loss and inflammation likely underlies the cyst-like growths characteristic of cherubism.',
   'This condition is inherited in an autosomal dominant pattern, which means one copy of the altered gene in each cell is sufficient to cause the disorder.',
   'These resources address the diagnosis or management of cherubism:  - Gene Review: Gene Review: Cherubism  - Genetic Testing Registry: Fibrous dysplasia of jaw   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care'],
  'synthetic_data': ['The condition of cherubic symphysis is diagnosed by gene mutations, which means that at least one copy of the gene is present in each cell. This provides guidelines for the management of bone and cartilage disorders in more than 250 people worldwide.',
   "This usually leads to the onset of a person's aphasia and the resulting aphasia is not known and there is a minimal level of the disorder in approximately 130,000 babies [sources: CHEEDS]",
   'An authoritative guide is provided about the condition cherubic pedunculosis, which is a disorder in which one copy of the gene in each cell is mutated, causing abnormalities in bone and tissue growth, and in the reproduction of the upper jaw. ',
   'A cherubic syndrome is uncommon, and it occurs in at least 250 cases. This disease may be transmitted by the same gene in both sexes. The resulting condition may take on more than one form, affecting bone and cartilage.See also: Inborn and induced skeletal disorders.Diseases of the first line of health care: Inborn and induced skeletal disorders.Diseases of the first line of health care: Inborn and induced skeletal disorders.Diseases of the first line of health care: Inborn and induced skeletal disorders',
   "Cherubic syndrome is diagnosed in at least one copy of the mutated gene. This gene interferes with the normal development of bone and other tissues, causing facial projections.  As many as 250 cases of this condition are reported worldwide.  As many as 2,000 cases are reported worldwide.  As many as 2,000 cases are reported worldwide.  The following is a comprehensive review of chin dysplasia, an inherited disorder that affects the body's ability to make and maintain healthy tissue.",
   "The following is a list of diseases associated with the condition - 'Cheroderma Pupillary Syndrome'. The condition is a primary inherited disorder. It occurs in one or both sexes. In the first case, the disease is asymptomatic. In the second case, the disease is asymptomatic. In the third case, the disease is asymptomatic. The changes in the genes that control the development of the bone marrow, syringes, and tendons in the body, such as adrenergic chondro",
   'The condition cherubic monstruum is diagnosed in at least 250 cases worldwide. This is an autosomal recessive disorder, which means that one copy of an altered gene in each cell is sufficient to cause the condition. In cherubic monstruum, an altered gene results in abnormal protein synthesis in the bone and facial tissues.  The following resources provide information about cherubic monstruum, including: 1 Clinical signs and symptoms. 2 Treatment. 3 Risk factors.',
   'The reversal of the chubbing is a hormone-mediated condition -- which means that at least one child with chubbing has the same symptoms as those with a more severe chubbing disorder.  See also: Up to 300 chromosomes (inactivated)  See also:  Genes (inactivated)  Symptoms (inactivated)  Symptoms (inactivated)  Symptoms (inactivated)  Symptoms (inactivated)    ',
   'A review of the medical literature indicates that cherubic suppurativum is an inherited condition, which means that at least 1 case of this disorder occurs in every 250 adults worldwide.  Mutations in the gene cause the effects of the disorder on bone and other tissues, thereby preventing the development of syndroms.',
   'The cherubic sarcoma is a gene-mediated disorder, so more than 250 cases are reported worldwide.  This fact sheet provides basic information about the development, management, and treatment of abnormalities in the jaw and other tissues that may be affected by this condition.']},
 {'focus_area': 'Rett Syndrome',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8313555717468262,
    0.8031039834022522,
    0.8009212613105774,
    0.810316264629364,
    0.8785330653190613,
    0.781316339969635,
    0.6799455881118774,
    0.8013699054718018,
    0.7970287799835205,
    0.8341147899627686],
   'self_bleu': [0.691441569283882,
    0.8545740127924681,
    0.9234732618882052,
    0.7691605673134586,
    0.0,
    0.0,
    0.0,
    0.8127596564026885,
    0.5348259312838877,
    1.0]},
  'real_data': ['What is (are) Rett Syndrome ?',
   'What is (are) Rett Syndrome ?',
   'What are the treatments for Rett Syndrome ?',
   'What is the outlook for Rett Syndrome ?',
   'what research (or clinical trials) is being done for Rett Syndrome ?'],
  'synthetic_data': ['What is a Rett Syndrome ( )?',
   'What are the treatments for Rett Syndrome ( Rett syndrome )?',
   'What are the treatments for Rett Syndrome ( R ett syndrome )?',
   'What are the treatments for Rett Syndrome ( Rett Syndrome )?',
   'What is the best way to treat Rett syndrome?',
   'Treatment for Rett Syndrome?',
   'What is a rett syndrome ( rett syndrome of the world )?',
   'What are the treatments for Rett syndrome ( R ett syndrome )?',
   'What is the Rett Syndrome ( treatment for one )?',
   'What is the Rett Syndrome ( )?']},
 {'focus_area': 'Rett Syndrome',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6401901245117188,
    0.6409039497375488,
    0.6000231504440308,
    0.603752851486206,
    0.587790310382843,
    0.6416839361190796,
    0.6535521745681763,
    0.6348390579223633,
    0.6360591053962708,
    0.6573225259780884],
   'self_bleu': [0.3422084252347712,
    0.3764895320074594,
    0.24507697406761642,
    0.1719001162734401,
    0.19144299131348125,
    0.41068122541074076,
    0.38300296248329574,
    0.2597305534817395,
    0.31114874566397616,
    0.25499599982789406]},
  'real_data': ["Rett syndrome is a rare genetic disease that causes developmental and nervous system problems, mostly in girls. It's related to autism spectrum disorder. Babies with Rett syndrome seem to grow and develop normally at first. Between 3 months and 3 years of age, though, they stop developing and even lose some skills. Symptoms include       - Loss of speech    - Loss of hand movements such as grasping    - Compulsive movements such as hand wringing    - Balance problems    - Breathing problems    - Behavior problems    - Learning problems or intellectual disability       Rett syndrome has no cure. You can treat some of the symptoms with medicines, surgery, and physical and speech therapy. Most people with Rett syndrome live into middle age and beyond. They will usually need care throughout their lives.    NIH: National Institute of Child Health and Human Development",
   'Rett syndrome is a childhood neurodevelopmental disorder that affects females almost exclusively. The child generally appears to grow and develop normally, before symptoms begin. Loss of muscle tone is usually the first symptom. Other early symptoms may include a slowing of development, problems crawling or walking, and diminished eye contact. As the syndrome progresses, a child will lose purposeful use of her hands and the ability to speak. Compulsive hand movements such as wringing and washing follow the loss of functional use of the hands. The inability to perform motor functions is perhaps the most severely disabling feature of Rett syndrome, interfering with every body movement, including eye gaze and speech.',
   'There is no cure for Rett syndrome. Treatment for the disorder is symptomatic, focusing on the management of symptoms, and supportive. Medication may be needed for breathing irregularities and motor difficulties, and antiepileptic drugs may be used to control seizures. Occupational therapy, physiotherapy, and hydrotherapy may prolong mobility. Some children may require special equipment and aids such as braces to arrest scoliosis, splints to modify hand movements, and nutritional programs to help them maintain adequate weight. Special academic, social, vocational, and support services may be required in some cases.',
   'The course of Rett syndrome, including the age of onset and the severity of symptoms, varies from child to child. Despite the difficulties with symptoms, most individuals with Rett syndrome continue to live well into middle age and beyond. Because the disorder is rare, very little is known about long-term prognosis and life expectancy.',
   'The National Institute of Neurological Disorders and Stroke (NINDS) and other institutes of the National Institutes of Health (NIH) conduct research related to Rett syndrome in laboratories at the NIH, and also support additional Rett syndrome research through grants to major medical institutions across the country. The discovery of the Rett syndrome gene in 1999 provides a basis for further genetic studies. Understanding the cause of this disorder is necessary for developing new therapies to manage specific symptoms, as well as for providing better methods of diagnosis.'],
  'synthetic_data': ['The disorder causes a loss of normal neurological development, with symptoms of rett syndrome, most commonly in the early to middle years of life. In rare cases, children may develop difficulty with speech, hand and foot movements, and the ability to walk. The National Institutes of Health and the Rett Syndrome Research Institute are developing a cure for this disease. Medical care and other treatments are ongoing, and the goal is to improve the quality of life for all girls and women with Rett syndrome.',
   'The Rett syndrome is a neurological disorder. The National Institutes of Health and the Office of Rare Diseases and Research are conducting clinical and medical treatments to improve the symptoms of this disorder. In most cases, children with Rett syndrome continue to develop symptoms in childhood, including difficulty with speech, swallowing, and hand and arm movements. In some cases, the disease may cause a loss of maturity, which may lead to a longer life expectancy than normal. No specific age or genetic predisposition exists for individuals affected.',
   'Few children inherit Rett syndrome: the symptoms are similar to normal neurological disorders, such as autism and cerebral palsy. As the disease progresses, symptoms may develop, including abnormalities in the brain and spinal cord, and progressive neurological deficits, such as seizures, aphasia, and delayed movement. The National Institutes of Health are conducting a life-long training course on Rett syndrome at the âR&Eâ laboratory. This is the only international research project to investigate Rett syndrome at the âE3â laboratory.',
   'Rett syndrome and medical treatment. The syndrome is a rare neurodegenerative disease. It impairs the normal development of the brain and other vital life skills. For the child with Rett syndrome, the symptoms may be different from those of any other type of neurological disorder. It is important to look for the individual with the syndrome, as soon as possible before the age of 12 months, to see if there is a cure, said Dr. Sandra R. Coss, director of the Rett Syndrome Research Institute (RiStD) & Applied Neurology (Ri',
   '(RESLET) Rett syndrome is a neurological disorder that causes some symptoms and is very rare. As a result, the knowledge of when and how an individual would suffer from the illness is important to determine the health of the patient. Neuroscience and Neurology â In our study, we examined the brains of patients with Rett syndrome, and the brains of patients with scoliosis.',
   'Rett syndrome is a rare neurological disorder. The disorder usually progresses to adulthood, and the symptoms of the disorder may continue throughout life. As the disorder progresses, children with the disorder may lose some ability to speak, grasp, and support their mother and siblings. The National Institutes of Health and the American Society for Clinical Research are developing specific therapies to treat the early signs and symptoms of Rett syndrome, including the development of early hand and arm movements.',
   'A girl with Rett syndrome develops rare neurological symptoms. These symptoms may lead to the loss of the ability to hold and grasp, and other disabilities, such as difficulty with speech and movement. The National Institutes of Health and the National Institutes of Health continue to monitor the progression of the disorder throughout life. As a result, there is no cure for Rett syndrome, although some medical and genetic treatments may be helpful in the first few years of life.',
   'The Rett syndrome is a neurological disorder, and the symptoms typically begin in infancy and progress to adulthood. In rare cases, they may develop abnormalities in the hand and fingers, which may lead to difficulty reaching and extending. The disease is a life-threatening condition, and no cure is known. I support the national and international research on the causes, symptoms, and prognosis of Rett syndrome. When children with this disorder experience symptoms, they may be asked to follow a specific course of care. Typically, they are expected to maintain normal development for at least 15 years',
   'The Rett syndrome Institute supports children with Rett syndrome through education, medical care, and lifelong learning. Rett syndrome is a rare neurological disorder. Its symptoms usually begin in infancy. As the disease progresses, symptoms may include loss of motor skills (e.g., squeezing), speech problems, and other problems. No cure exists for Rett syndrome. However, some people with the disease develop neurological symptoms before puberty. The following is a list of genes and their role in Rett syndrome. The disease is not a genetic disorder',
   'There is no cure for Rett syndrome. In children with the disease, symptoms usually occur in the mid-to-late stages of development, which may include loss of normal mobility, loss of ability to perform normal daily tasks, and difficulty with social and occupational activities. The health service IHS (National Institute of Health) also closely monitors the genetic basis of Rett syndrome, which is a rare genetic disorder related to the development of brains.']},
 {'focus_area': 'Mitochondrial neurogastrointestinal encephalopathy syndrome',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.7775529623031616,
    0.8281719088554382,
    0.7088631391525269,
    0.8049961924552917,
    0.8652077317237854,
    0.8281719088554382,
    0.8325582146644592,
    0.8530763387680054,
    0.7535783648490906,
    0.8110525012016296],
   'self_bleu': [0.48293752453528854,
    1.0,
    0.5081327481546147,
    0.6606328636027614,
    0.0,
    1.0,
    0.2978201796359045,
    0.7175852914772134,
    0.5115078115793242,
    0.691441569283882]},
  'real_data': ['What is (are) Mitochondrial neurogastrointestinal encephalopathy syndrome ?',
   'What are the symptoms of Mitochondrial neurogastrointestinal encephalopathy syndrome ?',
   'How to diagnose Mitochondrial neurogastrointestinal encephalopathy syndrome ?',
   'What are the treatments for Mitochondrial neurogastrointestinal encephalopathy syndrome ?'],
  'synthetic_data': ['What are the symptoms of mitochondrial gastrointestinal neuroendocrine syndrome ( GI neuroendocrine syndrome )?',
   'What is Mitochondrial neuroendocrine gastroenteritis syndrome?',
   'What are the symptoms of Mitochondrial neuroendocrine syndrome ( MNE-GATT-E-E-T-O-SYNDROME )?',
   'What are the symptoms of mitochondrial neurogeochondritis syndrome?',
   'What is the diagnosis of Mitochondrial encephalopathy ( neuro-gastrointestinal syndrome )?',
   'What is Mitochondrial neuroendocrine gastroenteritis syndrome?',
   'What are the treatments for Mitochondrial Neuroencephalopathy ( Mitochondrial gastroenteritis ) syndrome?',
   'What are the symptoms of mitochondrial neuroendocrine encephalopathy ( gastroenteritis ) syndrome?',
   'What are mitochondrial neuroendocrine syndrome?',
   'What are symptoms of mitochondrial neuroendocrine syndrome?']},
 {'focus_area': 'Mitochondrial neurogastrointestinal encephalopathy syndrome',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6049102544784546,
    0.5593628883361816,
    0.5598101019859314,
    0.5207103490829468,
    0.6101206541061401,
    0.574974536895752,
    0.5620838403701782,
    0.6209942698478699,
    0.5272840857505798,
    0.6113061904907227],
   'self_bleu': [0.11738735795345079,
    0.11796029245644635,
    0.08983100480809975,
    0.18656210297183662,
    0.24680713298591675,
    0.1436377555080052,
    0.2584208389512443,
    0.32123668958804386,
    0.0,
    0.0]},
  'real_data': ['Mitochondrial neurogastrointestinal encephalopathy (MNGIE) syndrome is a condition that particularly affects the digestive system and nervous system. Signs and symptoms of this condition most often begin by age 20 and worsen with time. Almost all people with MNGIE have gastrointestinal dysmotility, in which the muscles and nerves of the digestive system do not move food through the digestive tract efficiently. Affected individuals also experience peripheral neuropathy, droopy eyelids (ptosis), weakness of the muscles that control eye movement (ophthalmoplegia), and hearing loss. Leukoencephalopathy, which is the deterioration of a type of brain tissue known as white matter, is a hallmark of MNGIE; however it does not usually cause symptoms in people with this disorder. Mutations in the TYMP gene cause MNGIE, and this condition is inherited in an autosomal recessive pattern.',
   'What are the signs and symptoms of Mitochondrial neurogastrointestinal encephalopathy syndrome? The Human Phenotype Ontology provides the following list of signs and symptoms for Mitochondrial neurogastrointestinal encephalopathy syndrome. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Abdominal pain - Areflexia - Autosomal recessive inheritance - Cachexia - Constipation - Death in early adulthood - Decreased activity of cytochrome C oxidase in muscle tissue - Distal amyotrophy - Distal muscle weakness - Distal sensory impairment - Gastrointestinal dysmotility - Gastroparesis - Hypointensity of cerebral white matter on MRI - Intermittent diarrhea - Lactic acidosis - Leukoencephalopathy - Malabsorption - Malnutrition - Mitochondrial myopathy - Multiple mitochondrial DNA deletions - Progressive - Progressive external ophthalmoplegia - Ptosis - Ragged-red muscle fibers - Sensorineural hearing impairment - Subsarcolemmal accumulations of abnormally shaped mitochondria - Vomiting - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.',
   'How might mitochondrial neurogastrointestinal encephalopathy syndrome be diagnosed? The clinical diagnosis of mitochondrial neurogastrointestinal encephalopathy syndrome (MNGIE) is based on the presence of severe gastrointestinal dysmotility (when the muscles and nerves of the digestive system do not move food through the digestive tract efficiently), cachexia (wasting away of muscle and fat tissue), ptosis, external ophthalmoplegia (weakness in the muscles that control eye movement), sensorimotor neuropathy, asymptomatic leukoencephalopathy (observed on brain MRI), and a family history consistent with autosomal recessive inheritance. Direct evidence of MNGIE syndrome can be provided by one of the following:  A blood test showing an increase in plasma thymidine concentration (greater than 3 mol/L) and an increase in plasma deoxyuridine concentration (greater than 5 mol/L). This is sufficient to make the diagnosis of MNGIE disease. Thymidine phosphorylase enzyme activity in leukocytes (white blood cells) less than 10% of the control mean. Genetic testing of TYMP, the gene for thymidine phosphorylase (the enzyme deficient in individuals with MNGIE syndrome), detects mutations in approximately all of affected individuals.',
   'How might mitochondrial neurogastrointestinal encephalopathy syndrome be treated? References John M Shoffner. Mitochondrial Neurogastrointestinal Encephalopathy Disease. GeneReviews. May 11, 2010; http://www.ncbi.nlm.nih.gov/books/NBK1179/. Accessed 3/27/2011.'],
  'synthetic_data': ['What is mitochondrial neurogenic encephalopathy syndrome? PubMed Medical Reference (2010-03-10) By Andrew A. Hodges, MD, PhD, FAAN. Mitochondrial neurogenic encephalopathy syndrome could be diagnosed based on the signs and symptoms of the disease. The symptoms of the disease are usually associated with a progressive gastrointestinal disease. The NGIE gene is not found in the majority of people with mitochondrial neurogenic encephalopathy syndrome. The symptoms of the disease include a sluggish state of the stomach and a decreased ability to swallow',
   "How can the mitochondrial neuroencephalopathy syndrome be diagnosed? The symptoms of this syndrome are as follows: gastrointestinal neuroencephalopathy with gastrointestinal defecation or gastroesophageal reflux disease (GIE) based on the NIH's National Institute of Neurological Disorders and Stroke (NINOS). The NINOS is based on the NIH's National Institute of Neurological Disorders and Stroke (NINOS). The most common symptom is gastrointestinal neuroencephalopathy.",
   'What are the symptoms of mitochondrial neuroendocrine syndrome? The mitochondrial neuroendocrine syndrome (MNE) is a family of diseases that may only be diagnosed through the clinical management of the following: 1 A normal gastrointestinal tract with a spherical gastrointestinal tract that contains the atypical glial cytoplasmic cytoplasmic reticulum, atypical glial cytoplasmic reticulum, atypical glial cytoplasmic reticulum, atypical glial cytoplasmic reticulum',
   'Mitochondrial neuroendocrine encephalopathy syndrome How is this syndrome diagnosed and treated? References by John A. Gould, M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., M.D., and M.D. Signs and symptoms may',
   'Mitochondrial neuroendocrine encephalopathy syndrome is referred to in the medical literature as mitochondrial gastroenteritis syndrome. This syndrome is diagnosed and treated by a series of tests based on the following symptoms: Probable weakness of the muscles of the gastrointestinal tract. Probable loss of muscle tone in the gastrointestinal tract. How often does a person with MNGIE syndrome show signs and symptoms? The first sign and symptoms of MNGIE syndrome may not be present in all individuals with the same gene for the phenotype of a person with the same.',
   'What is mitochondrial neuroencephalopathy syndrome? Diagnosis of mitochondrial neuroencephalopathy syndrome is determined by a series of gastrointestinal symptoms, such as intestinal enlargement, muscle weakness, and gastrointestinal tract disease. How can mitochondrial neuroencephalopathy syndrome be treated? References for IGNE by John DePuy, MD, MPH, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB, AB.',
   'What is Mitochondrial Neuroencephalopathy Syndrome? RefGoogle Health. By John P. Ogilvie, M.D., and John P. Ogilvie, M.D. Gastrointestinal symptoms may be diagnosed and treated on the basis of symptoms of impaired endocrine, endocrine, or endocrine activity in the gastrointestinal tract. The MHNE gene does not appear in all people with this condition. The probability of developing a rare, severe, or chronic condition is less than 1% in the first 5 years of life.',
   'Mitochondrial neuroenzyme encephalopathy syndrome How can the syndrome be diagnosed and treated? References by Johns Hopkins Medicine and the National Institutes of Health (NIH) The first sign of this syndrome is the presence of symptoms of gastroparesis or weakness of the gastrointestinal tract. The symptoms of MNGIE may be a combination of the following: Decreased muscle tone in the legs and feet. Decreased muscle tone in the thoracic/abdominal area. People with this condition are more likely to have a genetic mutation in the.',
   'If the syndrome is transmitted through the gastrointestinal tract, it must be reversible. Mitochondrial encephalopathy of neurons (MENG) syndrome. MENG syndrome: Symptoms similar to those of MENG syndrome. MENG syndrome: Symptoms of MENG syndrome. MENG syndrome: Symptoms of MENG syndrome. MENG syndrome: Symptoms of MENG syndrome. MENG syndrome: Symptoms of MENG syndrome. MENG syndrome: Symptoms of MENG syndrome.',
   'What is mitochondrial neuroenzyme encephalopathy syndrome? The diagnosis of MNEG syndrome is determined through a family history of intestinal or gastrointestinal disorders. The frequency of symptoms may be increased in people with a genetic mutation. See the related links below. Symptoms of mitochondrial neuroenzyme encephalopathy syndrome. â Allergy to the intestines may be seen in people with MNEG syndrome. â Muscle and vision dysfunction may be seen in people with MNEG syndrome. â Neurological deficits may not be seen.']},
 {'focus_area': 'Familial mixed cryoglobulinemia',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.885451078414917,
    0.8025428056716919,
    0.8254721760749817,
    0.8015327453613281,
    0.8706623315811157,
    0.9537076950073242,
    0.8518168330192566,
    0.885451078414917,
    0.9892536401748657,
    0.9892536401748657],
   'self_bleu': [1.0,
    0.6803749333171202,
    0.4412484512922977,
    0.6997522298221912,
    0.8344522897223012,
    0.8739351325046805,
    0.0,
    1.0,
    1.0,
    1.0]},
  'real_data': ['What is (are) Familial mixed cryoglobulinemia ?',
   'What are the symptoms of Familial mixed cryoglobulinemia ?'],
  'synthetic_data': ['What is Familial mixed cryoglobulinemia ( symptoms )?',
   'What is Familial mixed cryoglobulinemia ( Cryoglobulinemia )?',
   'What is Familial mixed antibody-cryoglobulinemia ( symptoms )',
   'What are the symptoms of Familial mixed cryoglobulinemia (Family mixed cryoglobulinemia )?',
   'What are the symptoms of Familial mixed cryoglobulinemia ( cryoglobulinemia )?',
   'What are the symptoms of Familial mixed cryoglobulinemia ( )?',
   'What is the Familial mixed symptoms of Cryoglobulinemia ( )',
   'What is Familial mixed cryoglobulinemia ( symptoms )?',
   'What are the symptoms of Familial mixed cryoglobulinemia?',
   'What are the symptoms of Familial mixed cryoglobulinemia?']},
 {'focus_area': 'Familial mixed cryoglobulinemia',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6880764365196228,
    0.6304507255554199,
    0.6296831369400024,
    0.6298421025276184,
    0.5356323719024658,
    0.6213666200637817,
    0.5993555784225464,
    0.6249692440032959,
    0.665592610836029,
    0.5741549134254456],
   'self_bleu': [0.29790808438073174,
    0.3496525236255194,
    0.34335358150232664,
    0.24993860013211197,
    0.0,
    0.2437891264665907,
    0.3829038426693521,
    0.3072654058209713,
    0.3131588024571973,
    0.0]},
  'real_data': ['Familial mixed cryoglobulinemia is a rare condition that is characterized by the presence of abnormal proteins (called cryoglobulins) in the blood. These proteins clump together into a "gel-like" consistency at low temperatures, which can lead to inflammation, blocked blood vessels, and a variety of health problems. The associated signs and symptoms vary from person to person depending on which parts of the body or organ systems are affected; however, common features include purpura, joint pain, breathing problems, muscle pain, fatigue, glomerulonephritis, Raynaud\'s phenomenon, and skin abnormalities. The underlying genetic cause of familial mixed cryoglobulinemia is currently unknown. Although there are only a few reported families with this condition, it appears to be inherited in an autosomal dominant manner. Treatment is based on the signs and symptoms present in each person. In severe cases, medications that suppress the immune system may be necessary.',
   'What are the signs and symptoms of Familial mixed cryoglobulinemia? The Human Phenotype Ontology provides the following list of signs and symptoms for Familial mixed cryoglobulinemia. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Abnormality of temperature regulation 90% Acrocyanosis 90% Mediastinal lymphadenopathy 90% Skin ulcer 90% Subcutaneous hemorrhage 90% Vasculitis 90% Abdominal pain 50% Arthralgia 50% Arthritis 50% Gangrene 50% Gastrointestinal infarctions 50% Glomerulopathy 50% Hematuria 50% Hepatic failure 50% Hepatomegaly 50% Myalgia 50% Polyneuropathy 50% Proteinuria 50% Renal insufficiency 50% Splenomegaly 50% Gastrointestinal hemorrhage 7.5% Keratoconjunctivitis sicca 7.5% Abnormality of blood and blood-forming tissues - Anasarca - Autosomal dominant inheritance - Chronic kidney disease - Cryoglobulinemia - Elevated serum creatinine - Hypertension - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.'],
  'synthetic_data': ['Familial mixed cryoglobulinemia is a condition characterized by abnormalities in the human globulin protein. The name of the disease is derived from the Greek word cryo meaning thrombus. The symptoms and signs of familial mixed cryoglobulinemia appear in a subset of people. The frequency and severity of these symptoms depends on the type of disease and the time of life. Symptoms usually improve gradually over time and may include a rise in blood pressure, numbness, and joint pain. The following table lists symptoms and signs associated with ',
   'Mixed globulinemia or familial cryoglobulinemia means that the symptoms of mixed globulinemia are characterized by the presence of a protein called globulin. The frequency of these symptoms is listed below. The number of people with mixed globulinemia or familial cryoglobulinemia is estimated to be around 5% of the population. The symptoms and signs of mixed globulinemia or familial cryoglobulinemia are listed below. 1 Abdominal pain and swelling. 2 Fatigue. 3 Freeze-ups. 4 Diabetes',
   'Familial mixed cryoglobulinemia is characterized by the following symptoms and signs: Abnormality of the proteins on the surface of cryoglobulins in the blood. This condition is usually asymptomatic and may cause chronic pain, swelling, and/or a blockage of the blood vessels. The frequency of symptoms and signs is based on the number of people with this condition and how many of them have it. The frequency of symptoms and signs is based on the number of people with this condition and how many of them have it. The human phenotype is used.',
   "Family-associated mixed cryoglobulinemia is characterized by the following symptoms: The frequency of symptoms is very rare, meaning that a person's symptoms are affected on a per-tenth basis. The symptom is a combination of the abnormal protein globulin, the presence of a cytoplasmic abnormality, the presence of a hematogenous abnormality, and the presence of a natriuretic abnormality. The article below lists the symptoms, causes, and treatment options for the symptoms, as well as how to diagnose the condition.",
   'Family First Claudication. Mixed claudication is claudication due to a mutation in the proteins of cryoglobulin. The symptom frequencies are listed below and the occurrence is listed in the symptom description. There are rare or severe symptomatic disorders, including cold extremities, fibromyalgia, and a distorted view of the limbs. The occurrence is listed below and the occurrence is listed in the symptom description. There are rare or severe symptomatic disorders, including cold extremities, fibromyalgia, and',
   'Mixed globulinemia is a symptom or sign of familial cryoglobulinemia. The information provided helps diagnose the condition and determine how often people with this condition get these symptoms. The first digit represents the expected frequency of these symptoms. There may be a pattern of symptoms in the following categories: Pain or discomfort in the affected area, hepatocellular abnormalities, gastrointestinal abnormalities, gastrointestinal bleeding, swollen lymph nodes, and edema. The classification of familial cryoglobulinemia based on the number of signs and symptoms.',
   'Family mixed cryoglobulinemia is a condition characterized by the following signs and symptoms. The frequency of these symptoms is based on the number of people with the condition and the time between the onset of symptoms and the onset of symptoms. For more information, see the Symptoms and Signs section. The symptom categories are categorized by the frequency of the first symptom. Onset of symptoms is unknown, but the presence of a hyaluronic acid antibody in the blood, serum, or other body fluids causes the symptoms. In the advanced stages, the condition.',
   'Familial mixed cryoglobulinemia is a phenotype characterized by the abnormal protein on the plasma membrane. The following table lists the signs and symptoms of the condition, according to the Random House Human Genome Research Project. The frequency of these symptoms is listed below: People with the condition have a lower chance of having the condition. Signs and symptoms may include joint pain, hematomas, or vascular abnormalities. The time intervals for diagnosis of these conditions are listed below. The condition may be associated with other conditions, such as autoimmune disorders, or other conditions.',
   'Symptoms of Familial mixed cryoglobulinemia are a set of signs and symptoms that are usually associated with the condition. The number of signs and symptoms listed under the heading Familial mixed cryoglobulinemia is based on the frequency and type of people with this condition and the number of times between the first occurrence and the last occurrence. The rare condition is thought to cause abnormalities in the glomerular filtration rate, which is the amount of protein found in the blood. This may cause lower blood pressure, joint pain, and swelling of the joints. The Human Geno',
   'Cryoglobulinemia is a (familial) globulin disorder. Cryoglobulinemia is a rare, but disabling, condition. When diagnosed, these symptoms are usually seen on blood tests. How did Family Speciation Associated With Mixed Manifestations Cause The Patient to Have Mixed Manifestations? Family History of Manifestations Caused by Manifestations Caused by Manifestations Caused by Manifestations Caused by Manifestations Caused by Manifestations. Manifestations Caused by Manifestations Caused by ']},
 {'focus_area': 'Stormorken syndrome',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8266147375106812,
    0.6625737547874451,
    0.8050306439399719,
    0.8086466193199158,
    0.8044683337211609,
    0.8086466193199158,
    0.7833022475242615,
    0.8086466193199158,
    0.8141359686851501,
    0.7373102903366089],
   'self_bleu': [0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0, 1.0, 0.0, 0.0]},
  'real_data': ['What is (are) Stormorken syndrome ?',
   'How many people are affected by Stormorken syndrome ?',
   'What are the genetic changes related to Stormorken syndrome ?',
   'Is Stormorken syndrome inherited ?',
   'What are the treatments for Stormorken syndrome ?'],
  'synthetic_data': ['What are Stormerkoen syndrome?',
   'One Stormkroken syndrome is affected?',
   'What is Stormyk syndrome?',
   'What are Stormkroken syndrome?',
   'What is the Stormkroken syndrome?',
   'What are Stormkroken syndrome?',
   'What are Stormyken syndrome?',
   'What are Stormkroken syndrome?',
   'What is Stormerkoen syndrome?',
   'What are Stormy-Stroken syndrome?']},
 {'focus_area': 'Stormorken syndrome',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6450302600860596,
    0.6115885972976685,
    0.6209983229637146,
    0.6140073537826538,
    0.5528497099876404,
    0.6009929180145264,
    0.6097237467765808,
    0.6114602088928223,
    0.6157582402229309,
    0.6441615223884583],
   'self_bleu': [0.26186891787583505,
    0.0,
    0.3250787209424579,
    0.0,
    0.1716428084959482,
    0.22028153707343084,
    0.27597039002839535,
    0.10238827582150535,
    0.2879472636904447,
    0.47318776004173563]},
  'real_data': ['Stormorken syndrome is a rare condition that affects many body systems. Affected individuals usually have thrombocytopenia, in which there are abnormally low numbers of blood cells called platelets. Platelets are involved in normal blood clotting; a shortage of platelets typically results in easy bruising and abnormal bleeding. In addition, affected individuals often have a muscle disorder, called tubular aggregate myopathy, that leads to muscle weakness. Another feature of Stormorken syndrome is permanent constriction of the pupils of the eyes (miosis), which may be caused by abnormalities in the muscles that control the size of the pupils. Other features include lack of a functioning spleen (asplenia), scaly skin (ichthyosis), headaches, and difficulty with reading and spelling (dyslexia).',
   'Stormorken syndrome is a rare disorder. Approximately a dozen cases have been reported in the medical literature.',
   'Stormorken syndrome is caused by a mutation in the STIM1 gene. The protein produced from this gene is involved in controlling the entry of positively charged calcium atoms (calcium ions) into cells. The STIM1 protein recognizes when calcium ion levels are low and stimulates the flow of ions into the cell through special channels in the cell membrane called calcium-release activated calcium (CRAC) channels. The flow of calcium ions through CRAC channels triggers signaling within cells that helps control gene activity, cell growth and division, and immune function.  The STIM1 gene mutation involved in Stormorken syndrome leads to production of a STIM1 protein that is constantly turned on (constitutively active), which means it continually stimulates calcium ion entry through CRAC channels regardless of ion levels. Researchers suggest that the abnormal ion flow in platelets causes the cells to die earlier than usual, leading to thrombocytopenia and bleeding problems in people with Stormorken syndrome. It is unknown how constitutively active STIM1 leads to the other features of the disorder.',
   'This condition is inherited in an autosomal dominant pattern, which means one copy of the altered gene in each cell is sufficient to cause the disorder. In some cases, an affected person inherits the mutation from one affected parent. Other cases result from new mutations in the gene and occur in people with no history of the disorder in their family.',
   'These resources address the diagnosis or management of Stormorken syndrome:  - Genetic Testing Registry: Stormorken syndrome   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care'],
  'synthetic_data': ['Stormkoen syndrome is a musculoskeletal disorder. It requires a mutation in the OMIM1 gene. This gene is involved in the regulation of blood cell production. Only one copy of each chromosome is required in each case. This condition is rare and usually affects only a few people at a time [source: Molecular Biology ]. The following resources provide a comprehensive overview of the symptoms, causes, and diagnosis of this disorder.',
   'Stormorn syndrome is a mutated condition, which means that a total of 1 copy of the mRNA is required for normal blood clotting and cellular repair. People with this disorder also have a low incidence of other inherited disorders. (This resource provides information about possible causes and treatments of Stormorn syndrome in general)',
   'Stormkronen syndrome accounts for a rare disorder in which at least one copy of the Meyer gene is affected in each affected individual. In these cases, mutations in the cellular and cellular physiology are obstructing the normal course of the body. The following resources are available to help with diagnosis, treatment and management of this condition.',
   'Warkenstein syndrome is inherited in which each copy of the Stormenstein gene is mutated (see Stormenstein Syndrome Molecular Pathology and Molecular Biology Research). It is a rare condition for which patients have autosomal recessive disorders of the hepatic and kidney cells. The data in this article provide a snapshot of the clinical course for the disorder and the information that can be used to help you make informed decisions about treatment.',
   "Stormenkirk syndrome (or stormenkirk endocrine syndrome) is a genetic disorder. It is caused by mutations in the gene that is involved in the production of certain hormones. Only one copy is needed for the disorder to be diagnosed. The disorder affects your body's tissues. 1 Symptoms. 2 Diagnosis. 3 Symptoms. 4 Symptoms. 5 Symptoms. 6 Symptoms. 7 Symptoms. 8 Symptoms. 9 Symptoms. 10 Symptoms. 11 Symptoms. 12 Symptoms. 13",
   'Medical professionals are required to rule out Stormkrm-Mohr syndrome, according to the Diagnostic and Statistical Manual of Mental Disorders, available from the National Institutes of Health (NIH). This rare condition is a congenital disorder that occurs in adolescence. At least one copy of each gene is affected in each case. Blood tests are available for cases of Stormkrm-Mohr syndrome. These tests look for a number of different inherited mutations that can cause symptoms, including: 1 Inhibition of the production of skeletal ',
   'Stormerkorian syndrome is a chromosomal disorder. This means that only one copy of the affected gene is present in each person. The affected gene is responsible for the production of certain proteins that regulate the activity of certain cellular processes (such as vascular and blood clotting). These mutations are unlikely to cause symptoms; however, they may be a result of a genetic defect. For more information on the diagnosis and treatment of Stormerkorian syndrome, please visit the American Academy of Neurology (AAS).',
   'Smtrkn syndrome usually occurs in a family, and a gene that controls this condition is also documented in the online medical journal MedlinePlus.com, and a condition that is so rare that only a few individuals have this condition, and if the condition is a result of a blood disorder, the exact cause of the condition may be unknown (Dawley et al., 2007; p. 111)',
   'It is a disorder caused by an isolated mutation in the Stormkroken gene, which results in normal cell proliferation and a decrease in platelet count. In general, only one copy of each gene is reported in each case. The following resources from the MD Anderson Cancer Center help to address these genetic disorders in people with a chronic condition.',
   'A number of publications are available about Stormkroken syndrome, which is a genetic disorder caused by a recessive mutation in the marrow cells gene. In these cases, only one copy of the affected gene is present in each person. This condition usually requires diagnostic tests and other intervention in the body.']},
 {'focus_area': 'keratoderma with woolly hair',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8571504950523376,
    0.8146741390228271,
    0.7629620432853699,
    0.8607190847396851,
    0.8328554034233093,
    0.8778016567230225,
    0.6459608674049377,
    0.8335347175598145,
    0.8335347175598145,
    0.7022001147270203],
   'self_bleu': [0.5081327481546147,
    0.3655552228545123,
    0.3303164318013807,
    0.43472087194499137,
    0.42728700639623407,
    0.488923022434901,
    0.0,
    1.0,
    1.0,
    0.0]},
  'real_data': ['What is (are) keratoderma with woolly hair ?',
   'How many people are affected by keratoderma with woolly hair ?',
   'What are the genetic changes related to keratoderma with woolly hair ?',
   'Is keratoderma with woolly hair inherited ?',
   'What are the treatments for keratoderma with woolly hair ?'],
  'synthetic_data': ['What is keratopathy with woolly hair?',
   'What keratoderma changes are affected with woolly hair?',
   'How many keratopathy are there with woolly hair?',
   'What is keratoderma ( genetic ) with woolly hair?',
   'What are keratodermas related with woolly hair?',
   'What are Keratodermatitis with woolly hair?',
   'What is woolly hair in a Keratinized Poodle that you are a hair with a hair that is not genetically affected?',
   'What are keratoderma ( genetic changes related to woolly hair )?',
   'What are keratoderma ( genetic changes related to woolly hair )?',
   'What are the people with keratoderma periderm?']},
 {'focus_area': 'keratoderma with woolly hair',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5804358720779419,
    0.5838844180107117,
    0.5782971382141113,
    0.5903693437576294,
    0.5003352165222168,
    0.6053277850151062,
    0.6154000163078308,
    0.534894585609436,
    0.5876151323318481,
    0.6139659285545349],
   'self_bleu': [0.3158771760674862,
    0.29047193815967304,
    0.3399268834441225,
    0.290978544644872,
    0.0,
    0.21391165769964657,
    0.2608627591005193,
    0.0,
    0.22169194554222996,
    0.3107074296942318]},
  'real_data': ['Keratoderma with woolly hair is a group of related conditions that affect the skin and hair and in many cases increase the risk of potentially life-threatening heart problems. People with these conditions have hair that is unusually coarse, dry, fine, and tightly curled. In some cases, the hair is also sparse. The woolly hair texture typically affects only scalp hair and is present from birth. Starting early in life, affected individuals also develop palmoplantar keratoderma, a condition that causes skin on the palms of the hands and the soles of the feet to become thick, scaly, and calloused.  Cardiomyopathy, which is a disease of the heart muscle, is a life-threatening health problem that can develop in people with keratoderma with woolly hair. Unlike the other features of this condition, signs and symptoms of cardiomyopathy may not appear until adolescence or later. Complications of cardiomyopathy can include an abnormal heartbeat (arrhythmia), heart failure, and sudden death.  Keratoderma with woolly hair comprises several related conditions with overlapping signs and symptoms. Researchers have recently proposed classifying keratoderma with woolly hair into four types, based on the underlying genetic cause. Type I, also known as Naxos disease, is characterized by palmoplantar keratoderma, woolly hair, and a form of cardiomyopathy called arrhythmogenic right ventricular cardiomyopathy (ARVC). Type II, also known as Carvajal syndrome, has hair and skin abnormalities similar to type I but features a different form of cardiomyopathy, called dilated left ventricular cardiomyopathy. Type III also has signs and symptoms similar to those of type I, including ARVC, although the hair and skin abnormalities are often milder. Type IV is characterized by palmoplantar keratoderma and woolly and sparse hair, as well as abnormal fingernails and toenails. Type IV does not appear to cause cardiomyopathy.',
   'Keratoderma with woolly hair is rare; its prevalence worldwide is unknown.  Type I (Naxos disease) was first described in families from the Greek island of Naxos. Since then, affected families have been found in other Greek islands, Turkey, and the Middle East. This form of the condition may affect up to 1 in 1,000 people from the Greek islands.  Type II (Carvajal syndrome), type III, and type IV have each been identified in only a small number of families worldwide.',
   'Mutations in the JUP, DSP, DSC2, and KANK2 genes cause keratoderma with woolly hair types I through IV, respectively. The JUP, DSP, and DSC2 genes provide instructions for making components of specialized cell structures called desmosomes. Desmosomes are located in the membrane surrounding certain cells, including skin and heart muscle cells. Desmosomes help attach cells to one another, which provides strength and stability to tissues. They also play a role in signaling between cells.  Mutations in the JUP, DSP, or DSC2 gene alter the structure and impair the function of desmosomes. Abnormal or missing desmosomes prevent cells from sticking to one another effectively, which likely makes the hair, skin, and heart muscle more fragile. Over time, as these tissues are exposed to mechanical stress (for example, friction on the surface of the skin or the constant contraction and relaxation of the heart muscle), they become damaged and can no longer function normally. This mechanism probably underlies the skin, hair, and heart problems that occur in keratoderma with woolly hair. Some studies suggest that abnormal cell signaling may also contribute to cardiomyopathy in people with this group of conditions.  Unlike the other genes associated with keratoderma with woolly hair, the KANK2 gene provides instructions for making a protein that is not part of desmosomes. Instead, it regulates other proteins called steroid receptor coactivators (SRCs), whose function is to help turn on (activate) certain genes. SRCs play important roles in tissues throughout the body, including the skin. Studies suggest that mutations in the KANK2 gene disrupt the regulation of SRCs, which leads to abnormal gene activity. However, it is unclear how these changes underlie the skin and hair abnormalities in keratoderma with woolly hair type IV.',
   'Most cases of keratoderma with woolly hair have an autosomal recessive pattern of inheritance, which means both copies of the gene in each cell have mutations. The parents of an individual with an autosomal recessive condition each carry one copy of the mutated gene, but they usually do not show signs and symptoms of the condition.',
   'These resources address the diagnosis or management of keratoderma with woolly hair:  - Gene Review: Gene Review: Arrhythmogenic Right Ventricular Dysplasia/Cardiomyopathy  - Gene Review: Gene Review: Dilated Cardiomyopathy Overview  - Genetic Testing Registry: Arrhythmogenic right ventricular cardiomyopathy, type 11  - Genetic Testing Registry: Cardiomyopathy, dilated, with woolly hair, keratoderma, and tooth agenesis  - Genetic Testing Registry: Naxos disease  - Genetic Testing Registry: Palmoplantar keratoderma and woolly hair  - National Heart, Lung, and Blood Institute: How is Cardiomyopathy Diagnosed?  - National Heart, Lung, and Blood Institute: How is Cardiomyopathy Treated?   These resources from MedlinePlus offer information about the diagnosis and management of various health conditions:  - Diagnostic Tests  - Drug Therapy  - Surgery and Rehabilitation  - Genetic Counseling   - Palliative Care'],
  'synthetic_data': ['Dermatokeratosis with woolly hair is diagnosed in most families with the disorder. The National Institute of Health (NIH) provides a detailed description of the conditions Keratokeratosis with woolly hair: 1 Type I and II are recessive, meaning that each gene has a different sequence of DNA. 2 This gene may be missing or not working properly. These abnormalities may affect the heart, lungs, and other organs. 2 Several genes are associated with the symptoms of Keratokeratosis with woolly hair, but only one causes',
   'Keratodermal dermatosis is diagnosed with woolly hair syndrome. The XYZ gene is involved in regulating hair growth and development. The XYZ gene is present in two different types of keratodermal dermatosis: type I and type II. 1 Most people with keratodermal dermatosis have a family history of the condition. 2 However, a few people with keratodermal dermatosis develop a life-threatening condition. 3 The following information summarizes the causes, symptoms,',
   'Keratodermal wavy hair is diagnosed with relatives with either type I or type II keratodermal wavy hair.  The XYZ gene is responsible for most keratodermal wavy hair.  The disease is a rare condition, but it is not well understood.  The XYZ gene mutations that cause keratodermal wavy hair appear to affect the heart, skin, and nervous system.  People with keratodermal wavy hair are usually diagnosed with one or more symptoms',
   'Keratodermatosis with woolly hair is diagnosed when both parents have a dilated scrotum.  The DRV1 gene is responsible for keratodermatosis type I and keratodermatosis type II.  The DRV1 gene is absent from most people with keratodermatosis with woolly hair.  The disease is rare, but it may affect the body in different ways.  The following table summarizes life-long conditions associated with keratodermatosis',
   ' The keratodermal hair is described in terms of the type of keratodermal hair:  The disease is diagnosed by a recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent recurrent.',
   'Keratodermal woolopathy is diagnosed with hair or wooly skin. Most cases of keratodermal woolopathy are type I, with a recessive gene that affects the mitochondrial and vascular system.  The condition is uncommon in people with a single gene mutation.  The condition is present in at least two families.  The genes involved in keratodermal woolopathy are not well understood.  The following information summarizes the clinical characteristics of keratodermal woolopathy, including possible causes',
   '1 The Genome Review at right provides an overview of the various conditions associated with woolly hair:  Keratoderma with asymmetrical keratinization, or keratoderma, is a rare disease that affects the heart and blood vessels.  In most cases, the genes for keratoderma and keratoderma are recessive, so that each person inherits one copy of the abnormal gene from each parent.  Two types of keratoderma, type I and type II, are not associated with the same symptoms.',
   'The word âkeratosisâ is from the mitochondrial DNA of the neoplasmic reticulum; the âWolfâs diseaseâ is from the mitochondrial DNA of the neoplasmic reticulum. There are other types of hairy-dermatosis with the same gene but with a different mechanism. Care should be taken in all affected persons with a typical âKeratosis IIâ and âWolfâs diseaseâ syndrome.',
   'The resources on this page provide a general overview of Keratoderma with woolly hair:  Kardasi syndrome type I and type II are diagnosed in families with at least one of the following conditions:  Kardasi syndrome type II is recessive, but the gene that controls the gene that controls the gene that controls the gene that controls the gene that controls the gene for the protein xyrosine kinase is missing.  In most cases, the disorder affects the heart and circulatory system, causing symptoms and other life-threatening complications.',
   'A systematic review of the conditions is provided by the Kardoo Diseases and Dermatophytes Association of Australia: 1 Keratodermal type I and Keratodermal type II with woolly hair are diagnosed in most people with the disorder. 2 The underlying gene mutations that cause this condition are unknown. 3 The resulting mutations can affect the heart, lungs, and other organs. 4 The resulting mutations may be recessive, meaning that the parents may inherit the same gene for each gene, but the resulting mutations are not always present.']},
 {'focus_area': 'Severe combined immunodeficiency',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8128305077552795,
    0.7253809571266174,
    0.7704088091850281,
    0.8810354471206665,
    0.6878116130828857,
    0.8427348732948303,
    0.7214787602424622,
    0.7382015585899353,
    0.8810354471206665,
    0.8119080066680908],
   'self_bleu': [0.9193227152249185,
    0.30576902884505114,
    0.44833867003844585,
    1.0,
    0.0,
    0.9193227152249185,
    0.0,
    0.32559641262003014,
    1.0,
    0.7825422900366437]},
  'real_data': ['What is (are) Severe combined immunodeficiency ?',
   'Is Severe combined immunodeficiency inherited ?',
   'How to diagnose Severe combined immunodeficiency ?'],
  'synthetic_data': ['Is Severe combined immunodeficiency ( inherited immunodeficiency )?',
   'Question - is Severe combined immunodeficiency ( ISD, CDK, safaectin)?',
   'What is Severe combined immunodeficiency? ( Inheritance by two PDEs )',
   'What is Severe combined immunodeficiency?',
   'Is Severe interstitial immunodeficiency ( idiopathic ) an immunodeficiency?',
   'What is Severe combined immunodeficiency ( inherited )?',
   "What is 'Severe Immunodeficiency' if I combine sex and inherited immunodeficiency for diagnosis and monitoring?",
   'What is a combined immunodeficiency ( inherited ) Severe Severe Immunodeficiency Syndrome is?',
   'What is Severe combined immunodeficiency?',
   'Is Severe combined immunodeficiency (inherited immunodeficiency ) diagnose?']},
 {'focus_area': 'Severe combined immunodeficiency',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.6659555435180664,
    0.6722034811973572,
    0.6120599508285522,
    0.651154637336731,
    0.6054239869117737,
    0.5929700136184692,
    0.6292343735694885,
    0.6605289578437805,
    0.616744339466095,
    0.6754581332206726],
   'self_bleu': [0.23733471411762594,
    0.21000069303300464,
    0.331080590336906,
    0.2788952837890295,
    0.0,
    0.0,
    0.39520756960960846,
    0.15896130700704464,
    0.1708220136783451,
    0.2547783287277049]},
  'real_data': ['Severe combined immunodeficiencies (SCID) are inherited immune system disorders characterized by abnormalities with responses of both T cells and B cells (specific types of white blood cells needed for immune system function). Common signs and symptoms include an increased susceptibility to infections including ear infections; pneumonia or bronchitis; oral thrush; and diarrhea. Due to recurrent infections, affected children do not grow and gain weight as expected (failure to thrive). SCID may be caused by mutations in any of several genes and can be inherited in an X-linked recessive (most commonly) or autosomal recessive manner. The most effective treatment is transplantation of blood-forming stem cells from the bone marrow of a healthy person. Without treatment, affected children rarely live past the age of two.',
   "How is severe combined immunodeficiency inherited? Severe combined immunodeficiency (SCID) can be inherited in an X-linked recessive or autosomal recessive manner depending on the genetic cause of the condition. X-linked SCID is the most common type of SCID and is inherited in an X-linked recessive manner. A condition is X-linked if the changed (mutated) gene responsible for the condition is located on the X chromosome. The X chromosome is one of the two sex chromosomes; females have two X chromosomes and males have one X chromosome and one Y chromosome. In males, one mutated copy of the responsible gene causes signs and symptoms of the condition because they don't have another X chromosome with a working copy of the gene. In females, having one mutated copy of the gene would make them an unaffected carrier; a mutation would have to occur in both copies of the gene to cause the condition. This is why X-linked recessive disorders, including X-linked SCID, occur much more frequently in males. Because fathers only pass their Y chromosome on to their sons, fathers cannot pass X-linked conditions on to their sons. The other, less common causes of SCID are inherited in an autosomal recessive manner. These types are due to mutations in responsible genes on other chromosomes (not the sex chromosomes). In autosomal recessive conditions, a person must have mutations in both copies of the responsible gene in order to have signs or symptoms of the condition. In most cases, the affected person inherits one mutated copy of the gene from each of the parents, who are typically unaffected carriers.",
   'How is severe combined immunodeficiency (SCID) diagnosed? A diagnosis of severe combined immunodeficiency (SCID) may be suspected if a baby shows any of the following persistent symptoms within the first year of life: Eight or more ear infections Two or more cases of pneumonia Infections that do not resolve with antibiotic treatment for two or more months Failure to gain weight or grow normally Infections that require intravenous antibiotic treatment Deep-seated infections, such as pneumonia that affects an entire lung or an abscess in the liver Persistent thrush in the mouth or throat A family history of immune deficiency or infant deaths due to infections Diagnosis can be confirmed by blood tests. Blood tests show significantly lower-than-normal levels of T cells and antibodies.   For further details on diagnosis see the following Web pages: The Primary Immunodeficiency Resource Center provides further details regarding diagnosis of SCID. Click on the embedded link to view the page. An article from Medscape Reference provides detailed information on the diagnosis of SCID. Click on eMedicine Journal to view the page. You may need to register to view the article, but registration is free.'],
  'synthetic_data': ['How are severe combined immunodeficiency syndromes (SCID) diagnosed? SCID is inherited in a recessive or X-linked manner. The condition occurs in babies with a deficiency of one or more of the ten required genes for producing a type of immune response, usually in the T cells. The condition is usually inherited from parents. Severe infections in the body may result from abnormalities in the production of white blood cells and other immune system cells. Most people with severe infections do not have symptoms of the condition. Please see the related pages for more',
   'Severe combined immunodeficiency syndrome is diagnosed on the following page. Typically, SCD is inherited as a recessive condition, caused by a deficiency of two types of immune cells (called X-linked or X-linked). In males, a blood test is required to diagnose SCD. Symptoms of SCD include infections of the gastrointestinal tract and thrush (infection of the intestines). Because of the lack of normal immune responses, infants with SCD do not respond to conventional treatment.',
   'Severe combined immunodeficiency syndrome (SCID) is diagnosed in two ways: A condition characterized by inherited abnormalities of the X chromosomes. The most common causes of SCID are infections of the lungs or other blood-related tissues. The symptoms of SCID are usually not reversible after the child is born. A condition characterized by inherited abnormalities of the X chromosomes. The symptoms of SCID can be inherited from both parents. For more information, see the topic titled Can I inherit SCI',
   'Severe combined immunodeficiency syndrome (SCID) can be diagnosed by examining the blood and a monthly X-linked immunoassay. The condition is suspected to be inherited as an autosomal recessive disorder. In babies, symptoms may include: Infections are more likely because of mutations in one of the two X chromosomes. Infections are more likely because of abnormalities in the T cell type of the immune system. Infections may also occur because of a lack of normal white blood cell and a lack of normal.',
   'High levels of recombinant and clonal immune deficiency genes. Recombinant and clonal immune deficiency (SID) syndrome is diagnosed in a number of ways, but is most commonly caused by a lack of thymocytes in the lungs or liver.',
   'A severe and life-threatening condition known as combined immunodeficiency is diagnosed in children with CIDH (associated with a type of inherited immunodeficiency called X-linked recessiveness) based on the results of a series of tests. CIDH can be due to a variety of causes but not all are inherited.  Symptoms in CIDH are similar to those in normal individuals.  Infections occur but the immune system cannot respond to the cells.  Symptoms in CIDH are absent.',
   'How is severe combined immunodeficiency syndrome (SCID) diagnosed? SCID can be inherited as a recessive or an inherited condition characterized by abnormalities in the immune system. The most common causes of SCID are mutations in one or more genes on the X chromosome. Infants with SCID need two types of T cells to thrive. The first type of T cell does not respond well to antibiotics. The second type of T cell does not respond well to antibiotics. See the related links below for more information about SCID. See also: 1 ',
   'How is SCIDS inherited? Severe combined immunodeficiency syndrome (SCIDS) is a condition in which the immune system is not able to fight infections as well as normal cells. Infections can be caused by a mutation in the X-linked recessive gene or by a combination of both genes. Infections with a specific type of clotting factor, such as thalassemia, are the most common comorbidity in children with SCIDS. See the section on inherited immunodeficiency in the FAQ',
   'SCIDC is inherited as a combination of severe and severe infections caused by abnormally high levels of immune system-dependent (IGD) T cells in the body. To diagnose SCIDC, the National Institutes of Health (NIH) requires the following tests: X-rays of the limbs and a blood test for normal or abnormal X-linked genes. Symptoms of SCIDC may also be inherited as a recessive trait. How are you sure if the child is showing signs of SCIDC? Symptoms of SCIDC may',
   'Severe combined immunodeficiency syndrome (SCD) can be diagnosed as an inherited condition characterized by the following symptoms: In most cases, the cause of the symptoms is either X-linked recessive or autosomal recessive. Infants with SCD are at risk for infections of the thymus and other blood cells. The baby does not receive normal amounts of white blood cells from the fetus or a parent with SCD. This type of abnormality requires treatment with antibiotics. For more information on how to diagnose and treat SCD,']},
 {'focus_area': 'Focal dermal hypoplasia',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.9443359971046448,
    0.6351470947265625,
    0.9261305928230286,
    0.9739002585411072,
    0.884731650352478,
    0.7141185402870178,
    0.7517271637916565,
    0.8687989711761475,
    0.6594805717468262,
    0.9739002585411072],
   'self_bleu': [0.6756000774035172,
    0.0,
    0.0,
    1.0,
    0.5623413251903491,
    0.0,
    0.0,
    0.34987611491109566,
    0.0,
    1.0]},
  'real_data': ['What is (are) Focal dermal hypoplasia ?',
   'What are the symptoms of Focal dermal hypoplasia ?',
   'Is Focal dermal hypoplasia inherited ?'],
  'synthetic_data': ['What are the symptoms of Focal inherited dermal hypoplasia?',
   'No symptoms : Hypoplasia follicular dermatome ( F1 ) is?',
   'Are Focal dermal hypoplasia inherited?',
   'What are the symptoms of Focal dermal hypoplasia?',
   'What is Focal dermal hypoplasia?',
   'Is facial hypoplasia ( dermal hypoplasia )?',
   'Is follicular dermal hypoplasia a follicular inflammatory syndrome?',
   'What are the symptoms of focal hypoplasia of the dermis ( FIP )?',
   'Skin : Dermatospongiosis of the fossa is a symptom of FAP (Fossa Inherited Defect)?',
   'What are the symptoms of Focal dermal hypoplasia?']},
 {'focus_area': 'Focal dermal hypoplasia',
  'column': 'answer',
  'metrics': {'max_bert_scores': [0.5887036919593811,
    0.6211448311805725,
    0.630905032157898,
    0.6447768211364746,
    0.527679443359375,
    0.5945816040039062,
    0.6316239237785339,
    0.6076194643974304,
    0.5881009101867676,
    0.5856155753135681],
   'self_bleu': [0.3191799096593227,
    0.2757330657506523,
    0.3034333861445876,
    0.227371225473429,
    0.2385621534735658,
    0.2157027588419747,
    0.3058957666740728,
    0.3300997547667167,
    0.2603595754203612,
    0.22855473269625898]},
  'real_data': ['Focal dermal hypoplasia is a genetic disorder that primarily affects the skin, skeleton, eyes, and face. The skin abnormalities are present from birth and can include streaks of very thin skin (dermal hypoplasia), cutis aplasia, and telangiectases. They also may abnormalities in the nails, hands, and feet. Some of the eye findings present may include small eyes (microphthalmia), absent or severely underdeveloped eyes (anophthalmia), and problems with the tear ducts. People with focal dermal hypoplasia may also have distinctive facial features such as a pointed chin, small ears, notched nostrils, and a slight difference in the size and shape of the right and left sides of the face (facial asymmetry). Most individuals with this condition are female. Males usually have milder signs and symptoms than females. Although intelligence is typically unaffected, some individuals have intellectual disability. This condition is caused by mutations in the PORCN gene and is inherited in an X-linked dominant manner. Most cases of focal dermal hypoplasia in females result from new mutations in the PORCN gene and occur in people with no history of the disorder in their family. When focal dermal hypoplasia occurs in males, it always results from a new mutation in this gene that is not inherited. Treatment is based on the signs and symptoms present in the person; however, care usually involves a team of specialists, including dermatologists, otolaryngologist, physical/occupational therapists, and hand surgeons.',
   'What are the signs and symptoms of Focal dermal hypoplasia? Focal dermal hypoplasia is usually evident from birth and primarily affects the skin, skeleton, eyes, and face. The signs and symptoms of vary widely, although almost all affected individuals have skin abnormalities. Some of the skin findings include streaks of very thin skin (dermal hypoplasia), yellowish-pink nodules of fat under the skin, areas where the top layers of skin are absent (cutis aplasia), telangiectases, and streaks of slightly darker or lighter skin. These skin features can cause pain, itching, irritation, or lead to skin infections. With age, most develop wart-like growths, called papillomas, around the nostrils, lips, anus, and female genitalia. They may also be present in the throat, specifically in the esophagus or larynx, and can cause problems with swallowing, breathing, or sleeping. Other features include small, ridged fingernails and toenails as well as sparse, brittle or absent scalp hair. The skeleton is usually affected as well. Many individuals have hand and foot abnormalities, including missing fingers or toes (oligodactyly), webbed or fused fingers or toes (syndactyly), and a deep split in the hands or feet with missing fingers or toes and fusion of the remaining digits (ectrodactyly). X-rays can show streaks of altered bone density, called osteopathia striata, which usually do not cause symptoms.  Eye abnormalities are common and can include microphthalmia and anopthalmia as well as problems with the tear ducts. The retina or the optic nerve can also be incompletely developed, which can result in a gap or split in these structures (coloboma). Some of these eye abnormalities do not impair vision, while others can lead to low vision or blindness. People with focal dermal hypoplasia often have distinctive, but subtle facial features such as a pointed chin, small ears, notched nostrils, and a slight difference in the size and shape of the right and left sides of the face (facial asymmetry). Some individuals may have a cleft lip and/or palate. About half of those with focal dermal hypoplasia have teeth abnormalities of their teeth, especially of the enamel (the hard, white material that forms the protective outer layer of each tooth). Less commonly, kidney and gastrointestinal abnormalities are present. The kidneys may be fused together, which can lead to kidney infections. The main gastrointestinal abnormality that is seen is an omphalocele. The Human Phenotype Ontology provides the following list of signs and symptoms for Focal dermal hypoplasia. If the information is available, the table below includes how often the symptom is seen in people with this condition. You can use the MedlinePlus Medical Dictionary to look up the definitions for these medical terms. Signs and Symptoms Approximate number of patients (when available) Abnormality of dental enamel 90% Abnormality of dental morphology 90% Abnormality of epiphysis morphology 90% Abnormality of the nail 90% Camptodactyly of finger 90% Dermal atrophy 90% Finger syndactyly 90% Hand polydactyly 90% Hypermelanotic macule 90% Lower limb asymmetry 90% Low-set, posteriorly rotated ears 90% Reduced number of teeth 90% Rough bone trabeculation 90% Split foot 90% Split hand 90% Telangiectasia of the skin 90% Thin skin 90% Toe syndactyly 90% Verrucae 90% Abnormal localization of kidney 50% Abnormality of pelvic girdle bone morphology 50% Abnormality of the clavicle 50% Abnormality of the ribs 50% Alopecia 50% Aplasia/Hypoplasia of the iris 50% Choroideremia 50% Cognitive impairment 50% Dental malocclusion 50% Ectopia lentis 50% Facial asymmetry 50% Iris coloboma 50% Multicystic kidney dysplasia 50% Opacification of the corneal stroma 50% Scoliosis 50% Spina bifida 50% Strabismus 50% Abdominal pain 7.5% Abnormality of adipose tissue 7.5% Abnormality of the mediastinum 7.5% Abnormality of the pulmonary vasculature 7.5% Acute hepatic failure 7.5% Aplasia/Hypoplasia of the lungs 7.5% Congenital diaphragmatic hernia 7.5% Duodenal stenosis 7.5% Narrow nasal bridge 7.5% Neoplasm of the skeletal system 7.5% Omphalocele 7.5% Patent ductus arteriosus 7.5% Pointed chin 7.5% Renal hypoplasia/aplasia 7.5% Umbilical hernia 7.5% Ventricular septal defect 7.5% Abnormality of the larynx - Abnormality of the pinna - Absent fingernail - Absent toenail - Agenesis of corpus callosum - Aniridia - Anophthalmia - Anteriorly placed anus - Arnold-Chiari malformation - Bifid ureter - Brachydactyly syndrome - Brittle hair - Broad nasal tip - Chorioretinal coloboma - Cleft ala nasi - Cleft palate - Cleft upper lip - Clitoral hypoplasia - Congenital hip dislocation - Cryptorchidism - Delayed eruption of teeth - Diastasis recti - Foot polydactyly - Hiatus hernia - Horseshoe kidney - Hydrocephalus - Hydronephrosis - Hypodontia - Hypoplasia of dental enamel - Hypoplastic nipples - Inguinal hernia - Intellectual disability - Intestinal malrotation - Joint laxity - Labial hypoplasia - Linear hyperpigmentation - Low-set ears - Microcephaly - Microphthalmia - Midclavicular aplasia - Midclavicular hypoplasia - Mixed hearing impairment - Myelomeningocele - Nail dysplasia - Nystagmus - Oligodactyly (feet) - Oligodactyly (hands) - Oligodontia - Optic atrophy - Osteopathia striata - Patchy alopecia - Postaxial hand polydactyly - Reduced visual acuity - Reticular hyperpigmentation - Short finger - Short metacarpal - Short metatarsal - Short phalanx of finger - Short ribs - Short stature - Sparse hair - Spina bifida occulta - Stenosis of the external auditory canal - Supernumerary nipple - Telangiectasia - Ureteral duplication - Visual impairment - X-linked dominant inheritance - The Human Phenotype Ontology (HPO) has collected information on how often a sign or symptom occurs in a condition. Much of this information comes from Orphanet, a European rare disease database. The frequency of a sign or symptom is usually listed as a rough estimate of the percentage of patients who have that feature. The frequency may also be listed as a fraction. The first number of the fraction is how many people had the symptom, and the second number is the total number of people who were examined in one study. For example, a frequency of 25/25 means that in a study of 25 people all patients were found to have that symptom. Because these frequencies are based on a specific study, the fractions may be different if another group of patients are examined. Sometimes, no information on frequency is available. In these cases, the sign or symptom may be rare or common.',
   'How is this condition inherited? Focal dermal hypoplasia is caused by mutations in the PORCN gene and is inherited in an X-linked dominant manner. Many cases of focal dermal hypoplasia result from a new mutation and occur in people with no history of the disorder in their family For a woman affected with focal dermal hypoplasia, the theoretical risk of passing the mutation to each of her offspring is 50%; however, many males with this condition do not survive. In addition, there are cases in which a woman may have the focal dermal hypoplasia mutation in some but not all of her egg cells, a condition known as germline mosaicism. In this case the risk of passing along the mutation may be as high as 50% depending on the level of mosaicism. Males with focal dermal hypoplasia typically have the mutation in some but not all of their cells. The risk that a male with FDH will pass the condition on to his daughters may be as high as 100%; men do not pass this condition on to their sons. We recommend discussing specific concerns with a genetics professional, who can help you understand how this condition might be inherited in your family. Click on the following link for resources for finding a genetics professional.'],
  'synthetic_data': ['Focal hypodermia pharyngitis is usually inherited by a dominant gene. Signs and symptoms of this disorder may include skin lesions, eye lesions, and a loss of bone. The presence of a defect in the DENX gene is not known. The DENX gene is used to determine which genes are affected. How often does focal hypodermia pharyngitis affect individuals? This disorder is very rare, with a prevalence of less than 1% in males and less than 1% in females. For more information,',
   'Focal hypodermia plexiformis is mainly a genetic condition. It is usually caused by a mutation in a gene on the X chromosome. The affected individuals may have a reduced or absent chromosome set. Signs and symptoms of focal hypodermia plexiformis may include: The skin, eye, and nose are affected. The way a person inherits the disease is very variable. No signs and symptoms are present in all people with focal hypodermia plexiformis. Use the left navigation',
   'Focal dermal hypoplasia is inherited as a recessive disorder. This means that the condition usually affects females and males. The signs and symptoms of this condition include a small number of abnormalities of the skin, eyes, and phalanges (the phalanges are the first areas to appear). The presence of a particular gene, called the poronucleotide X-linked gene, can also cause focal dermal hypoplasia. The frequency of birth defects varies from person to person. For more information about how people with this',
   'Focal hypodermia is a genetic disorder marked by the presence of possible inherited defects in the phanoploidy gene found on chromosomes 1 and 2. This condition is usually inherited as a recessive trait. Females with focal hypodermia usually do not show any symptoms. This condition affects only about 1 in 30 people. Some people with focal hypodermia also have a range of other symptoms, including skin and eye problems, and a lack of normal facial features. The following can help to guide the diagnosis of this condition.',
   'Causes of focal hypodermia follicularis. The usual symptom of focal hypodermia follicularis is a genital abnormality that is present on the OPIN test. The genital abnormality is not affected by the chromosomes. The genital abnormality is usually a result of a change in the chromosomes. The genital abnormality can be seen on the OPIN test. The genital abnormality can be seen in both males and females. For more information, ',
   'Focal hypodermia pulmonis is a genetic deformity. The DEN gene is usually found by a mutation in the OPIN gene. The DEN gene is usually not affected by a mutation. The DEN gene may be affected by a number of factors, including chromosome abnormalities. Symptoms and signs of focal hypodermia pulmonis vary among individuals. For example, the skin and hair may be affected most often in males and females. The incidence of new cases of focal hypodermia pulmonis',
   'Focal hypodermia follicularis is a degenerative disorder that is usually inherited by a dominant genetic approach. The following are some possible signs and symptoms of this condition: The presence of a mutated gene for the XP gene is shown in the figure below. The mutated gene is not found in humans. Focal hypodermia follicularis usually affects the eyes, lips, and skin. It can also affect the hair, nails, and gums. Females with this condition have a very low incidence of the disorder.',
   'Focal hypodermia dermatosis is inherited from a dominant genetic background. This means that the affected person will inherit a specific set of genes. The occurrence of these genes is usually listed as XXX. Some people with focal hypodermia dermatosis may have no signs or symptoms until the condition is severe. Symptoms include abnormalities of the skin, nails, and eyelids. The condition most often affects females, but males may also be affected. The incidence of these symptoms varies from about 1% to 30%. For',
   'Focal hypodermatosis and dermatosis is a genetic phenotype. The following links show how the condition is inherited. The first signs and symptoms of focal hypodermatosis and dermatosis are usually seen when the affected individual inherits the FNP gene. The skin, bones, and lungs may also be affected. The majority of affected individuals have no symptoms. The condition can occur in both males and females, and it can occur in both sexes. Approximately 1% of affected individuals have no symptoms.',
   'Symptoms and signs include: Formosan hypoplasia is usually caused by a defect in the DERP gene, which is a genetic trait. This defect affects the skin, hair, and nails. Formosan hypoplasia is usually inherited as a recessive condition. When this condition occurs, individuals with this condition may be X-linked (no more than 99%) and the other individuals may be X-linked (no more than 99%). When this condition occurs, individuals with this condition may be X-linked.']}]

In [ ]:
results

[{'focus_area': 'Pseudopelade of Brocq',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.8517076969146729,
    0.8646624088287354,
    0.5227058529853821,
    0.8417725563049316,
    0.877738893032074,
    0.5812272429466248,
    0.553707480430603,
    0.7167820930480957,
    0.8080316781997681,
    0.4613971710205078],
   'self_bleu': [0.6434588841607617,
    0.8408964152537146,
    0.0,
    0.5946035575013605,
    0.7952707287670506,
    0.0,
    0.0,
    0.5348259312838877,
    0.5019724248795793,
    0.6434588841607617]},
  'real_data': ['What is (are) Pseudopelade of Brocq ?',
   'What are the symptoms of Pseudopelade of Brocq ?',
   'What are the treatments for Pseudopelade of Brocq ?'],
  'synthetic_data': ['What are the symptoms of Pseudo-Brodacque?',
   'What are the symptoms of Pseudo-Brodaek?',
   'What is a P  Broderick? (P  Broderick )??????????????????????????????????????????????? Symptoms of p  Broderick ',
   'What are the treatments of Pseudo-Brodaque?',
  

In [ ]:
# Run comparison with straight LLM generation

In [ ]:
from openai import OpenAI

client = OpenAI()

prompt = "Generate 10 more examples based on the given data. Ensure diversity in the generated examples. Return a JSON object with key 'examples' and its value should be a list of the generated examples as strings."

In [ ]:
import json

# Initialize storage for results
llm_results = []

for focus_area in sampled_focus_areas:
    sub_df = filtered_df[filtered_df['focus_area'] == focus_area]

    # Generate 10 synthetic examples for 'question' and 'answer'
    for column in ['question', 'answer']:
        print(f"Generating synthetic data ({focus_area} + {column})")
        real_data = sub_df[column].tolist()
        #llm_synthetic_data = sample_synthetic_data_cone(real_data, corrector, 10, num_steps=20, height_factor=2.0, angle_factor=1.15, min_height=0.3, distribution='normal')
        completion = client.chat.completions.create(
            messages=[
                {
                    "role": "user",
                    "content": prompt,
                },
                {"role": "user",
                "content": "\n".join(real_data)}
            ],
            model="gpt-3.5-turbo-1106",
            response_format={"type": "json_object"},
        )

        llm_synthetic_data = json.loads(completion.choices[0].message.content)['examples']


        # Score synthetic examples using BERTScore and Self-BLEU
        print(f"Calculating metrics ({focus_area} + {column})")
        metrics = calculate_metrics(llm_synthetic_data, real_data, bert_score, bleu)

        # Store results
        llm_results.append({
            'focus_area': focus_area,
            'column': column,
            'metrics': metrics,
            'real_data': real_data,
            'synthetic_data': llm_synthetic_data
        })

Generating synthetic data (Fibromuscular Dysplasia + question)
Calculating metrics (Fibromuscular Dysplasia + question)
Generating synthetic data (Fibromuscular Dysplasia + answer)
Calculating metrics (Fibromuscular Dysplasia + answer)
Generating synthetic data (Craniometaphyseal dysplasia, autosomal recessive type + question)
Calculating metrics (Craniometaphyseal dysplasia, autosomal recessive type + question)
Generating synthetic data (Craniometaphyseal dysplasia, autosomal recessive type + answer)
Calculating metrics (Craniometaphyseal dysplasia, autosomal recessive type + answer)
Generating synthetic data (LAMA2-related muscular dystrophy + question)
Calculating metrics (LAMA2-related muscular dystrophy + question)
Generating synthetic data (LAMA2-related muscular dystrophy + answer)
Calculating metrics (LAMA2-related muscular dystrophy + answer)
Generating synthetic data (GRACILE syndrome + question)
Calculating metrics (GRACILE syndrome + question)
Generating synthetic data (GRA

In [ ]:
llm_results

[{'focus_area': 'Fibromuscular Dysplasia',
  'column': 'question',
  'metrics': {'max_bert_scores': [0.9223172664642334,
    0.841181755065918,
    0.8259348273277283,
    0.8508749008178711,
    0.817637026309967,
    0.8903335332870483,
    0.8604024648666382,
    0.8987301588058472,
    0.8512603044509888,
    0.7890917062759399],
   'self_bleu': [0.5,
    0.0,
    0.0,
    0.0,
    0.0,
    0.3303164318013807,
    0.0,
    0.43167001068522526,
    0.31239399369202553,
    0.0]},
  'real_data': ['What is (are) Fibromuscular Dysplasia ?',
   'What are the treatments for Fibromuscular Dysplasia ?',
   'What is the outlook for Fibromuscular Dysplasia ?',
   'what research (or clinical trials) is being done for Fibromuscular Dysplasia ?'],
  'synthetic_data': ['What are the symptoms of Fibromuscular Dysplasia?',
   'Are there any risk factors for developing Fibromuscular Dysplasia?',
   'Can Fibromuscular Dysplasia be inherited?',
   'What imaging tests are used to diagnose Fibromuscula

In [ ]:
def average_max_bert_scores(results):
    """Calculate the average of the maximum BERT scores."""
    all_max_scores = [max(item['metrics']['max_bert_scores']) for item in results]
    return sum(all_max_scores) / len(all_max_scores)

def average_self_bleu(results):
    """Calculate the average Self-BLEU score."""
    all_self_bleu = [sum(item['metrics']['self_bleu']) / len(item['metrics']['self_bleu']) for item in results]
    return sum(all_self_bleu) / len(all_self_bleu)

def length_consistency(results):
    """Calculate the average difference in length between synthetic and real data."""
    length_diffs = []
    for item in results:
        real_lengths = [len(text.split()) for text in item['real_data']]
        synthetic_lengths = [len(text.split()) for text in item['synthetic_data']]
        diff = sum(abs(rl - sl) for rl, sl in zip(real_lengths, synthetic_lengths)) / len(real_lengths)
        length_diffs.append(diff)
    return sum(length_diffs) / len(length_diffs)

In [ ]:
results_method1 = results
results_method2 = llm_results

# For Method 1
avg_max_bert_1 = average_max_bert_scores(results_method1)
avg_self_bleu_1 = average_self_bleu(results_method1)
length_consistency_1 = length_consistency(results_method1)

# For Method 2
avg_max_bert_2 = average_max_bert_scores(results_method2)
avg_self_bleu_2 = average_self_bleu(results_method2)
length_consistency_2 = length_consistency(results_method2)

# Print Comparisons
print("Comparison of Methods based on Text Generation:")
print(f"Average Max BERT Scores:\nMethod 1: {avg_max_bert_1}\nMethod 2: {avg_max_bert_2}\n")
print(f"Average Self-BLEU Scores (Lower is better):\nMethod 1: {avg_self_bleu_1}\nMethod 2: {avg_self_bleu_2}\n")
print(f"Average Length Consistency (Closer to real data is better):\nMethod 1: {length_consistency_1}\nMethod 2: {length_consistency_2}\n")

Comparison of Methods based on Text Generation:
Average Max BERT Scores:
Method 1: 0.7710246026515961
Method 2: 0.8462130427360535

Average Self-BLEU Scores (Lower is better):
Method 1: 0.20658147858821946
Method 2: 0.2081610607157296

Average Length Consistency (Closer to real data is better):
Method 1: 47.54642857142857
Method 2: 62.403571428571425



In [ ]:
import plotly.graph_objs as go
from scipy import stats
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

# Assuming 'results' and 'llm_results' are your two lists of dictionaries.

def calculate_average_bert_scores(data):
    """Calculate the average BERT scores for each entry."""
    return [np.mean(entry['metrics']['max_bert_scores']) for entry in data]

def calculate_self_bleu(data):
    """Calculate the average self-BLEU scores for each entry."""
    return [np.mean(entry['metrics']['self_bleu']) for entry in data]

def content_diversity_analysis(data):
    """Calculate diversity based on cosine similarity of TF-IDF vectors."""
    vectorizer = CountVectorizer().fit_transform([' '.join(entry['synthetic_data']) for entry in data])
    vectors = vectorizer.toarray()
    return [cosine_similarity([vectors[i]], vectors).mean() for i in range(len(vectors))]

def plot_data(d1, d2, title):
    """Create a plot comparing two datasets."""
    trace1 = go.Box(y=d1, name='Results')
    trace2 = go.Box(y=d2, name='LLM Results')
    layout = go.Layout(title=title, yaxis=dict(title='Score'))
    fig = go.Figure(data=[trace1, trace2], layout=layout)
    fig.show()

# Calculate metrics
average_bert_scores_results = calculate_average_bert_scores(results)
average_bert_scores_llm = calculate_average_bert_scores(llm_results)

self_bleu_results = calculate_self_bleu(results)
self_bleu_llm = calculate_self_bleu(llm_results)

diversity_results = content_diversity_analysis(results)
diversity_llm = content_diversity_analysis(llm_results)

# Plotting the results
plot_data(average_bert_scores_results, average_bert_scores_llm, 'Average BERT Scores Comparison')
plot_data(self_bleu_results, self_bleu_llm, 'Self-BLEU Scores Comparison')
plot_data(diversity_results, diversity_llm, 'Content Diversity Comparison')

# Statistical Analysis
print("BERT Score t-test:", stats.ttest_ind(average_bert_scores_results, average_bert_scores_llm))
print("Self-BLEU Score t-test:", stats.ttest_ind(self_bleu_results, self_bleu_llm))
print("Diversity t-test:", stats.ttest_ind(diversity_results, diversity_llm))

BERT Score t-test: TtestResult(statistic=-1.2025564708281218, pvalue=0.24472890990118473, df=18.0)
Self-BLEU Score t-test: TtestResult(statistic=-0.018298213133836606, pvalue=0.9856022580357583, df=18.0)
Diversity t-test: TtestResult(statistic=2.388127899117385, pvalue=0.028102856328865403, df=18.0)


In [ ]:
import plotly.graph_objs as go
import numpy as np
import statsmodels.api as sm

def extract_individual_lengths_scores(data):
    """Extract individual lengths, self-BLEU scores, and BERT scores for all entries and all focus areas."""
    individual_lengths = []
    individual_bleu_scores = []
    individual_bert_scores = []
    for entry in data:
        for synthetic in entry['synthetic_data']:
            individual_lengths.append(len(synthetic.split()))
        for score in entry['metrics']['self_bleu']:
            individual_bleu_scores.append(score)
        for score in entry['metrics']['max_bert_scores']:
            individual_bert_scores.append(score)
    return individual_lengths, individual_bleu_scores, individual_bert_scores

def plot_with_trendline(x, y, title, xaxis_title, yaxis_title):
    """Create a scatter plot with a LOWESS trendline to visualize detailed relationships."""
    # Scatter plot for individual data points
    scatter = go.Scatter(x=x, y=y, mode='markers', marker=dict(size=5), name='Individual Data')

    # LOWESS trendline for granular trends
    lowess = sm.nonparametric.lowess(y, x, frac=0.5)
    trendline = go.Scatter(x=lowess[:, 0], y=lowess[:, 1], mode='lines', name='LOWESS Trend', line=dict(color='red'))

    # Layout settings
    layout = go.Layout(title=title, xaxis=dict(title=xaxis_title), yaxis=dict(title=yaxis_title))

    # Create and show the figure
    fig = go.Figure(data=[scatter, trendline], layout=layout)
    fig.show()

# Extracting individual lengths, self-BLEU scores, and BERT scores
lengths_results, bleu_scores_results, bert_scores_results = extract_individual_lengths_scores(results)
lengths_llm, bleu_scores_llm, bert_scores_llm = extract_individual_lengths_scores(llm_results)

# Plotting Length vs. Self-BLEU for Results and LLM Results
plot_with_trendline(lengths_results, bleu_scores_results, 'Synthetic Length vs. Self-BLEU for Results', 'Text Length (words)', 'Self-BLEU Score')
plot_with_trendline(lengths_llm, bleu_scores_llm, 'Synthetic Length vs. Self-BLEU for LLM Results', 'Text Length (words)', 'Self-BLEU Score')

# Plotting Length vs. BERT Scores for Results and LLM Results
plot_with_trendline(lengths_results, bert_scores_results, 'Synthetic Length vs. BERT Score for Results', 'Text Length (words)', 'BERT Score')
plot_with_trendline(lengths_llm, bert_scores_llm, 'Synthetic Length vs. BERT Score for LLM Results', 'Text Length (words)', 'BERT Score')

In [ ]:
plot_focus_area_results(llm_results)

In [ ]:
import plotly.graph_objects as go
import numpy as np

# Let's create some dummy embeddings in 3D space
embeddings = np.array([[1, 2, 3], [4, 5, 6], [7, 8, 2], [2, 1, 5]])
labels = ['Text Chunk 3', 'Text Chunk 2', 'Text Chunk 4', 'Text Chunk 5']

# Now, we'll create vectors to represent the directions from the origin
directions = embeddings - np.array([0, 0, 0])

# Creating the figure
fig = go.Figure()

# Adding the points to the plot
fig.add_trace(go.Scatter3d(x=embeddings[:, 0], y=embeddings[:, 1], z=embeddings[:, 2],
                           mode='markers+text', text=labels, textposition='top center',
                           marker=dict(size=5, color='blue'), name='Embeddings as Points'))

# Adding the lines to represent the directions
for i, direction in enumerate(directions):
    fig.add_trace(go.Scatter3d(x=[0, direction[0]], y=[0, direction[1]], z=[0, direction[2]],
                               mode='lines', line=dict(color='red', width=2),
                               name=f'Direction of {labels[i]}'))

# Enhancing layout
fig.update_layout(title='Visualizing Embeddings as Points and Directions',
                  scene=dict(xaxis_title='X',
                             yaxis_title='Y',
                             zaxis_title='Z',
                             camera=dict(eye=dict(x=1.5, y=-1.25, z=.5))),
                  showlegend=True,)

fig.show()


In [ ]:
import plotly.graph_objects as go
import numpy as np

# Let's create some dummy embeddings in 3D space
embeddings = np.array([[1, 2, 3], [4, 5, 6], [7, 8, 2], [2, 1, 5]])
labels = ['Text Chunk 3', 'Text Chunk 2', 'Text Chunk 4', 'Text Chunk 5']

# Anisotropic scaling factors for each axis (to simulate the "shape" of the space)
scaling_factors = np.array([1, 1.5, 0.5])

# Applying the anisotropic scaling to the embeddings and directions
aniso_embeddings = embeddings * scaling_factors
aniso_directions = aniso_embeddings - np.array([0, 0, 0])

# Creating the figure
fig = go.Figure()

# Adding the points to the plot with anisotropic scaling
fig.add_trace(go.Scatter3d(x=aniso_embeddings[:, 0], y=aniso_embeddings[:, 1], z=aniso_embeddings[:, 2],
                           mode='markers+text', text=labels, textposition='top center',
                           marker=dict(size=5, color='blue'), name='Anisotropic Embeddings as Points'))

# Adding the lines to represent the directions with anisotropic scaling
for i, direction in enumerate(aniso_directions):
    fig.add_trace(go.Scatter3d(x=[0, direction[0]], y=[0, direction[1]], z=[0, direction[2]],
                               mode='lines', line=dict(color='red', width=2),
                               name=f'Direction of {labels[i]}'))

# Enhancing layout
fig.update_layout(title='Visualizing Embeddings in Anisotropic Space',
                  scene=dict(xaxis_title='X (scaled)',
                             yaxis_title='Y (scaled)',
                             zaxis_title='Z (scaled)',
                             camera=dict(eye=dict(x=1.5, y=-1.25, z=0.5))),
                  showlegend=True)

fig.show()

In [ ]:
import plotly.graph_objects as go
import numpy as np

# Define the center point
center_point = np.array([0, 0, 0])
center_label = "Text Chunk 1"

# Define a point on the surface of the sphere
# Assuming a unit sphere for simplicity, a point on the surface can be (1, 0, 0) or any point with a norm of 1
sphere_point = np.array([1, 0, 0])  # This point is on the sphere surface
sphere_label = "Possibly similar text"

# Creating the figure
fig = go.Figure()

# Adding the center point
fig.add_trace(go.Scatter3d(x=[center_point[0]], y=[center_point[1]], z=[center_point[2]],
                           mode='markers+text', text=[center_label], textposition='bottom center',
                           marker=dict(size=5, color='blue'), name='Center Point'))

# Adding the point on the sphere
fig.add_trace(go.Scatter3d(x=[sphere_point[0]], y=[sphere_point[1]], z=[sphere_point[2]],
                           mode='markers+text', text=[sphere_label], textposition='bottom center',
                           marker=dict(size=5, color='red'), name='Sphere Point'))

# Adding a sphere for visualization
# Create a sphere centered at the origin
u, v = np.mgrid[0:2*np.pi:20j, 0:np.pi:10j]
x = np.cos(u)*np.sin(v)
y = np.sin(u)*np.sin(v)
z = np.cos(v)
fig.add_trace(go.Surface(x=x, y=y, z=z, opacity=0.3, colorscale='Blues'))

# Enhancing layout
fig.update_layout(title='Center Point with Surrounding Sphere',
                  scene=dict(xaxis_title='X',
                             yaxis_title='Y',
                             zaxis_title='Z',
                             aspectmode='cube'),  # Ensure the sphere is not distorted
                  showlegend=True)

fig.show()


In [ ]:
import plotly.graph_objects as go
import numpy as np

# Define the center point
center_point = np.array([0, 0, 0])
center_label = "Text Chunk 1"

# Define a point on the surface of the sphere for "Possibly similar text"
sphere_surface_point = np.array([1, 0, 0])  # On the unit sphere surface
sphere_surface_label = "Possibly similar text"

# Define a point inside the sphere for "Actually similar text"
inside_sphere_point = np.array([0.25, 0.25, 0])  # Inside the unit sphere
inside_sphere_label = "Actually similar text"

# Anisotropic scaling factors for each axis
scaling_factors = np.array([1, 2, 0.5])

# Apply anisotropic scaling to the points
aniso_center_point = center_point * scaling_factors
aniso_sphere_surface_point = sphere_surface_point * scaling_factors
aniso_inside_sphere_point = inside_sphere_point * scaling_factors

# Creating the figure
fig = go.Figure()

# Adding the center point
fig.add_trace(go.Scatter3d(x=[aniso_center_point[0]], y=[aniso_center_point[1]], z=[aniso_center_point[2]],
                           mode='markers+text', text=[center_label], textposition='bottom center',
                           marker=dict(size=5, color='blue'), name='Center Point'))

# Adding the point on the sphere surface
fig.add_trace(go.Scatter3d(x=[aniso_sphere_surface_point[0]], y=[aniso_sphere_surface_point[1]], z=[aniso_sphere_surface_point[2]],
                           mode='markers+text', text=[sphere_surface_label], textposition='bottom center',
                           marker=dict(size=5, color='red'), name='Sphere Surface Point'))

# Adding the point inside the sphere
fig.add_trace(go.Scatter3d(x=[aniso_inside_sphere_point[0]], y=[aniso_inside_sphere_point[1]], z=[aniso_inside_sphere_point[2]],
                           mode='markers+text', text=[inside_sphere_label], textposition='bottom center',
                           marker=dict(size=5, color='green'), name='Inside Sphere Point'))

# Adding an ellipsoid for visualization of anisotropic space
# Create a grid for the ellipsoid
u, v = np.mgrid[0:2*np.pi:20j, 0:np.pi:10j]
x = np.cos(u)*np.sin(v)
y = 2*np.sin(u)*np.sin(v)  # Scale y by 2
z = 0.5*np.cos(v)  # Scale z by 0.5

fig.add_trace(go.Surface(x=x, y=y, z=z, opacity=0.3, colorscale='Blues', name='Anisotropic Space'))

# Enhancing layout
fig.update_layout(title='Points in Anisotropic Space',
                  scene=dict(xaxis_title='X',
                             yaxis_title='Y',
                             zaxis_title='Z',
                             aspectmode='manual',  # Allow for custom aspect ratio
                             aspectratio=dict(x=1, y=2, z=0.5)),  # Reflect the anisotropic scaling
                  showlegend=True)

fig.show()


In [ ]:
import plotly.graph_objects as go
import numpy as np

# Define the centroid on the Z axis, where the two cone bases join
centroid = np.array([0, 0, 0])
centroid_label = "Text Chunk 1"

# Create a double cone (two cones joined at their bases) along the Z-axis
theta = np.linspace(0, 2 * np.pi, 30)
r = np.linspace(0, 1, 30)  # radius values
T, R = np.meshgrid(theta, r)
X = R * np.cos(T)
Y = R * np.sin(T)
Z1 = centroid[2] - R  # Lower cone (bases joined at the centroid)
Z2 = centroid[2] + R  # Upper cone (bases joined at the centroid, extending upwards)

# Define several points inside the double cone
# Randomly distributed around the centroid within the cone
points_inside = np.array([
    [np.random.uniform(-0.5, 0.5), np.random.uniform(-0.5, 0.5), np.random.uniform(-1, 1)]
    for _ in range(10)
])
inside_labels = ["Inside Point"] * len(points_inside)

# Creating the figure
fig = go.Figure()

# Add the centroid to the figure
fig.add_trace(go.Scatter3d(x=[centroid[0]], y=[centroid[1]], z=[centroid[2]],
                           mode='markers+text', text=[centroid_label],
                           marker=dict(size=5, color='blue'), name='Centroid'))

# Add the points inside the double cone
fig.add_trace(go.Scatter3d(x=points_inside[:, 0], y=points_inside[:, 1], z=points_inside[:, 2],
                           mode='markers+text', text=inside_labels,
                           marker=dict(size=3, color='red', opacity=0.5), name='Points Inside'))

# Add the double cone to the figure
fig.add_trace(go.Surface(x=X, y=Y, z=Z1, opacity=0.5, showscale=False, name='Lower Cone'))
fig.add_trace(go.Surface(x=X, y=Y, z=Z2, opacity=0.5, showscale=False, name='Upper Cone'))

# Update the layout
fig.update_layout(title='Double Cone with Points in Anisotropic Space',
                  scene=dict(xaxis_title='X', yaxis_title='Y', zaxis_title='Z',
                             aspectratio=dict(x=1, y=1, z=1)),  # Custom aspect ratio for better visualization
                  showlegend=True)

fig.show()
